In [2]:
import pandas as pd
import numpy as np

from sklearn.externals import joblib
import matplotlib.pyplot as plt
import lightgbm as lgb

from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn import svm
from sklearn.linear_model import SGDClassifier
from sklearn.svm import LinearSVC

from sklearn.metrics import f1_score,recall_score
from sklearn.metrics import accuracy_score
from sklearn.metrics import roc_auc_score
from sklearn.utils import shuffle
from sklearn.model_selection import  train_test_split

from sklearn.externals import joblib

import numpy as np
import seaborn as sns
import pickle

In [3]:
DROP_COL = ['chrom-Enh','chromStart','chromEnd','TSS','label','id']

# Split Train Test

In [4]:
def merge_seq_protein(sequence, protein):
    sequence = sequence.rename(columns={'0':'chrom-Enh',
                                        '1':'chromStart',
                                        '2':'chromEnd',
                                        '3':'TSS',
                                        '4':'label',
                                        '5':'id'})
    
    sequence = sequence.drop(['chrom-Enh','chromStart','chromEnd','TSS','label'],axis=1)
    
    print('sequence shape {}, protein shape {}'.format(sequence.shape,protein.shape))
    #sequence[keys] = sequence[keys].astype(str)
    #protein[keys] = protein[keys].astype(str)
    
    merged = protein.merge(sequence, on='id', how='left')
    
    print('merged shape {}'.format(merged.shape))
    return merged

def generate_lgb_use_data(X_train,y_train,X_test,y_test):
    train_x = X_train[:int(0.9*X_train.shape[0])]
    train_y = y_train[:int(0.9*X_train.shape[0])]
    
    valid_x = X_train[int(0.9*X_train.shape[0]):]
    valid_y = y_train[int(0.9*X_train.shape[0]):]
    
    lgb_train = lgb.Dataset(data=train_x,label=train_y)
    lgb_valid = lgb.Dataset(data=valid_x,label=valid_y)
    lgb_test = lgb.Dataset(data=X_test,label=y_test)
    
    return lgb_train,lgb_valid,lgb_test


def pre_split(protein_train_path,seq_path):
    protein = pd.read_csv(protein_train_path)
    seq = pd.read_csv(seq_path)
    
    merged = merge_seq_protein(sequence=seq,protein=protein)
    
    #merge_cols = merged.columns.tolist()
    #merged = merged.values
    
    #np.random.seed(111)
    #np.random.shuffle(merged)
    
    #merged = pd.DataFrame(merged,columns=merge_cols)
    
    merged = shuffle(merged)
    
    y = merged['label']
    X = merged.drop(DROP_COL,axis=1)
    
    X = X.fillna(method='pad')
    X = X.fillna(0)
    
    X = X.astype(float)
    y = y.astype(float)
    
    
    X_train_all, X_test_all, y_train_all,y_test_all = train_test_split(X, 
                                                        y, 
                                                        test_size=0.2, 
                                                        random_state=42,
                                                        shuffle=False)
    
    
    protein_part = protein.shape[1]-6
    
    X_train_protein = X_train_all.iloc[:,0:protein_part]
    y_train_protein = y_train_all
    X_test_protein = X_test_all.iloc[:,0:protein_part]
    y_test_protein = y_test_all
    
    X_train_seq = X_train_all.iloc[:,protein_part:]
    y_train_seq = y_train_all
    
    X_test_seq = X_test_all.iloc[:,protein_part:]
    y_test_seq = y_test_all
    
    return {'X_train_protein':X_train_protein,
           'y_train_protein':y_train_protein,
            
           'X_test_protein':X_test_protein,
           'y_test_protein':y_test_protein,
            
           'X_train_seq':X_train_seq,
           'y_train_seq':y_train_seq,
            
           'X_test_seq':X_test_seq,
           'y_test_seq':y_test_seq,
            
           'X_train_all':X_train_all,
           'y_train_all':y_train_all,
           
            'X_test_all':X_test_all,
           'y_test_all':y_test_all}

In [144]:
nhek_original_data_json = pre_split(protein_train_path='../../data/NHEK/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_NHEK.csv')

sequence shape (2582, 321), protein shape (2582, 754)
merged shape (2582, 1074)


In [151]:
k562_original_data_json = pre_split(protein_train_path='../../data/k562/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_K562.csv')

sequence shape (3954, 321), protein shape (3954, 8498)
merged shape (3954, 8818)


In [155]:
imr90_original_data_json = pre_split(protein_train_path='../../data/IMR90/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_imr90.csv')

sequence shape (2508, 321), protein shape (2508, 2382)
merged shape (2508, 2702)


In [160]:
gm12878_original_data_json = pre_split(protein_train_path='../../data/GM12878/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_GM12878.csv')

sequence shape (4226, 321), protein shape (4226, 7486)
merged shape (4226, 7806)


In [164]:
huvec_original_data_json = pre_split(protein_train_path='../../data/HUVEC/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_HUVEC.csv')

sequence shape (3048, 321), protein shape (3048, 930)
merged shape (3048, 1250)


In [171]:
helas3_original_data_json = pre_split(protein_train_path='../../data/Hela-S3/muti-midfile/train.csv',
                                   seq_path='../../data/EP-lower/low_seq_feature_Hela-S3.csv')

sequence shape (3480, 321), protein shape (3480, 5902)
merged shape (3480, 6222)


# Define Models

## RandomForest

In [5]:
def random_forest(train_X,train_y,valid_X,valid_y):
    rf = RandomForestClassifier(n_jobs=-1,n_estimators=800).fit(train_X,train_y)
    # for valid, it is not necessary here, rf have its benefits
    return rf

## GBDT

In [6]:
def gbdt(train_X,train_y,valid_X,valid_y):
    gbdt = GradientBoostingClassifier(n_estimators=600).fit(train_X,train_y)
    return gbdt

## AdaBoost

In [7]:
def adaboost(train_X,train_y,valid_X,valid_y):
    adaboost = AdaBoostClassifier(n_estimators=600).fit(train_X,train_y)
    return adaboost

## SGD

In [8]:
def sgd(train_X,train_y,valid_X,valid_y):
    clf = SGDClassifier(loss="hinge", penalty="l2", max_iter=1000).fit(train_X,train_y,valid_X)
    return clf

## SVM

In [9]:
def svm(train_X,train_y,valid_X,valid_y):
    clf = LinearSVC(random_state=0, tol=1e-5)
    clf = clf.fit(train_X,train_y)
    return clf

## LightGBM

In [10]:
def prob2label(pred):
    pred_label = []
    for item in pred:
        if item >= 0.5:
            pred_label.append(1)
        else:
            pred_label.append(0)
    return pred_label

In [11]:
def lgb_f1_score(y_hat, data):
    y_true = data.get_label()
    y_hat = np.round(y_hat) # scikits f1 doesn't like probabilities
    return 'f1', f1_score(y_true, y_hat), True

In [12]:
def train_lgb(train_data,val_data,lgb_param,num_round,early_stop,nfold,is_cv=True):
    evals_result = {}
    if is_cv:
        lgb_model = lgb.cv(params=lgb_param, 
                      train_set = train_data, 
                       num_boost_round = num_round,
                      feval=lgb_f1_score, 
                      early_stopping_rounds=early_stop,
                       nfold=nfold,
                       verbose_eval=True
                      )
    if not is_cv:
        lgb_model = lgb.train(params=lgb_param, 
                              train_set = train_data, 
                              valid_sets=[val_data, train_data], 
                              valid_names=['val', 'train'],
                              num_boost_round = num_round,
                              feval=lgb_f1_score, 
                              #early_stopping_rounds=early_stop,
                              verbose_eval=True)
    
    return lgb_model


In [28]:
lgb_param = {
    'num_leaves':31, 
    'objective':'binary',
    'max_depth':None,
    'min_data_in_leaf':1,
    'learning_rate':0.03,
    'max_bin':None,
    'bagging_fraction':0.8,
    'tree_learner_type':'voting',
    'boosting_type':'gbdt',
    'metric':['binary_logloss']}
num_round = 3000
early_stop = 20
nfold = 10

# Only Use Protein

## LGB

### Train LGB on K562

In [152]:
k562X_train = k562_original_data_json['X_train_protein']
k562y_train = k562_original_data_json['y_train_protein']
k562X_test = k562_original_data_json['X_test_protein']
k562y_test = k562_original_data_json['y_test_protein']


k562_lgb_train_protein,k562_lgb_valid_protein,k562_lgb_test_protein = generate_lgb_use_data(k562X_train,
                                                                                            k562y_train,
                                                                                            k562X_test,
                                                                                            k562y_test)

In [153]:
k562_lgb_protein = train_lgb(k562_lgb_train_protein,k562_lgb_valid_protein,
                             lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.681251	train's f1: 0.803841	val's binary_logloss: 0.684801	val's f1: 0.719298
[2]	train's binary_logloss: 0.670013	train's f1: 0.814384	val's binary_logloss: 0.676815	val's f1: 0.727811
[3]	train's binary_logloss: 0.659318	train's f1: 0.814408	val's binary_logloss: 0.668214	val's f1: 0.723529
[4]	train's binary_logloss: 0.648503	train's f1: 0.82087	val's binary_logloss: 0.660942	val's f1: 0.736527
[5]	train's binary_logloss: 0.638122	train's f1: 0.827247	val's binary_logloss: 0.6521	val's f1: 0.74772
[6]	train's binary_logloss: 0.627849	train's f1: 0.835157	val's binary_logloss: 0.644688	val's f1: 0.75841
[7]	train's binary_logloss: 0.618291	train's f1: 0.845302	val's binary_logloss: 0.63788	val's f1: 0.755418
[8]	train's binary_logloss: 0.608597	train's f1: 0.853448	val's binary_logloss: 0.631218	val's f1: 0.770186
[9]	train's binary_logloss: 0.598964	train's f1: 0.857967	val's binary_logloss: 0.625074	val's f1: 0.763975
[10]	train's binary_logloss: 0.589

[77]	train's binary_logloss: 0.26092	train's f1: 0.985846	val's binary_logloss: 0.418609	val's f1: 0.831804
[78]	train's binary_logloss: 0.258385	train's f1: 0.98694	val's binary_logloss: 0.417502	val's f1: 0.831804
[79]	train's binary_logloss: 0.255642	train's f1: 0.986912	val's binary_logloss: 0.415323	val's f1: 0.831804
[80]	train's binary_logloss: 0.252855	train's f1: 0.987628	val's binary_logloss: 0.413464	val's f1: 0.840491
[81]	train's binary_logloss: 0.250115	train's f1: 0.987986	val's binary_logloss: 0.411416	val's f1: 0.83792
[82]	train's binary_logloss: 0.247531	train's f1: 0.988343	val's binary_logloss: 0.409398	val's f1: 0.840491
[83]	train's binary_logloss: 0.244863	train's f1: 0.989407	val's binary_logloss: 0.407686	val's f1: 0.844037
[84]	train's binary_logloss: 0.242358	train's f1: 0.989407	val's binary_logloss: 0.40578	val's f1: 0.844985
[85]	train's binary_logloss: 0.239835	train's f1: 0.98905	val's binary_logloss: 0.404341	val's f1: 0.847561
[86]	train's binary_logl

[155]	train's binary_logloss: 0.123744	train's f1: 1	val's binary_logloss: 0.337257	val's f1: 0.868502
[156]	train's binary_logloss: 0.122553	train's f1: 1	val's binary_logloss: 0.33587	val's f1: 0.865854
[157]	train's binary_logloss: 0.121429	train's f1: 1	val's binary_logloss: 0.335085	val's f1: 0.871951
[158]	train's binary_logloss: 0.120335	train's f1: 1	val's binary_logloss: 0.333573	val's f1: 0.871951
[159]	train's binary_logloss: 0.119259	train's f1: 1	val's binary_logloss: 0.333249	val's f1: 0.871951
[160]	train's binary_logloss: 0.118161	train's f1: 1	val's binary_logloss: 0.332676	val's f1: 0.871951
[161]	train's binary_logloss: 0.117129	train's f1: 1	val's binary_logloss: 0.332374	val's f1: 0.868502
[162]	train's binary_logloss: 0.115995	train's f1: 1	val's binary_logloss: 0.331218	val's f1: 0.868502
[163]	train's binary_logloss: 0.114879	train's f1: 1	val's binary_logloss: 0.330134	val's f1: 0.871951
[164]	train's binary_logloss: 0.113877	train's f1: 1	val's binary_logloss:

[235]	train's binary_logloss: 0.0613926	train's f1: 1	val's binary_logloss: 0.300246	val's f1: 0.87538
[236]	train's binary_logloss: 0.0608801	train's f1: 1	val's binary_logloss: 0.300045	val's f1: 0.871951
[237]	train's binary_logloss: 0.0603202	train's f1: 1	val's binary_logloss: 0.299305	val's f1: 0.869301
[238]	train's binary_logloss: 0.0598106	train's f1: 1	val's binary_logloss: 0.299283	val's f1: 0.871951
[239]	train's binary_logloss: 0.0592992	train's f1: 1	val's binary_logloss: 0.298817	val's f1: 0.871951
[240]	train's binary_logloss: 0.0588382	train's f1: 1	val's binary_logloss: 0.298501	val's f1: 0.871951
[241]	train's binary_logloss: 0.0583262	train's f1: 1	val's binary_logloss: 0.297998	val's f1: 0.871951
[242]	train's binary_logloss: 0.0578471	train's f1: 1	val's binary_logloss: 0.298181	val's f1: 0.871951
[243]	train's binary_logloss: 0.0572993	train's f1: 1	val's binary_logloss: 0.297715	val's f1: 0.874618
[244]	train's binary_logloss: 0.0567861	train's f1: 1	val's binar

[315]	train's binary_logloss: 0.0315761	train's f1: 1	val's binary_logloss: 0.282101	val's f1: 0.871951
[316]	train's binary_logloss: 0.0313105	train's f1: 1	val's binary_logloss: 0.281887	val's f1: 0.874618
[317]	train's binary_logloss: 0.0310504	train's f1: 1	val's binary_logloss: 0.281769	val's f1: 0.874618
[318]	train's binary_logloss: 0.030788	train's f1: 1	val's binary_logloss: 0.281507	val's f1: 0.874618
[319]	train's binary_logloss: 0.0305298	train's f1: 1	val's binary_logloss: 0.280921	val's f1: 0.877301
[320]	train's binary_logloss: 0.030285	train's f1: 1	val's binary_logloss: 0.280907	val's f1: 0.878049
[321]	train's binary_logloss: 0.0300418	train's f1: 1	val's binary_logloss: 0.281145	val's f1: 0.878049
[322]	train's binary_logloss: 0.0297873	train's f1: 1	val's binary_logloss: 0.281017	val's f1: 0.878049
[323]	train's binary_logloss: 0.0295388	train's f1: 1	val's binary_logloss: 0.281128	val's f1: 0.874618
[324]	train's binary_logloss: 0.0293082	train's f1: 1	val's binary

...

[2627]	train's binary_logloss: 1.86256e-06	train's f1: 1	val's binary_logloss: 0.458336	val's f1: 0.888889
[2628]	train's binary_logloss: 1.86181e-06	train's f1: 1	val's binary_logloss: 0.458373	val's f1: 0.888889
[2629]	train's binary_logloss: 1.86112e-06	train's f1: 1	val's binary_logloss: 0.4584	val's f1: 0.888889
[2630]	train's binary_logloss: 1.86044e-06	train's f1: 1	val's binary_logloss: 0.458417	val's f1: 0.888889
[2631]	train's binary_logloss: 1.85963e-06	train's f1: 1	val's binary_logloss: 0.458452	val's f1: 0.888889
[2632]	train's binary_logloss: 1.85889e-06	train's f1: 1	val's binary_logloss: 0.458446	val's f1: 0.888889
[2633]	train's binary_logloss: 1.85811e-06	train's f1: 1	val's binary_logloss: 0.458433	val's f1: 0.888889
[2634]	train's binary_logloss: 1.85736e-06	train's f1: 1	val's binary_logloss: 0.458476	val's f1: 0.888889
[2635]	train's binary_logloss: 1.85661e-06	train's f1: 1	val's binary_logloss: 0.458509	val's f1: 0.888889
[2636]	train's binary_logloss: 1.85601e

[2711]	train's binary_logloss: 1.79956e-06	train's f1: 1	val's binary_logloss: 0.458805	val's f1: 0.888889
[2712]	train's binary_logloss: 1.79909e-06	train's f1: 1	val's binary_logloss: 0.458792	val's f1: 0.888889
[2713]	train's binary_logloss: 1.79821e-06	train's f1: 1	val's binary_logloss: 0.458905	val's f1: 0.888889
[2714]	train's binary_logloss: 1.79751e-06	train's f1: 1	val's binary_logloss: 0.458936	val's f1: 0.888889
[2715]	train's binary_logloss: 1.79679e-06	train's f1: 1	val's binary_logloss: 0.45902	val's f1: 0.888889
[2716]	train's binary_logloss: 1.79609e-06	train's f1: 1	val's binary_logloss: 0.45904	val's f1: 0.888889
[2717]	train's binary_logloss: 1.79537e-06	train's f1: 1	val's binary_logloss: 0.459029	val's f1: 0.888889
[2718]	train's binary_logloss: 1.79469e-06	train's f1: 1	val's binary_logloss: 0.459067	val's f1: 0.888889
[2719]	train's binary_logloss: 1.79381e-06	train's f1: 1	val's binary_logloss: 0.459212	val's f1: 0.888889
[2720]	train's binary_logloss: 1.79301e

[2795]	train's binary_logloss: 1.74173e-06	train's f1: 1	val's binary_logloss: 0.460255	val's f1: 0.888889
[2796]	train's binary_logloss: 1.74092e-06	train's f1: 1	val's binary_logloss: 0.460381	val's f1: 0.888889
[2797]	train's binary_logloss: 1.74032e-06	train's f1: 1	val's binary_logloss: 0.460303	val's f1: 0.888889
[2798]	train's binary_logloss: 1.73968e-06	train's f1: 1	val's binary_logloss: 0.460157	val's f1: 0.888889
[2799]	train's binary_logloss: 1.73887e-06	train's f1: 1	val's binary_logloss: 0.460127	val's f1: 0.888889
[2800]	train's binary_logloss: 1.73854e-06	train's f1: 1	val's binary_logloss: 0.460164	val's f1: 0.888889
[2801]	train's binary_logloss: 1.7379e-06	train's f1: 1	val's binary_logloss: 0.460117	val's f1: 0.888889
[2802]	train's binary_logloss: 1.73749e-06	train's f1: 1	val's binary_logloss: 0.460131	val's f1: 0.888889
[2803]	train's binary_logloss: 1.73681e-06	train's f1: 1	val's binary_logloss: 0.460054	val's f1: 0.888889
[2804]	train's binary_logloss: 1.736e-

[2882]	train's binary_logloss: 1.68741e-06	train's f1: 1	val's binary_logloss: 0.461563	val's f1: 0.888889
[2883]	train's binary_logloss: 1.68672e-06	train's f1: 1	val's binary_logloss: 0.461489	val's f1: 0.888889
[2884]	train's binary_logloss: 1.6861e-06	train's f1: 1	val's binary_logloss: 0.461586	val's f1: 0.888889
[2885]	train's binary_logloss: 1.6855e-06	train's f1: 1	val's binary_logloss: 0.461546	val's f1: 0.888889
[2886]	train's binary_logloss: 1.68485e-06	train's f1: 1	val's binary_logloss: 0.461589	val's f1: 0.888889
[2887]	train's binary_logloss: 1.6842e-06	train's f1: 1	val's binary_logloss: 0.461658	val's f1: 0.888889
[2888]	train's binary_logloss: 1.68349e-06	train's f1: 1	val's binary_logloss: 0.461741	val's f1: 0.888889
[2889]	train's binary_logloss: 1.68308e-06	train's f1: 1	val's binary_logloss: 0.461697	val's f1: 0.888889
[2890]	train's binary_logloss: 1.68243e-06	train's f1: 1	val's binary_logloss: 0.461711	val's f1: 0.888889
[2891]	train's binary_logloss: 1.68166e-

[2959]	train's binary_logloss: 1.64287e-06	train's f1: 1	val's binary_logloss: 0.462496	val's f1: 0.888889
[2960]	train's binary_logloss: 1.64247e-06	train's f1: 1	val's binary_logloss: 0.462461	val's f1: 0.888889
[2961]	train's binary_logloss: 1.64182e-06	train's f1: 1	val's binary_logloss: 0.46249	val's f1: 0.888889
[2962]	train's binary_logloss: 1.64151e-06	train's f1: 1	val's binary_logloss: 0.462496	val's f1: 0.888889
[2963]	train's binary_logloss: 1.64086e-06	train's f1: 1	val's binary_logloss: 0.462545	val's f1: 0.888889
[2964]	train's binary_logloss: 1.6405e-06	train's f1: 1	val's binary_logloss: 0.462525	val's f1: 0.888889
[2965]	train's binary_logloss: 1.63993e-06	train's f1: 1	val's binary_logloss: 0.462457	val's f1: 0.888889
[2966]	train's binary_logloss: 1.63921e-06	train's f1: 1	val's binary_logloss: 0.462489	val's f1: 0.888889
[2967]	train's binary_logloss: 1.6386e-06	train's f1: 1	val's binary_logloss: 0.462533	val's f1: 0.888889
[2968]	train's binary_logloss: 1.63792e-

In [154]:
k562_lgb_pred_protein = k562_lgb_protein.predict(k562X_test,num_iteration=k562_lgb_protein.best_iteration)
f1_score(k562y_test,prob2label(k562_lgb_pred_protein))

0.9017199017199017

In [ ]:
roc_auc_score(k562y_test,k562_lgb_pred_protein)

### Train LGB on IMR90

In [156]:
IMR90X_train = imr90_original_data_json['X_train_protein']
IMR90y_train = imr90_original_data_json['y_train_protein']
IMR90X_test = imr90_original_data_json['X_test_protein']
IMR90y_test = imr90_original_data_json['y_test_protein']

imr90_lgb_train_protein, imr90_lgb_valid_protein, imr_lgb_test_protein = generate_lgb_use_data(IMR90X_train,
                                                                                               IMR90y_train,
                                                                                               IMR90X_test,
                                                                                               IMR90y_test)

In [157]:
imr90_lgb_protein = train_lgb(imr90_lgb_train_protein,imr90_lgb_valid_protein,
                              lgb_param,num_round+700,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.68141	train's f1: 0.796898	val's binary_logloss: 0.686353	val's f1: 0.709677
[2]	train's binary_logloss: 0.669616	train's f1: 0.818095	val's binary_logloss: 0.679451	val's f1: 0.7393
[3]	train's binary_logloss: 0.658785	train's f1: 0.837686	val's binary_logloss: 0.673763	val's f1: 0.731092
[4]	train's binary_logloss: 0.648208	train's f1: 0.845371	val's binary_logloss: 0.666307	val's f1: 0.74477
[5]	train's binary_logloss: 0.637893	train's f1: 0.855385	val's binary_logloss: 0.659755	val's f1: 0.748936
[6]	train's binary_logloss: 0.628196	train's f1: 0.86646	val's binary_logloss: 0.654408	val's f1: 0.738197
[7]	train's binary_logloss: 0.618654	train's f1: 0.865765	val's binary_logloss: 0.648308	val's f1: 0.740426
[8]	train's binary_logloss: 0.609336	train's f1: 0.868435	val's binary_logloss: 0.646109	val's f1: 0.735043
[9]	train's binary_logloss: 0.600441	train's f1: 0.874351	val's binary_logloss: 0.640742	val's f1: 0.737288
[10]	train's binary_logloss: 0.59

[79]	train's binary_logloss: 0.258964	train's f1: 0.990153	val's binary_logloss: 0.488479	val's f1: 0.79476
[80]	train's binary_logloss: 0.256141	train's f1: 0.9896	val's binary_logloss: 0.487512	val's f1: 0.798246
[81]	train's binary_logloss: 0.253615	train's f1: 0.992358	val's binary_logloss: 0.487024	val's f1: 0.807018
[82]	train's binary_logloss: 0.25091	train's f1: 0.990705	val's binary_logloss: 0.485998	val's f1: 0.803493
[83]	train's binary_logloss: 0.2483	train's f1: 0.992358	val's binary_logloss: 0.484505	val's f1: 0.819383
[84]	train's binary_logloss: 0.245819	train's f1: 0.991808	val's binary_logloss: 0.483726	val's f1: 0.808696
[85]	train's binary_logloss: 0.243197	train's f1: 0.99345	val's binary_logloss: 0.482205	val's f1: 0.812227
[86]	train's binary_logloss: 0.240732	train's f1: 0.9929	val's binary_logloss: 0.481981	val's f1: 0.812227
[87]	train's binary_logloss: 0.238206	train's f1: 0.992892	val's binary_logloss: 0.481675	val's f1: 0.815789
[88]	train's binary_logloss:

[159]	train's binary_logloss: 0.121525	train's f1: 1	val's binary_logloss: 0.427297	val's f1: 0.819383
[160]	train's binary_logloss: 0.120436	train's f1: 1	val's binary_logloss: 0.427421	val's f1: 0.815789
[161]	train's binary_logloss: 0.119308	train's f1: 1	val's binary_logloss: 0.42646	val's f1: 0.819383
[162]	train's binary_logloss: 0.118303	train's f1: 1	val's binary_logloss: 0.426116	val's f1: 0.819383
[163]	train's binary_logloss: 0.117226	train's f1: 1	val's binary_logloss: 0.425358	val's f1: 0.819383
[164]	train's binary_logloss: 0.116215	train's f1: 1	val's binary_logloss: 0.425343	val's f1: 0.815789
[165]	train's binary_logloss: 0.115192	train's f1: 1	val's binary_logloss: 0.425495	val's f1: 0.819383
[166]	train's binary_logloss: 0.114136	train's f1: 1	val's binary_logloss: 0.424993	val's f1: 0.815789
[167]	train's binary_logloss: 0.113149	train's f1: 1	val's binary_logloss: 0.424467	val's f1: 0.815789
[168]	train's binary_logloss: 0.112154	train's f1: 1	val's binary_logloss:

[242]	train's binary_logloss: 0.0595377	train's f1: 1	val's binary_logloss: 0.418058	val's f1: 0.822511
[243]	train's binary_logloss: 0.0590171	train's f1: 1	val's binary_logloss: 0.417561	val's f1: 0.822511
[244]	train's binary_logloss: 0.0585043	train's f1: 1	val's binary_logloss: 0.417669	val's f1: 0.822511
[245]	train's binary_logloss: 0.0580689	train's f1: 1	val's binary_logloss: 0.418538	val's f1: 0.822511
[246]	train's binary_logloss: 0.0575411	train's f1: 1	val's binary_logloss: 0.419145	val's f1: 0.822511
[247]	train's binary_logloss: 0.0570458	train's f1: 1	val's binary_logloss: 0.419088	val's f1: 0.822511
[248]	train's binary_logloss: 0.056588	train's f1: 1	val's binary_logloss: 0.41963	val's f1: 0.822511
[249]	train's binary_logloss: 0.0561212	train's f1: 1	val's binary_logloss: 0.419863	val's f1: 0.826087
[250]	train's binary_logloss: 0.0556798	train's f1: 1	val's binary_logloss: 0.419806	val's f1: 0.826087
[251]	train's binary_logloss: 0.0552371	train's f1: 1	val's binary

[326]	train's binary_logloss: 0.0297464	train's f1: 1	val's binary_logloss: 0.419174	val's f1: 0.823009
[327]	train's binary_logloss: 0.0295342	train's f1: 1	val's binary_logloss: 0.419423	val's f1: 0.828194
[328]	train's binary_logloss: 0.0292886	train's f1: 1	val's binary_logloss: 0.419815	val's f1: 0.828194
[329]	train's binary_logloss: 0.0290356	train's f1: 1	val's binary_logloss: 0.419905	val's f1: 0.828194
[330]	train's binary_logloss: 0.0288357	train's f1: 1	val's binary_logloss: 0.419692	val's f1: 0.828194
[331]	train's binary_logloss: 0.0286169	train's f1: 1	val's binary_logloss: 0.419827	val's f1: 0.828194
[332]	train's binary_logloss: 0.0283628	train's f1: 1	val's binary_logloss: 0.419862	val's f1: 0.828194
[333]	train's binary_logloss: 0.0281236	train's f1: 1	val's binary_logloss: 0.420011	val's f1: 0.828194
[334]	train's binary_logloss: 0.0279093	train's f1: 1	val's binary_logloss: 0.420165	val's f1: 0.828194
[335]	train's binary_logloss: 0.0277201	train's f1: 1	val's bina

...

[3258]	train's binary_logloss: 2.57547e-06	train's f1: 1	val's binary_logloss: 0.755762	val's f1: 0.835556
[3259]	train's binary_logloss: 2.5747e-06	train's f1: 1	val's binary_logloss: 0.75587	val's f1: 0.835556
[3260]	train's binary_logloss: 2.57435e-06	train's f1: 1	val's binary_logloss: 0.755867	val's f1: 0.835556
[3261]	train's binary_logloss: 2.57373e-06	train's f1: 1	val's binary_logloss: 0.755775	val's f1: 0.835556
[3262]	train's binary_logloss: 2.57331e-06	train's f1: 1	val's binary_logloss: 0.755882	val's f1: 0.835556
[3263]	train's binary_logloss: 2.57272e-06	train's f1: 1	val's binary_logloss: 0.755963	val's f1: 0.835556
[3264]	train's binary_logloss: 2.57237e-06	train's f1: 1	val's binary_logloss: 0.756006	val's f1: 0.835556
[3265]	train's binary_logloss: 2.57147e-06	train's f1: 1	val's binary_logloss: 0.756062	val's f1: 0.835556
[3266]	train's binary_logloss: 2.57072e-06	train's f1: 1	val's binary_logloss: 0.756101	val's f1: 0.835556
[3267]	train's binary_logloss: 2.57036e

[3366]	train's binary_logloss: 2.51567e-06	train's f1: 1	val's binary_logloss: 0.758013	val's f1: 0.835556
[3367]	train's binary_logloss: 2.51486e-06	train's f1: 1	val's binary_logloss: 0.757991	val's f1: 0.835556
[3368]	train's binary_logloss: 2.51449e-06	train's f1: 1	val's binary_logloss: 0.757996	val's f1: 0.835556
[3369]	train's binary_logloss: 2.5136e-06	train's f1: 1	val's binary_logloss: 0.758028	val's f1: 0.835556
[3370]	train's binary_logloss: 2.51301e-06	train's f1: 1	val's binary_logloss: 0.758016	val's f1: 0.835556
[3371]	train's binary_logloss: 2.51264e-06	train's f1: 1	val's binary_logloss: 0.758028	val's f1: 0.835556
[3372]	train's binary_logloss: 2.51231e-06	train's f1: 1	val's binary_logloss: 0.758017	val's f1: 0.835556
[3373]	train's binary_logloss: 2.51191e-06	train's f1: 1	val's binary_logloss: 0.758182	val's f1: 0.835556
[3374]	train's binary_logloss: 2.51122e-06	train's f1: 1	val's binary_logloss: 0.758147	val's f1: 0.835556
[3375]	train's binary_logloss: 2.51045

[3476]	train's binary_logloss: 2.46037e-06	train's f1: 1	val's binary_logloss: 0.759116	val's f1: 0.835556
[3477]	train's binary_logloss: 2.45969e-06	train's f1: 1	val's binary_logloss: 0.759272	val's f1: 0.835556
[3478]	train's binary_logloss: 2.45901e-06	train's f1: 1	val's binary_logloss: 0.759358	val's f1: 0.835556
[3479]	train's binary_logloss: 2.45839e-06	train's f1: 1	val's binary_logloss: 0.759511	val's f1: 0.835556
[3480]	train's binary_logloss: 2.45743e-06	train's f1: 1	val's binary_logloss: 0.759558	val's f1: 0.835556
[3481]	train's binary_logloss: 2.45678e-06	train's f1: 1	val's binary_logloss: 0.759523	val's f1: 0.835556
[3482]	train's binary_logloss: 2.45621e-06	train's f1: 1	val's binary_logloss: 0.759507	val's f1: 0.835556
[3483]	train's binary_logloss: 2.45552e-06	train's f1: 1	val's binary_logloss: 0.759575	val's f1: 0.835556
[3484]	train's binary_logloss: 2.45516e-06	train's f1: 1	val's binary_logloss: 0.759597	val's f1: 0.835556
[3485]	train's binary_logloss: 2.4544

[3585]	train's binary_logloss: 2.40535e-06	train's f1: 1	val's binary_logloss: 0.759649	val's f1: 0.835556
[3586]	train's binary_logloss: 2.40502e-06	train's f1: 1	val's binary_logloss: 0.759689	val's f1: 0.835556
[3587]	train's binary_logloss: 2.40449e-06	train's f1: 1	val's binary_logloss: 0.759702	val's f1: 0.835556
[3588]	train's binary_logloss: 2.4041e-06	train's f1: 1	val's binary_logloss: 0.759659	val's f1: 0.835556
[3589]	train's binary_logloss: 2.4032e-06	train's f1: 1	val's binary_logloss: 0.759544	val's f1: 0.835556
[3590]	train's binary_logloss: 2.40263e-06	train's f1: 1	val's binary_logloss: 0.759694	val's f1: 0.835556
[3591]	train's binary_logloss: 2.40173e-06	train's f1: 1	val's binary_logloss: 0.759741	val's f1: 0.835556
[3592]	train's binary_logloss: 2.40138e-06	train's f1: 1	val's binary_logloss: 0.759875	val's f1: 0.835556
[3593]	train's binary_logloss: 2.40107e-06	train's f1: 1	val's binary_logloss: 0.759893	val's f1: 0.835556
[3594]	train's binary_logloss: 2.40044e

[3696]	train's binary_logloss: 2.35315e-06	train's f1: 1	val's binary_logloss: 0.761103	val's f1: 0.835556
[3697]	train's binary_logloss: 2.35282e-06	train's f1: 1	val's binary_logloss: 0.761234	val's f1: 0.835556
[3698]	train's binary_logloss: 2.35249e-06	train's f1: 1	val's binary_logloss: 0.761258	val's f1: 0.835556
[3699]	train's binary_logloss: 2.35219e-06	train's f1: 1	val's binary_logloss: 0.761341	val's f1: 0.835556
[3700]	train's binary_logloss: 2.3519e-06	train's f1: 1	val's binary_logloss: 0.761368	val's f1: 0.835556


In [159]:
imr90_lgb_pred_ptotein = imr90_lgb_protein.predict(IMR90X_test,num_iteration=imr90_lgb_protein.best_iteration)
f1_score(IMR90y_test,prob2label(imr90_lgb_pred_ptotein))

0.8442622950819674

In [ ]:
roc_auc_score(IMR90y_test,imr90_lgb_pred_ptotein)

### Train LGB on GM12878

In [161]:
GM12878X_train = gm12878_original_data_json['X_train_protein']
GM12878y_train = gm12878_original_data_json['y_train_protein']
GM12878X_test = gm12878_original_data_json['X_test_protein']
GM12878y_test = gm12878_original_data_json['y_test_protein']


gm12878_lgb_train_protein, gm12878_lgb_valid_protein, gm12878_lgb_tes_proteint = generate_lgb_use_data(GM12878X_train,
                                                                                                       GM12878y_train,
                                                                                                       GM12878X_test,
                                                                                                       GM12878y_test)

In [162]:
gm12878_lgb_protein = train_lgb(gm12878_lgb_train_protein,gm12878_lgb_valid_protein,
                                lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.683607	train's f1: 0.117276	val's binary_logloss: 0.689025	val's f1: 0.0837696
[2]	train's binary_logloss: 0.674668	train's f1: 0.681928	val's binary_logloss: 0.683453	val's f1: 0.558923
[3]	train's binary_logloss: 0.666089	train's f1: 0.722353	val's binary_logloss: 0.678442	val's f1: 0.608696
[4]	train's binary_logloss: 0.657691	train's f1: 0.742081	val's binary_logloss: 0.671525	val's f1: 0.623794
[5]	train's binary_logloss: 0.649851	train's f1: 0.757274	val's binary_logloss: 0.667043	val's f1: 0.64557
[6]	train's binary_logloss: 0.642128	train's f1: 0.771199	val's binary_logloss: 0.661314	val's f1: 0.666667
[7]	train's binary_logloss: 0.634661	train's f1: 0.771676	val's binary_logloss: 0.655985	val's f1: 0.685015
[8]	train's binary_logloss: 0.627464	train's f1: 0.789305	val's binary_logloss: 0.650908	val's f1: 0.692771
[9]	train's binary_logloss: 0.620492	train's f1: 0.791562	val's binary_logloss: 0.646028	val's f1: 0.702703
[10]	train's binary_logloss:

[86]	train's binary_logloss: 0.323092	train's f1: 0.960243	val's binary_logloss: 0.473346	val's f1: 0.810198
[87]	train's binary_logloss: 0.321047	train's f1: 0.960216	val's binary_logloss: 0.473588	val's f1: 0.806818
[88]	train's binary_logloss: 0.318893	train's f1: 0.96194	val's binary_logloss: 0.473408	val's f1: 0.806818
[89]	train's binary_logloss: 0.316528	train's f1: 0.96159	val's binary_logloss: 0.472299	val's f1: 0.809117
[90]	train's binary_logloss: 0.314341	train's f1: 0.961966	val's binary_logloss: 0.471358	val's f1: 0.806818
[91]	train's binary_logloss: 0.312091	train's f1: 0.963312	val's binary_logloss: 0.470498	val's f1: 0.80791
[92]	train's binary_logloss: 0.309793	train's f1: 0.963636	val's binary_logloss: 0.469165	val's f1: 0.80791
[93]	train's binary_logloss: 0.307437	train's f1: 0.963985	val's binary_logloss: 0.468623	val's f1: 0.806818
[94]	train's binary_logloss: 0.305554	train's f1: 0.96431	val's binary_logloss: 0.468074	val's f1: 0.809117
[95]	train's binary_logl

[163]	train's binary_logloss: 0.200803	train's f1: 0.991962	val's binary_logloss: 0.428077	val's f1: 0.813559
[164]	train's binary_logloss: 0.199542	train's f1: 0.991962	val's binary_logloss: 0.427246	val's f1: 0.811268
[165]	train's binary_logloss: 0.198216	train's f1: 0.991962	val's binary_logloss: 0.42633	val's f1: 0.808989
[166]	train's binary_logloss: 0.197129	train's f1: 0.991962	val's binary_logloss: 0.426013	val's f1: 0.811268
[167]	train's binary_logloss: 0.195966	train's f1: 0.992295	val's binary_logloss: 0.425779	val's f1: 0.811268
[168]	train's binary_logloss: 0.194862	train's f1: 0.992295	val's binary_logloss: 0.425451	val's f1: 0.811268
[169]	train's binary_logloss: 0.193834	train's f1: 0.992965	val's binary_logloss: 0.425631	val's f1: 0.808989
[170]	train's binary_logloss: 0.19276	train's f1: 0.992627	val's binary_logloss: 0.42479	val's f1: 0.808989
[171]	train's binary_logloss: 0.191544	train's f1: 0.992627	val's binary_logloss: 0.42404	val's f1: 0.808989
[172]	train's 

[239]	train's binary_logloss: 0.132673	train's f1: 0.999328	val's binary_logloss: 0.399681	val's f1: 0.820225
[240]	train's binary_logloss: 0.132019	train's f1: 0.999328	val's binary_logloss: 0.399616	val's f1: 0.823529
[241]	train's binary_logloss: 0.131318	train's f1: 0.999328	val's binary_logloss: 0.399363	val's f1: 0.820225
[242]	train's binary_logloss: 0.130688	train's f1: 0.999328	val's binary_logloss: 0.399391	val's f1: 0.817927
[243]	train's binary_logloss: 0.130113	train's f1: 0.999328	val's binary_logloss: 0.399415	val's f1: 0.820225
[244]	train's binary_logloss: 0.129516	train's f1: 0.999328	val's binary_logloss: 0.399225	val's f1: 0.821229
[245]	train's binary_logloss: 0.128892	train's f1: 0.999328	val's binary_logloss: 0.398886	val's f1: 0.821229
[246]	train's binary_logloss: 0.128145	train's f1: 0.999664	val's binary_logloss: 0.398611	val's f1: 0.821229
[247]	train's binary_logloss: 0.127457	train's f1: 0.999664	val's binary_logloss: 0.398188	val's f1: 0.818942
[248]	trai

[327]	train's binary_logloss: 0.0842903	train's f1: 1	val's binary_logloss: 0.379642	val's f1: 0.823204
[328]	train's binary_logloss: 0.0839488	train's f1: 1	val's binary_logloss: 0.379824	val's f1: 0.823204
[329]	train's binary_logloss: 0.0834841	train's f1: 1	val's binary_logloss: 0.379686	val's f1: 0.823204
[330]	train's binary_logloss: 0.0829957	train's f1: 1	val's binary_logloss: 0.379162	val's f1: 0.823204
[331]	train's binary_logloss: 0.0826006	train's f1: 1	val's binary_logloss: 0.379101	val's f1: 0.823204
[332]	train's binary_logloss: 0.082237	train's f1: 1	val's binary_logloss: 0.378895	val's f1: 0.823204
[333]	train's binary_logloss: 0.0817638	train's f1: 1	val's binary_logloss: 0.378598	val's f1: 0.826446
[334]	train's binary_logloss: 0.0813732	train's f1: 1	val's binary_logloss: 0.378593	val's f1: 0.826446
[335]	train's binary_logloss: 0.0809966	train's f1: 1	val's binary_logloss: 0.377888	val's f1: 0.826446
[336]	train's binary_logloss: 0.080593	train's f1: 1	val's binary

...

[2610]	train's binary_logloss: 4.27261e-06	train's f1: 1	val's binary_logloss: 0.501988	val's f1: 0.861878
[2611]	train's binary_logloss: 4.26808e-06	train's f1: 1	val's binary_logloss: 0.501909	val's f1: 0.861878
[2612]	train's binary_logloss: 4.264e-06	train's f1: 1	val's binary_logloss: 0.501948	val's f1: 0.861878
[2613]	train's binary_logloss: 4.25856e-06	train's f1: 1	val's binary_logloss: 0.502077	val's f1: 0.859504
[2614]	train's binary_logloss: 4.25482e-06	train's f1: 1	val's binary_logloss: 0.502192	val's f1: 0.859504
[2615]	train's binary_logloss: 4.25033e-06	train's f1: 1	val's binary_logloss: 0.502209	val's f1: 0.859504
[2616]	train's binary_logloss: 4.24566e-06	train's f1: 1	val's binary_logloss: 0.502176	val's f1: 0.861878
[2617]	train's binary_logloss: 4.24208e-06	train's f1: 1	val's binary_logloss: 0.502411	val's f1: 0.859504
[2618]	train's binary_logloss: 4.23704e-06	train's f1: 1	val's binary_logloss: 0.502444	val's f1: 0.861878
[2619]	train's binary_logloss: 4.23163e

[2711]	train's binary_logloss: 3.87131e-06	train's f1: 1	val's binary_logloss: 0.505615	val's f1: 0.861878
[2712]	train's binary_logloss: 3.86772e-06	train's f1: 1	val's binary_logloss: 0.505574	val's f1: 0.861878
[2713]	train's binary_logloss: 3.86429e-06	train's f1: 1	val's binary_logloss: 0.505635	val's f1: 0.861878
[2714]	train's binary_logloss: 3.86114e-06	train's f1: 1	val's binary_logloss: 0.505652	val's f1: 0.861878
[2715]	train's binary_logloss: 3.85736e-06	train's f1: 1	val's binary_logloss: 0.505572	val's f1: 0.861878
[2716]	train's binary_logloss: 3.85441e-06	train's f1: 1	val's binary_logloss: 0.505755	val's f1: 0.861878
[2717]	train's binary_logloss: 3.85034e-06	train's f1: 1	val's binary_logloss: 0.505675	val's f1: 0.861878
[2718]	train's binary_logloss: 3.84663e-06	train's f1: 1	val's binary_logloss: 0.505776	val's f1: 0.861878
[2719]	train's binary_logloss: 3.84318e-06	train's f1: 1	val's binary_logloss: 0.505743	val's f1: 0.861878
[2720]	train's binary_logloss: 3.8388

[2789]	train's binary_logloss: 3.61138e-06	train's f1: 1	val's binary_logloss: 0.506389	val's f1: 0.861878
[2790]	train's binary_logloss: 3.60833e-06	train's f1: 1	val's binary_logloss: 0.506336	val's f1: 0.861878
[2791]	train's binary_logloss: 3.60595e-06	train's f1: 1	val's binary_logloss: 0.506218	val's f1: 0.861878
[2792]	train's binary_logloss: 3.60323e-06	train's f1: 1	val's binary_logloss: 0.506145	val's f1: 0.861878
[2793]	train's binary_logloss: 3.59987e-06	train's f1: 1	val's binary_logloss: 0.506188	val's f1: 0.861878
[2794]	train's binary_logloss: 3.59676e-06	train's f1: 1	val's binary_logloss: 0.5061	val's f1: 0.861878
[2795]	train's binary_logloss: 3.59427e-06	train's f1: 1	val's binary_logloss: 0.506235	val's f1: 0.861878
[2796]	train's binary_logloss: 3.59154e-06	train's f1: 1	val's binary_logloss: 0.506305	val's f1: 0.861878
[2797]	train's binary_logloss: 3.589e-06	train's f1: 1	val's binary_logloss: 0.50624	val's f1: 0.861878
[2798]	train's binary_logloss: 3.5855e-06	

[2868]	train's binary_logloss: 3.39585e-06	train's f1: 1	val's binary_logloss: 0.508088	val's f1: 0.861878
[2869]	train's binary_logloss: 3.39343e-06	train's f1: 1	val's binary_logloss: 0.508166	val's f1: 0.861878
[2870]	train's binary_logloss: 3.39098e-06	train's f1: 1	val's binary_logloss: 0.508258	val's f1: 0.861878
[2871]	train's binary_logloss: 3.38875e-06	train's f1: 1	val's binary_logloss: 0.50818	val's f1: 0.861878
[2872]	train's binary_logloss: 3.38679e-06	train's f1: 1	val's binary_logloss: 0.508137	val's f1: 0.861878
[2873]	train's binary_logloss: 3.38394e-06	train's f1: 1	val's binary_logloss: 0.508154	val's f1: 0.861878
[2874]	train's binary_logloss: 3.38119e-06	train's f1: 1	val's binary_logloss: 0.508125	val's f1: 0.861878
[2875]	train's binary_logloss: 3.37844e-06	train's f1: 1	val's binary_logloss: 0.508409	val's f1: 0.861878
[2876]	train's binary_logloss: 3.37616e-06	train's f1: 1	val's binary_logloss: 0.508327	val's f1: 0.861878
[2877]	train's binary_logloss: 3.37323

[2951]	train's binary_logloss: 3.20494e-06	train's f1: 1	val's binary_logloss: 0.509774	val's f1: 0.861878
[2952]	train's binary_logloss: 3.20281e-06	train's f1: 1	val's binary_logloss: 0.509807	val's f1: 0.861878
[2953]	train's binary_logloss: 3.20096e-06	train's f1: 1	val's binary_logloss: 0.509874	val's f1: 0.861878
[2954]	train's binary_logloss: 3.19866e-06	train's f1: 1	val's binary_logloss: 0.509949	val's f1: 0.861878
[2955]	train's binary_logloss: 3.19625e-06	train's f1: 1	val's binary_logloss: 0.510147	val's f1: 0.861878
[2956]	train's binary_logloss: 3.19395e-06	train's f1: 1	val's binary_logloss: 0.510278	val's f1: 0.861878
[2957]	train's binary_logloss: 3.19166e-06	train's f1: 1	val's binary_logloss: 0.510446	val's f1: 0.861878
[2958]	train's binary_logloss: 3.18982e-06	train's f1: 1	val's binary_logloss: 0.510523	val's f1: 0.861878
[2959]	train's binary_logloss: 3.1875e-06	train's f1: 1	val's binary_logloss: 0.510561	val's f1: 0.861878
[2960]	train's binary_logloss: 3.18539

In [163]:
gm12878_lgb_pred_protein = gm12878_lgb_protein.predict(GM12878X_test,num_iteration=gm12878_lgb_protein.best_iteration)
f1_score(GM12878y_test,prob2label(gm12878_lgb_pred_protein))

0.854586129753915

In [ ]:
roc_auc_score(GM12878y_test,gm12878_lgb_pred_protein)

### Train LGB On HUVEC

In [165]:
HUVECX_train = huvec_original_data_json['X_train_protein']
HUVECy_train = huvec_original_data_json['y_train_protein']
HUVECX_test = huvec_original_data_json['X_test_protein']
HUVECy_test = huvec_original_data_json['y_test_protein']

huvec_lgb_train_protein,huvec_lgb_valid_protein,huvec_lgb_test_protein = generate_lgb_use_data(HUVECX_train,
                                                                                            HUVECy_train,
                                                                                            HUVECX_test,
                                                                                            HUVECy_test)
huvec_lgb_protein = train_lgb(huvec_lgb_train_protein,huvec_lgb_valid_protein,
                             lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.679224	train's f1: 0.839387	val's binary_logloss: 0.683258	val's f1: 0.746154
[2]	train's binary_logloss: 0.665938	train's f1: 0.842918	val's binary_logloss: 0.674489	val's f1: 0.740458
[3]	train's binary_logloss: 0.65341	train's f1: 0.844212	val's binary_logloss: 0.665559	val's f1: 0.741313
[4]	train's binary_logloss: 0.640826	train's f1: 0.856004	val's binary_logloss: 0.657805	val's f1: 0.75969
[5]	train's binary_logloss: 0.6294	train's f1: 0.863278	val's binary_logloss: 0.650976	val's f1: 0.744186
[6]	train's binary_logloss: 0.618445	train's f1: 0.878841	val's binary_logloss: 0.643719	val's f1: 0.754864
[7]	train's binary_logloss: 0.607164	train's f1: 0.881654	val's binary_logloss: 0.637075	val's f1: 0.757812
[8]	train's binary_logloss: 0.597035	train's f1: 0.890062	val's binary_logloss: 0.630169	val's f1: 0.75969
[9]	train's binary_logloss: 0.586933	train's f1: 0.885174	val's binary_logloss: 0.623547	val's f1: 0.749035
[10]	train's binary_logloss: 0.57

[85]	train's binary_logloss: 0.229883	train's f1: 0.986907	val's binary_logloss: 0.41623	val's f1: 0.829457
[86]	train's binary_logloss: 0.227721	train's f1: 0.988703	val's binary_logloss: 0.415745	val's f1: 0.833977
[87]	train's binary_logloss: 0.225584	train's f1: 0.98916	val's binary_logloss: 0.41494	val's f1: 0.829457
[88]	train's binary_logloss: 0.223334	train's f1: 0.988257	val's binary_logloss: 0.413732	val's f1: 0.829457
[89]	train's binary_logloss: 0.221124	train's f1: 0.988257	val's binary_logloss: 0.412522	val's f1: 0.829457
[90]	train's binary_logloss: 0.218918	train's f1: 0.988703	val's binary_logloss: 0.411748	val's f1: 0.833977
[91]	train's binary_logloss: 0.216863	train's f1: 0.989616	val's binary_logloss: 0.411022	val's f1: 0.838462
[92]	train's binary_logloss: 0.214801	train's f1: 0.990063	val's binary_logloss: 0.410522	val's f1: 0.829457
[93]	train's binary_logloss: 0.212539	train's f1: 0.990063	val's binary_logloss: 0.409576	val's f1: 0.826255
[94]	train's binary_lo

[169]	train's binary_logloss: 0.107265	train's f1: 1	val's binary_logloss: 0.368606	val's f1: 0.870229
[170]	train's binary_logloss: 0.106361	train's f1: 1	val's binary_logloss: 0.367706	val's f1: 0.870229
[171]	train's binary_logloss: 0.1054	train's f1: 1	val's binary_logloss: 0.367475	val's f1: 0.870229
[172]	train's binary_logloss: 0.104512	train's f1: 1	val's binary_logloss: 0.367207	val's f1: 0.870229
[173]	train's binary_logloss: 0.103629	train's f1: 1	val's binary_logloss: 0.366398	val's f1: 0.8659
[174]	train's binary_logloss: 0.102788	train's f1: 1	val's binary_logloss: 0.366537	val's f1: 0.8659
[175]	train's binary_logloss: 0.101928	train's f1: 1	val's binary_logloss: 0.366504	val's f1: 0.8659
[176]	train's binary_logloss: 0.101053	train's f1: 1	val's binary_logloss: 0.365905	val's f1: 0.874525
[177]	train's binary_logloss: 0.10014	train's f1: 1	val's binary_logloss: 0.365787	val's f1: 0.871212
[178]	train's binary_logloss: 0.0993141	train's f1: 1	val's binary_logloss: 0.3654

[253]	train's binary_logloss: 0.0529607	train's f1: 1	val's binary_logloss: 0.346137	val's f1: 0.862595
[254]	train's binary_logloss: 0.0524989	train's f1: 1	val's binary_logloss: 0.34631	val's f1: 0.86692
[255]	train's binary_logloss: 0.0520749	train's f1: 1	val's binary_logloss: 0.345738	val's f1: 0.862595
[256]	train's binary_logloss: 0.0516333	train's f1: 1	val's binary_logloss: 0.345618	val's f1: 0.871212
[257]	train's binary_logloss: 0.0512197	train's f1: 1	val's binary_logloss: 0.345927	val's f1: 0.871212
[258]	train's binary_logloss: 0.0508028	train's f1: 1	val's binary_logloss: 0.346737	val's f1: 0.86692
[259]	train's binary_logloss: 0.0504298	train's f1: 1	val's binary_logloss: 0.346857	val's f1: 0.86692
[260]	train's binary_logloss: 0.049998	train's f1: 1	val's binary_logloss: 0.346875	val's f1: 0.86692
[261]	train's binary_logloss: 0.0496284	train's f1: 1	val's binary_logloss: 0.346998	val's f1: 0.86692
[262]	train's binary_logloss: 0.0492034	train's f1: 1	val's binary_logl

[337]	train's binary_logloss: 0.0270038	train's f1: 1	val's binary_logloss: 0.342258	val's f1: 0.847328
[338]	train's binary_logloss: 0.0267862	train's f1: 1	val's binary_logloss: 0.342356	val's f1: 0.854962
[339]	train's binary_logloss: 0.0265658	train's f1: 1	val's binary_logloss: 0.342479	val's f1: 0.851711
[340]	train's binary_logloss: 0.0263566	train's f1: 1	val's binary_logloss: 0.342246	val's f1: 0.851711
[341]	train's binary_logloss: 0.0261373	train's f1: 1	val's binary_logloss: 0.342487	val's f1: 0.851711
[342]	train's binary_logloss: 0.0259458	train's f1: 1	val's binary_logloss: 0.341919	val's f1: 0.854962
[343]	train's binary_logloss: 0.0257305	train's f1: 1	val's binary_logloss: 0.341419	val's f1: 0.851711
[344]	train's binary_logloss: 0.0255166	train's f1: 1	val's binary_logloss: 0.341431	val's f1: 0.851711
[345]	train's binary_logloss: 0.0252916	train's f1: 1	val's binary_logloss: 0.340891	val's f1: 0.851711
[346]	train's binary_logloss: 0.025101	train's f1: 1	val's binar

...

[2487]	train's binary_logloss: 2.8152e-06	train's f1: 1	val's binary_logloss: 0.576199	val's f1: 0.859316
[2488]	train's binary_logloss: 2.81375e-06	train's f1: 1	val's binary_logloss: 0.576238	val's f1: 0.859316
[2489]	train's binary_logloss: 2.81238e-06	train's f1: 1	val's binary_logloss: 0.576287	val's f1: 0.859316
[2490]	train's binary_logloss: 2.81079e-06	train's f1: 1	val's binary_logloss: 0.576115	val's f1: 0.859316
[2491]	train's binary_logloss: 2.80937e-06	train's f1: 1	val's binary_logloss: 0.576055	val's f1: 0.859316
[2492]	train's binary_logloss: 2.80801e-06	train's f1: 1	val's binary_logloss: 0.576048	val's f1: 0.859316
[2493]	train's binary_logloss: 2.80671e-06	train's f1: 1	val's binary_logloss: 0.576166	val's f1: 0.859316
[2494]	train's binary_logloss: 2.80536e-06	train's f1: 1	val's binary_logloss: 0.576273	val's f1: 0.859316
[2495]	train's binary_logloss: 2.8039e-06	train's f1: 1	val's binary_logloss: 0.57628	val's f1: 0.859316
[2496]	train's binary_logloss: 2.80224e-

[2597]	train's binary_logloss: 2.67881e-06	train's f1: 1	val's binary_logloss: 0.576217	val's f1: 0.859316
[2598]	train's binary_logloss: 2.67731e-06	train's f1: 1	val's binary_logloss: 0.576188	val's f1: 0.859316
[2599]	train's binary_logloss: 2.67617e-06	train's f1: 1	val's binary_logloss: 0.576287	val's f1: 0.859316
[2600]	train's binary_logloss: 2.67502e-06	train's f1: 1	val's binary_logloss: 0.57641	val's f1: 0.859316
[2601]	train's binary_logloss: 2.67383e-06	train's f1: 1	val's binary_logloss: 0.57636	val's f1: 0.859316
[2602]	train's binary_logloss: 2.67253e-06	train's f1: 1	val's binary_logloss: 0.57646	val's f1: 0.859316
[2603]	train's binary_logloss: 2.67128e-06	train's f1: 1	val's binary_logloss: 0.576496	val's f1: 0.859316
[2604]	train's binary_logloss: 2.66993e-06	train's f1: 1	val's binary_logloss: 0.576336	val's f1: 0.859316
[2605]	train's binary_logloss: 2.66852e-06	train's f1: 1	val's binary_logloss: 0.576349	val's f1: 0.859316
[2606]	train's binary_logloss: 2.66718e-

[2708]	train's binary_logloss: 2.56484e-06	train's f1: 1	val's binary_logloss: 0.576341	val's f1: 0.854962
[2709]	train's binary_logloss: 2.56316e-06	train's f1: 1	val's binary_logloss: 0.5762	val's f1: 0.854962
[2710]	train's binary_logloss: 2.56175e-06	train's f1: 1	val's binary_logloss: 0.576205	val's f1: 0.854962
[2711]	train's binary_logloss: 2.56082e-06	train's f1: 1	val's binary_logloss: 0.576141	val's f1: 0.854962
[2712]	train's binary_logloss: 2.55944e-06	train's f1: 1	val's binary_logloss: 0.576253	val's f1: 0.854962
[2713]	train's binary_logloss: 2.55873e-06	train's f1: 1	val's binary_logloss: 0.576373	val's f1: 0.854962
[2714]	train's binary_logloss: 2.55761e-06	train's f1: 1	val's binary_logloss: 0.576324	val's f1: 0.854962
[2715]	train's binary_logloss: 2.55682e-06	train's f1: 1	val's binary_logloss: 0.576323	val's f1: 0.854962
[2716]	train's binary_logloss: 2.55567e-06	train's f1: 1	val's binary_logloss: 0.576465	val's f1: 0.854962
[2717]	train's binary_logloss: 2.55496e

[2816]	train's binary_logloss: 2.46472e-06	train's f1: 1	val's binary_logloss: 0.577456	val's f1: 0.854962
[2817]	train's binary_logloss: 2.46381e-06	train's f1: 1	val's binary_logloss: 0.577538	val's f1: 0.854962
[2818]	train's binary_logloss: 2.463e-06	train's f1: 1	val's binary_logloss: 0.577548	val's f1: 0.854962
[2819]	train's binary_logloss: 2.46226e-06	train's f1: 1	val's binary_logloss: 0.577562	val's f1: 0.854962
[2820]	train's binary_logloss: 2.46124e-06	train's f1: 1	val's binary_logloss: 0.577579	val's f1: 0.854962
[2821]	train's binary_logloss: 2.46051e-06	train's f1: 1	val's binary_logloss: 0.57747	val's f1: 0.854962
[2822]	train's binary_logloss: 2.4597e-06	train's f1: 1	val's binary_logloss: 0.577481	val's f1: 0.854962
[2823]	train's binary_logloss: 2.45897e-06	train's f1: 1	val's binary_logloss: 0.577427	val's f1: 0.854962
[2824]	train's binary_logloss: 2.45822e-06	train's f1: 1	val's binary_logloss: 0.577547	val's f1: 0.854962
[2825]	train's binary_logloss: 2.45747e-0

[2924]	train's binary_logloss: 2.37798e-06	train's f1: 1	val's binary_logloss: 0.579155	val's f1: 0.854962
[2925]	train's binary_logloss: 2.37719e-06	train's f1: 1	val's binary_logloss: 0.579142	val's f1: 0.854962
[2926]	train's binary_logloss: 2.37592e-06	train's f1: 1	val's binary_logloss: 0.579051	val's f1: 0.854962
[2927]	train's binary_logloss: 2.37507e-06	train's f1: 1	val's binary_logloss: 0.578951	val's f1: 0.854962
[2928]	train's binary_logloss: 2.37425e-06	train's f1: 1	val's binary_logloss: 0.578943	val's f1: 0.854962
[2929]	train's binary_logloss: 2.37354e-06	train's f1: 1	val's binary_logloss: 0.579009	val's f1: 0.854962
[2930]	train's binary_logloss: 2.37262e-06	train's f1: 1	val's binary_logloss: 0.579026	val's f1: 0.854962
[2931]	train's binary_logloss: 2.37183e-06	train's f1: 1	val's binary_logloss: 0.57908	val's f1: 0.854962
[2932]	train's binary_logloss: 2.37119e-06	train's f1: 1	val's binary_logloss: 0.579045	val's f1: 0.854962
[2933]	train's binary_logloss: 2.36987

In [166]:
huvec_lgb_pred_protein = huvec_lgb_protein.predict(HUVECX_test,num_iteration=huvec_lgb_protein.best_iteration)
f1_score(HUVECy_test,prob2label(huvec_lgb_pred_protein))

0.8585526315789473

### Train LGB on NHEK

In [145]:
NHEKX_train = nhek_original_data_json['X_train_protein']
NHEKy_train = nhek_original_data_json['y_train_protein']
NHEKX_test = nhek_original_data_json['X_test_protein']
NHEKy_test = nhek_original_data_json['y_test_protein']

nhek_lgb_train_protein,nhek_lgb_valid_protein,nhek_lgb_test_protein = generate_lgb_use_data(NHEKX_train,
                                                                                            NHEKy_train,
                                                                                            NHEKX_test,
                                                                                            NHEKy_test)
nhek_lgb_protein = train_lgb(nhek_lgb_train_protein,nhek_lgb_valid_protein,
                             lgb_param,num_round+600,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.677758	train's f1: 0.820399	val's binary_logloss: 0.683438	val's f1: 0.71028
[2]	train's binary_logloss: 0.663127	train's f1: 0.852033	val's binary_logloss: 0.672471	val's f1: 0.752294
[3]	train's binary_logloss: 0.649263	train's f1: 0.866948	val's binary_logloss: 0.661768	val's f1: 0.747748
[4]	train's binary_logloss: 0.635819	train's f1: 0.86429	val's binary_logloss: 0.651058	val's f1: 0.791111
[5]	train's binary_logloss: 0.623161	train's f1: 0.87882	val's binary_logloss: 0.64198	val's f1: 0.789474
[6]	train's binary_logloss: 0.610936	train's f1: 0.88794	val's binary_logloss: 0.634752	val's f1: 0.782222
[7]	train's binary_logloss: 0.599587	train's f1: 0.889007	val's binary_logloss: 0.625795	val's f1: 0.792952
[8]	train's binary_logloss: 0.588191	train's f1: 0.891849	val's binary_logloss: 0.618551	val's f1: 0.791111
[9]	train's binary_logloss: 0.576558	train's f1: 0.894904	val's binary_logloss: 0.610198	val's f1: 0.803571
[10]	train's binary_logloss: 0.56

[85]	train's binary_logloss: 0.19438	train's f1: 0.991826	val's binary_logloss: 0.363831	val's f1: 0.891775
[86]	train's binary_logloss: 0.192091	train's f1: 0.991826	val's binary_logloss: 0.361817	val's f1: 0.887931
[87]	train's binary_logloss: 0.18977	train's f1: 0.992366	val's binary_logloss: 0.360609	val's f1: 0.895652
[88]	train's binary_logloss: 0.187645	train's f1: 0.992908	val's binary_logloss: 0.358703	val's f1: 0.891775
[89]	train's binary_logloss: 0.185233	train's f1: 0.993999	val's binary_logloss: 0.357033	val's f1: 0.895652
[90]	train's binary_logloss: 0.183127	train's f1: 0.99345	val's binary_logloss: 0.356634	val's f1: 0.887931
[91]	train's binary_logloss: 0.181039	train's f1: 0.99345	val's binary_logloss: 0.354379	val's f1: 0.895652
[92]	train's binary_logloss: 0.179113	train's f1: 0.993999	val's binary_logloss: 0.353467	val's f1: 0.895652
[93]	train's binary_logloss: 0.176827	train's f1: 0.993999	val's binary_logloss: 0.35151	val's f1: 0.895652
[94]	train's binary_logl

[167]	train's binary_logloss: 0.0788586	train's f1: 0.999455	val's binary_logloss: 0.290219	val's f1: 0.909091
[168]	train's binary_logloss: 0.0780802	train's f1: 0.999455	val's binary_logloss: 0.290188	val's f1: 0.909091
[169]	train's binary_logloss: 0.0772261	train's f1: 0.999455	val's binary_logloss: 0.289877	val's f1: 0.909091
[170]	train's binary_logloss: 0.0764515	train's f1: 0.999455	val's binary_logloss: 0.289301	val's f1: 0.909091
[171]	train's binary_logloss: 0.0756191	train's f1: 0.999455	val's binary_logloss: 0.288752	val's f1: 0.905172
[172]	train's binary_logloss: 0.074844	train's f1: 0.999455	val's binary_logloss: 0.28804	val's f1: 0.901288
[173]	train's binary_logloss: 0.0740826	train's f1: 0.999455	val's binary_logloss: 0.288108	val's f1: 0.905172
[174]	train's binary_logloss: 0.0732464	train's f1: 0.999455	val's binary_logloss: 0.287341	val's f1: 0.901288
[175]	train's binary_logloss: 0.0724531	train's f1: 0.999455	val's binary_logloss: 0.287071	val's f1: 0.901288
[17

[249]	train's binary_logloss: 0.0343756	train's f1: 1	val's binary_logloss: 0.268024	val's f1: 0.922414
[250]	train's binary_logloss: 0.034022	train's f1: 1	val's binary_logloss: 0.267529	val's f1: 0.922414
[251]	train's binary_logloss: 0.0336727	train's f1: 1	val's binary_logloss: 0.267414	val's f1: 0.922414
[252]	train's binary_logloss: 0.0333489	train's f1: 1	val's binary_logloss: 0.267234	val's f1: 0.922414
[253]	train's binary_logloss: 0.0330222	train's f1: 1	val's binary_logloss: 0.266943	val's f1: 0.922414
[254]	train's binary_logloss: 0.0327153	train's f1: 1	val's binary_logloss: 0.266625	val's f1: 0.922414
[255]	train's binary_logloss: 0.0323897	train's f1: 1	val's binary_logloss: 0.26655	val's f1: 0.922414
[256]	train's binary_logloss: 0.0320806	train's f1: 1	val's binary_logloss: 0.266337	val's f1: 0.922414
[257]	train's binary_logloss: 0.0317239	train's f1: 1	val's binary_logloss: 0.265588	val's f1: 0.922414
[258]	train's binary_logloss: 0.0313995	train's f1: 1	val's binary

[332]	train's binary_logloss: 0.0152568	train's f1: 1	val's binary_logloss: 0.260622	val's f1: 0.926407
[333]	train's binary_logloss: 0.015115	train's f1: 1	val's binary_logloss: 0.261101	val's f1: 0.930435
[334]	train's binary_logloss: 0.0149539	train's f1: 1	val's binary_logloss: 0.261265	val's f1: 0.930435
[335]	train's binary_logloss: 0.0148124	train's f1: 1	val's binary_logloss: 0.261365	val's f1: 0.930435
[336]	train's binary_logloss: 0.0146671	train's f1: 1	val's binary_logloss: 0.261452	val's f1: 0.926407
[337]	train's binary_logloss: 0.0145252	train's f1: 1	val's binary_logloss: 0.261999	val's f1: 0.930435
[338]	train's binary_logloss: 0.0143903	train's f1: 1	val's binary_logloss: 0.262447	val's f1: 0.930435
[339]	train's binary_logloss: 0.0142456	train's f1: 1	val's binary_logloss: 0.262349	val's f1: 0.930435
[340]	train's binary_logloss: 0.0141003	train's f1: 1	val's binary_logloss: 0.261729	val's f1: 0.930435
[341]	train's binary_logloss: 0.0139675	train's f1: 1	val's binar

...

[3249]	train's binary_logloss: 2.21115e-06	train's f1: 1	val's binary_logloss: 0.429053	val's f1: 0.929825
[3250]	train's binary_logloss: 2.21078e-06	train's f1: 1	val's binary_logloss: 0.429044	val's f1: 0.929825
[3251]	train's binary_logloss: 2.21015e-06	train's f1: 1	val's binary_logloss: 0.429049	val's f1: 0.929825
[3252]	train's binary_logloss: 2.20982e-06	train's f1: 1	val's binary_logloss: 0.429061	val's f1: 0.929825
[3253]	train's binary_logloss: 2.20936e-06	train's f1: 1	val's binary_logloss: 0.429111	val's f1: 0.929825
[3254]	train's binary_logloss: 2.20895e-06	train's f1: 1	val's binary_logloss: 0.429117	val's f1: 0.929825
[3255]	train's binary_logloss: 2.20856e-06	train's f1: 1	val's binary_logloss: 0.429067	val's f1: 0.929825
[3256]	train's binary_logloss: 2.20822e-06	train's f1: 1	val's binary_logloss: 0.429024	val's f1: 0.929825
[3257]	train's binary_logloss: 2.20782e-06	train's f1: 1	val's binary_logloss: 0.429078	val's f1: 0.929825
[3258]	train's binary_logloss: 2.2074

[3329]	train's binary_logloss: 2.17851e-06	train's f1: 1	val's binary_logloss: 0.429545	val's f1: 0.929825
[3330]	train's binary_logloss: 2.17815e-06	train's f1: 1	val's binary_logloss: 0.429517	val's f1: 0.929825
[3331]	train's binary_logloss: 2.1778e-06	train's f1: 1	val's binary_logloss: 0.429514	val's f1: 0.929825
[3332]	train's binary_logloss: 2.17742e-06	train's f1: 1	val's binary_logloss: 0.429541	val's f1: 0.929825
[3333]	train's binary_logloss: 2.17699e-06	train's f1: 1	val's binary_logloss: 0.429481	val's f1: 0.929825
[3334]	train's binary_logloss: 2.17645e-06	train's f1: 1	val's binary_logloss: 0.429465	val's f1: 0.929825
[3335]	train's binary_logloss: 2.176e-06	train's f1: 1	val's binary_logloss: 0.429482	val's f1: 0.929825
[3336]	train's binary_logloss: 2.17562e-06	train's f1: 1	val's binary_logloss: 0.429442	val's f1: 0.929825
[3337]	train's binary_logloss: 2.17504e-06	train's f1: 1	val's binary_logloss: 0.429489	val's f1: 0.929825
[3338]	train's binary_logloss: 2.17466e-

[3410]	train's binary_logloss: 2.14783e-06	train's f1: 1	val's binary_logloss: 0.429878	val's f1: 0.929825
[3411]	train's binary_logloss: 2.14746e-06	train's f1: 1	val's binary_logloss: 0.429899	val's f1: 0.929825
[3412]	train's binary_logloss: 2.14714e-06	train's f1: 1	val's binary_logloss: 0.429848	val's f1: 0.929825
[3413]	train's binary_logloss: 2.14677e-06	train's f1: 1	val's binary_logloss: 0.429805	val's f1: 0.929825
[3414]	train's binary_logloss: 2.14642e-06	train's f1: 1	val's binary_logloss: 0.429875	val's f1: 0.929825
[3415]	train's binary_logloss: 2.14603e-06	train's f1: 1	val's binary_logloss: 0.429897	val's f1: 0.929825
[3416]	train's binary_logloss: 2.14564e-06	train's f1: 1	val's binary_logloss: 0.429968	val's f1: 0.929825
[3417]	train's binary_logloss: 2.14532e-06	train's f1: 1	val's binary_logloss: 0.430026	val's f1: 0.929825
[3418]	train's binary_logloss: 2.14491e-06	train's f1: 1	val's binary_logloss: 0.430107	val's f1: 0.929825
[3419]	train's binary_logloss: 2.1445

[3491]	train's binary_logloss: 2.11847e-06	train's f1: 1	val's binary_logloss: 0.430705	val's f1: 0.929825
[3492]	train's binary_logloss: 2.11811e-06	train's f1: 1	val's binary_logloss: 0.43069	val's f1: 0.929825
[3493]	train's binary_logloss: 2.11777e-06	train's f1: 1	val's binary_logloss: 0.430679	val's f1: 0.929825
[3494]	train's binary_logloss: 2.11742e-06	train's f1: 1	val's binary_logloss: 0.430741	val's f1: 0.929825
[3495]	train's binary_logloss: 2.11704e-06	train's f1: 1	val's binary_logloss: 0.430754	val's f1: 0.929825
[3496]	train's binary_logloss: 2.11674e-06	train's f1: 1	val's binary_logloss: 0.430727	val's f1: 0.929825
[3497]	train's binary_logloss: 2.11641e-06	train's f1: 1	val's binary_logloss: 0.430721	val's f1: 0.929825
[3498]	train's binary_logloss: 2.11592e-06	train's f1: 1	val's binary_logloss: 0.430765	val's f1: 0.929825
[3499]	train's binary_logloss: 2.11553e-06	train's f1: 1	val's binary_logloss: 0.430716	val's f1: 0.929825
[3500]	train's binary_logloss: 2.11517

[3570]	train's binary_logloss: 2.09367e-06	train's f1: 1	val's binary_logloss: 0.431113	val's f1: 0.929825
[3571]	train's binary_logloss: 2.09326e-06	train's f1: 1	val's binary_logloss: 0.431141	val's f1: 0.929825
[3572]	train's binary_logloss: 2.09283e-06	train's f1: 1	val's binary_logloss: 0.431069	val's f1: 0.929825
[3573]	train's binary_logloss: 2.09243e-06	train's f1: 1	val's binary_logloss: 0.430999	val's f1: 0.929825
[3574]	train's binary_logloss: 2.09207e-06	train's f1: 1	val's binary_logloss: 0.430958	val's f1: 0.929825
[3575]	train's binary_logloss: 2.09172e-06	train's f1: 1	val's binary_logloss: 0.431011	val's f1: 0.929825
[3576]	train's binary_logloss: 2.09138e-06	train's f1: 1	val's binary_logloss: 0.431006	val's f1: 0.929825
[3577]	train's binary_logloss: 2.0913e-06	train's f1: 1	val's binary_logloss: 0.430981	val's f1: 0.929825
[3578]	train's binary_logloss: 2.09097e-06	train's f1: 1	val's binary_logloss: 0.431003	val's f1: 0.929825
[3579]	train's binary_logloss: 2.09054

In [146]:
nhek_lgb_pred_protein = nhek_lgb_protein.predict(NHEKX_test,num_iteration=nhek_lgb_protein.best_iteration)
f1_score(NHEKy_test,prob2label(nhek_lgb_pred_protein))

0.9120287253141832

### Train LGB On Hela-S3

In [172]:
HELAS3X_train = helas3_original_data_json['X_train_protein']
HELAS3y_train = helas3_original_data_json['y_train_protein']
HELAS3X_test = helas3_original_data_json['X_test_protein']
HELAS3y_test = helas3_original_data_json['y_test_protein']

helas3_lgb_train_protein,helas3_lgb_valid_protein,helas3_lgb_test_protein = generate_lgb_use_data(HELAS3X_train,
                                                                                            HELAS3y_train,
                                                                                            HELAS3X_test,
                                                                                            HELAS3y_test)

In [173]:
helas3_lgb_protein = train_lgb(helas3_lgb_train_protein,helas3_lgb_valid_protein,
                             lgb_param,num_round+600,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.679979	train's f1: 0.813912	val's binary_logloss: 0.684487	val's f1: 0.711974
[2]	train's binary_logloss: 0.667627	train's f1: 0.830943	val's binary_logloss: 0.676323	val's f1: 0.735786
[3]	train's binary_logloss: 0.655913	train's f1: 0.828673	val's binary_logloss: 0.668239	val's f1: 0.730496
[4]	train's binary_logloss: 0.643933	train's f1: 0.853136	val's binary_logloss: 0.659352	val's f1: 0.760563
[5]	train's binary_logloss: 0.633022	train's f1: 0.854467	val's binary_logloss: 0.652931	val's f1: 0.754448
[6]	train's binary_logloss: 0.622099	train's f1: 0.866068	val's binary_logloss: 0.646246	val's f1: 0.767606
[7]	train's binary_logloss: 0.610831	train's f1: 0.881594	val's binary_logloss: 0.638215	val's f1: 0.792982
[8]	train's binary_logloss: 0.6008	train's f1: 0.885658	val's binary_logloss: 0.631853	val's f1: 0.795848
[9]	train's binary_logloss: 0.590208	train's f1: 0.89185	val's binary_logloss: 0.623635	val's f1: 0.795848
[10]	train's binary_logloss: 0.

[77]	train's binary_logloss: 0.258842	train's f1: 0.97082	val's binary_logloss: 0.422884	val's f1: 0.833333
[78]	train's binary_logloss: 0.256291	train's f1: 0.972376	val's binary_logloss: 0.421112	val's f1: 0.833333
[79]	train's binary_logloss: 0.253737	train's f1: 0.972781	val's binary_logloss: 0.419207	val's f1: 0.837545
[80]	train's binary_logloss: 0.251223	train's f1: 0.974359	val's binary_logloss: 0.4176	val's f1: 0.837545
[81]	train's binary_logloss: 0.248936	train's f1: 0.975128	val's binary_logloss: 0.416784	val's f1: 0.841727
[82]	train's binary_logloss: 0.246437	train's f1: 0.975533	val's binary_logloss: 0.41539	val's f1: 0.841727
[83]	train's binary_logloss: 0.243907	train's f1: 0.975552	val's binary_logloss: 0.413694	val's f1: 0.841727
[84]	train's binary_logloss: 0.241498	train's f1: 0.975956	val's binary_logloss: 0.412043	val's f1: 0.83871
[85]	train's binary_logloss: 0.239071	train's f1: 0.976726	val's binary_logloss: 0.410297	val's f1: 0.83871
[86]	train's binary_loglo

[155]	train's binary_logloss: 0.127873	train's f1: 0.998815	val's binary_logloss: 0.348116	val's f1: 0.851986
[156]	train's binary_logloss: 0.12683	train's f1: 0.998419	val's binary_logloss: 0.34781	val's f1: 0.851986
[157]	train's binary_logloss: 0.125798	train's f1: 0.998815	val's binary_logloss: 0.347828	val's f1: 0.851986
[158]	train's binary_logloss: 0.124675	train's f1: 0.998815	val's binary_logloss: 0.347169	val's f1: 0.856115
[159]	train's binary_logloss: 0.123702	train's f1: 0.998815	val's binary_logloss: 0.346832	val's f1: 0.856115
[160]	train's binary_logloss: 0.122743	train's f1: 0.998815	val's binary_logloss: 0.346344	val's f1: 0.860215
[161]	train's binary_logloss: 0.121725	train's f1: 0.998815	val's binary_logloss: 0.345815	val's f1: 0.860215
[162]	train's binary_logloss: 0.120834	train's f1: 0.998815	val's binary_logloss: 0.345738	val's f1: 0.860215
[163]	train's binary_logloss: 0.119777	train's f1: 0.998815	val's binary_logloss: 0.345139	val's f1: 0.856115
[164]	train'

[233]	train's binary_logloss: 0.0686704	train's f1: 1	val's binary_logloss: 0.318802	val's f1: 0.879433
[234]	train's binary_logloss: 0.0681791	train's f1: 1	val's binary_logloss: 0.31838	val's f1: 0.876325
[235]	train's binary_logloss: 0.0676384	train's f1: 1	val's binary_logloss: 0.317863	val's f1: 0.876325
[236]	train's binary_logloss: 0.0671494	train's f1: 1	val's binary_logloss: 0.317059	val's f1: 0.879433
[237]	train's binary_logloss: 0.0666784	train's f1: 1	val's binary_logloss: 0.316934	val's f1: 0.879433
[238]	train's binary_logloss: 0.0661681	train's f1: 1	val's binary_logloss: 0.316709	val's f1: 0.879433
[239]	train's binary_logloss: 0.06572	train's f1: 1	val's binary_logloss: 0.316477	val's f1: 0.879433
[240]	train's binary_logloss: 0.06518	train's f1: 1	val's binary_logloss: 0.316242	val's f1: 0.879433
[241]	train's binary_logloss: 0.0647294	train's f1: 1	val's binary_logloss: 0.316621	val's f1: 0.879433
[242]	train's binary_logloss: 0.0643151	train's f1: 1	val's binary_lo

[324]	train's binary_logloss: 0.0345195	train's f1: 1	val's binary_logloss: 0.302831	val's f1: 0.88172
[325]	train's binary_logloss: 0.0342457	train's f1: 1	val's binary_logloss: 0.302846	val's f1: 0.88172
[326]	train's binary_logloss: 0.0339971	train's f1: 1	val's binary_logloss: 0.30236	val's f1: 0.88172
[327]	train's binary_logloss: 0.0337409	train's f1: 1	val's binary_logloss: 0.302331	val's f1: 0.88172
[328]	train's binary_logloss: 0.0334496	train's f1: 1	val's binary_logloss: 0.302292	val's f1: 0.88172
[329]	train's binary_logloss: 0.0331837	train's f1: 1	val's binary_logloss: 0.302246	val's f1: 0.88172
[330]	train's binary_logloss: 0.0329449	train's f1: 1	val's binary_logloss: 0.301854	val's f1: 0.88172
[331]	train's binary_logloss: 0.0326821	train's f1: 1	val's binary_logloss: 0.30224	val's f1: 0.88172
[332]	train's binary_logloss: 0.0324688	train's f1: 1	val's binary_logloss: 0.301655	val's f1: 0.88172
[333]	train's binary_logloss: 0.032223	train's f1: 1	val's binary_logloss: 

...

[3165]	train's binary_logloss: 2.11244e-06	train's f1: 1	val's binary_logloss: 0.566358	val's f1: 0.888087
[3166]	train's binary_logloss: 2.11147e-06	train's f1: 1	val's binary_logloss: 0.566342	val's f1: 0.888087
[3167]	train's binary_logloss: 2.111e-06	train's f1: 1	val's binary_logloss: 0.566428	val's f1: 0.891304
[3168]	train's binary_logloss: 2.1102e-06	train's f1: 1	val's binary_logloss: 0.566498	val's f1: 0.888087
[3169]	train's binary_logloss: 2.10923e-06	train's f1: 1	val's binary_logloss: 0.56643	val's f1: 0.888087
[3170]	train's binary_logloss: 2.10875e-06	train's f1: 1	val's binary_logloss: 0.5665	val's f1: 0.888087
[3171]	train's binary_logloss: 2.1081e-06	train's f1: 1	val's binary_logloss: 0.566534	val's f1: 0.888087
[3172]	train's binary_logloss: 2.10762e-06	train's f1: 1	val's binary_logloss: 0.566561	val's f1: 0.888087
[3173]	train's binary_logloss: 2.10714e-06	train's f1: 1	val's binary_logloss: 0.566576	val's f1: 0.888087
[3174]	train's binary_logloss: 2.10681e-06	t

[3276]	train's binary_logloss: 2.05214e-06	train's f1: 1	val's binary_logloss: 0.567992	val's f1: 0.891304
[3277]	train's binary_logloss: 2.05157e-06	train's f1: 1	val's binary_logloss: 0.56803	val's f1: 0.891304
[3278]	train's binary_logloss: 2.05115e-06	train's f1: 1	val's binary_logloss: 0.56793	val's f1: 0.891304
[3279]	train's binary_logloss: 2.05064e-06	train's f1: 1	val's binary_logloss: 0.567997	val's f1: 0.891304
[3280]	train's binary_logloss: 2.05006e-06	train's f1: 1	val's binary_logloss: 0.567905	val's f1: 0.891304
[3281]	train's binary_logloss: 2.04933e-06	train's f1: 1	val's binary_logloss: 0.567935	val's f1: 0.891304
[3282]	train's binary_logloss: 2.04877e-06	train's f1: 1	val's binary_logloss: 0.568022	val's f1: 0.891304
[3283]	train's binary_logloss: 2.04819e-06	train's f1: 1	val's binary_logloss: 0.56791	val's f1: 0.891304
[3284]	train's binary_logloss: 2.04774e-06	train's f1: 1	val's binary_logloss: 0.567855	val's f1: 0.891304
[3285]	train's binary_logloss: 2.0472e-0

[3353]	train's binary_logloss: 2.01348e-06	train's f1: 1	val's binary_logloss: 0.5688	val's f1: 0.891304
[3354]	train's binary_logloss: 2.01304e-06	train's f1: 1	val's binary_logloss: 0.568764	val's f1: 0.891304
[3355]	train's binary_logloss: 2.01249e-06	train's f1: 1	val's binary_logloss: 0.568778	val's f1: 0.891304
[3356]	train's binary_logloss: 2.01199e-06	train's f1: 1	val's binary_logloss: 0.568701	val's f1: 0.891304
[3357]	train's binary_logloss: 2.01147e-06	train's f1: 1	val's binary_logloss: 0.568749	val's f1: 0.891304
[3358]	train's binary_logloss: 2.01088e-06	train's f1: 1	val's binary_logloss: 0.56872	val's f1: 0.891304
[3359]	train's binary_logloss: 2.0104e-06	train's f1: 1	val's binary_logloss: 0.568698	val's f1: 0.891304
[3360]	train's binary_logloss: 2.00998e-06	train's f1: 1	val's binary_logloss: 0.568694	val's f1: 0.891304
[3361]	train's binary_logloss: 2.00949e-06	train's f1: 1	val's binary_logloss: 0.568748	val's f1: 0.891304
[3362]	train's binary_logloss: 2.00923e-0

[3431]	train's binary_logloss: 1.97767e-06	train's f1: 1	val's binary_logloss: 0.569967	val's f1: 0.891304
[3432]	train's binary_logloss: 1.97715e-06	train's f1: 1	val's binary_logloss: 0.569904	val's f1: 0.891304
[3433]	train's binary_logloss: 1.9769e-06	train's f1: 1	val's binary_logloss: 0.569893	val's f1: 0.891304
[3434]	train's binary_logloss: 1.97639e-06	train's f1: 1	val's binary_logloss: 0.569899	val's f1: 0.891304
[3435]	train's binary_logloss: 1.97615e-06	train's f1: 1	val's binary_logloss: 0.569912	val's f1: 0.891304
[3436]	train's binary_logloss: 1.97562e-06	train's f1: 1	val's binary_logloss: 0.569929	val's f1: 0.891304
[3437]	train's binary_logloss: 1.97505e-06	train's f1: 1	val's binary_logloss: 0.569903	val's f1: 0.891304
[3438]	train's binary_logloss: 1.97452e-06	train's f1: 1	val's binary_logloss: 0.569944	val's f1: 0.891304
[3439]	train's binary_logloss: 1.97396e-06	train's f1: 1	val's binary_logloss: 0.569943	val's f1: 0.891304
[3440]	train's binary_logloss: 1.97281

[3509]	train's binary_logloss: 1.94137e-06	train's f1: 1	val's binary_logloss: 0.571002	val's f1: 0.891304
[3510]	train's binary_logloss: 1.94093e-06	train's f1: 1	val's binary_logloss: 0.571093	val's f1: 0.891304
[3511]	train's binary_logloss: 1.9407e-06	train's f1: 1	val's binary_logloss: 0.571129	val's f1: 0.891304
[3512]	train's binary_logloss: 1.94003e-06	train's f1: 1	val's binary_logloss: 0.571142	val's f1: 0.891304
[3513]	train's binary_logloss: 1.93967e-06	train's f1: 1	val's binary_logloss: 0.571169	val's f1: 0.891304
[3514]	train's binary_logloss: 1.93917e-06	train's f1: 1	val's binary_logloss: 0.571123	val's f1: 0.891304
[3515]	train's binary_logloss: 1.93869e-06	train's f1: 1	val's binary_logloss: 0.571062	val's f1: 0.891304
[3516]	train's binary_logloss: 1.93839e-06	train's f1: 1	val's binary_logloss: 0.571115	val's f1: 0.891304
[3517]	train's binary_logloss: 1.93814e-06	train's f1: 1	val's binary_logloss: 0.571128	val's f1: 0.891304
[3518]	train's binary_logloss: 1.93787

In [174]:
helas3_lgb_pred_protein = helas3_lgb_protein.predict(HELAS3X_test,num_iteration=helas3_lgb_protein.best_iteration)
f1_score(HELAS3y_test,prob2label(helas3_lgb_pred_protein))

0.8920454545454546

## SVM

In [259]:
k562_svm_protein = svm(k562X_train,k562y_train,None,None)
imr90_svm_protein = svm(IMR90X_train,IMR90y_train,None,None)
gm12878_svm_protein = svm(GM12878X_train,GM12878y_train,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [260]:
huvec_svm_protein = svm(HUVECX_train,HUVECy_train,None,None)
nhek_svm_protein = svm(NHEKX_train,NHEKy_train,None,None)
helas3_svm_protein = svm(HELAS3X_train,HELAS3y_train,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [261]:
k562_svm_pred_ptotein = k562_svm_protein.predict(k562X_test)
f1_score(k562y_test,k562_svm_pred_ptotein)

0.6801099908340971

In [262]:
imr90_svm_pred_ptotein = imr90_svm_protein.predict(IMR90X_test)
f1_score(IMR90y_test,imr90_svm_pred_ptotein)

0.6255259467040674

In [263]:
gm12878_svm_pred_ptotein = gm12878_svm_protein.predict(GM12878X_test)
f1_score(GM12878y_test,gm12878_svm_pred_ptotein)

0.6974716652136007

In [264]:
huvec_svm_pred_ptotein = huvec_svm_protein.predict(HUVECX_test)
f1_score(HUVECy_test,huvec_svm_pred_ptotein)

0.5987261146496815

In [265]:
nhek_svm_pred_ptotein = nhek_svm_protein.predict(NHEKX_test)
f1_score(NHEKy_test,nhek_svm_pred_ptotein)

0.6493150684931506

In [266]:
helas3_svm_pred_ptotein = helas3_svm_protein.predict(HELAS3X_test)
f1_score(HELAS3y_test,helas3_svm_pred_ptotein)

0.6595538312318138

## Adaboost

In [267]:
k562_ada_protein = adaboost(k562X_train,k562y_train,None,None)
imr90_ada_protein = adaboost(IMR90X_train,IMR90y_train,None,None)
gm12878_ada_protein = adaboost(GM12878X_train,GM12878y_train,None,None)

In [268]:
huvec_ada_protein = adaboost(HUVECX_train,HUVECy_train,None,None)
nhek_ada_protein = adaboost(NHEKX_train,NHEKy_train,None,None)
helas3_ada_protein = adaboost(HELAS3X_train,HELAS3y_train,None,None)

In [269]:
k562_ada_pred_ptotein = k562_ada_protein.predict(k562X_test)
f1_score(k562y_test,k562_ada_pred_ptotein)

0.8362369337979093

In [270]:
imr90_ada_pred_ptotein = imr90_ada_protein.predict(IMR90X_test)
f1_score(IMR90y_test,imr90_ada_pred_ptotein)

0.7864271457085829

In [271]:
gm12878_ada_pred_ptotein = gm12878_ada_protein.predict(GM12878X_test)
f1_score(GM12878y_test,gm12878_ada_pred_ptotein)

0.7999999999999999

In [272]:
huvec_ada_pred_ptotein = huvec_ada_protein.predict(HUVECX_test)
f1_score(HUVECy_test,huvec_ada_pred_ptotein)

0.7974683544303798

In [273]:
nhek_ada_pred_ptotein = nhek_ada_protein.predict(NHEKX_test)
f1_score(NHEKy_test,nhek_ada_pred_ptotein)

0.8596491228070174

In [274]:
helas3_ada_pred_ptotein = helas3_ada_protein.predict(HELAS3X_test)
f1_score(HELAS3y_test,helas3_ada_pred_ptotein)

0.8422535211267604

# Save Protein Model and Data

## Save Model

In [175]:
k562_lgb_protein.save_model('./model/LGB/k562_protein_lgb.txt', num_iteration=k562_lgb_protein.best_iteration)
imr90_lgb_protein.save_model('./model/LGB/img90_protein_lgb.txt', num_iteration=imr90_lgb_protein.best_iteration)
gm12878_lgb_protein.save_model('./model/LGB/gm12878_protein_lgb.txt', num_iteration=gm12878_lgb_protein.best_iteration)

In [176]:
huvec_lgb_protein.save_model('./model/LGB/huvec_protein_lgb.txt', num_iteration=huvec_lgb_protein.best_iteration)
nhek_lgb_protein.save_model('./model/LGB/nhek_protein_lgb.txt', num_iteration=nhek_lgb_protein.best_iteration)
helas3_lgb_protein.save_model('./model/LGB/helas3_protein_lgb.txt', num_iteration=helas3_lgb_protein.best_iteration)

In [275]:
joblib.dump(k562_svm_protein,'./model/RF/k562_svm_protein.model')
joblib.dump(imr90_svm_protein,'./model/RF/imr90_svm_protein.model')
joblib.dump(gm12878_svm_protein,'./model/RF/gm12878_svm_protein.model')

['./model/RF/gm12878_svm_protein.model']

In [276]:
joblib.dump(huvec_svm_protein,'./model/RF/huvec_svm_protein.model')
joblib.dump(nhek_svm_protein,'./model/RF/nhek_svm_protein.model')
joblib.dump(helas3_svm_protein,'./model/RF/helas3_svm_protein.model')

['./model/RF/helas3_svm_protein.model']

In [277]:
joblib.dump(k562_ada_protein,'./model/Adaboost/k562_ada_protein.model')
joblib.dump(imr90_ada_protein,'./model/Adaboost/imr90_ada_protein.model')
joblib.dump(gm12878_ada_protein,'./model/Adaboost/gm12878_ada_protein.model')

['./model/Adaboost/gm12878_ada_protein.model']

In [278]:
joblib.dump(huvec_ada_protein,'./model/Adaboost/huvec_ada_protein.model')
joblib.dump(nhek_ada_protein,'./model/Adaboost/nhek_ada_protein.model')
joblib.dump(helas3_ada_protein,'./model/Adaboost/helas3_ada_protein.model')

['./model/Adaboost/helas3_ada_protein.model']

## Save Data

In [177]:
pickle.dump(k562_original_data_json,open('./mid-data/K562/k562_original_data_json.pkl','wb'))

#pickle.dump(k562,open('./mid-data/K562/k562.pkl','wb'))
#pickle.dump(k562X_train,open('./mid-data/K562/K562X_train.pkl','wb'))
#pickle.dump(k562y_train,open('./mid-data/K562/K562y_train.pkl','wb'))
#pickle.dump(k562X_test,open('./mid-data/K562/K562X_test.pkl','wb'))
#pickle.dump(k562y_test,open('./mid-data/K562/K562y_test.pkl','wb'))
#k562_lgb_train_protein.save_binary('./mid-data/K562/k562_lgb_train_protein.bin')
#k562_lgb_valid_protein.save_binary('./mid-data/K562/k562_lgb_valid_protein.bin')

In [178]:
pickle.dump(gm12878_original_data_json,open('./mid-data/GM12878/gm12878_original_data_json.pkl','wb'))

#pickle.dump(GM12878,open('./mid-data/GM12878/GM12878.pkl','wb'))
#pickle.dump(GM12878X_train,open('./mid-data/GM12878/GM12878X_train.pkl','wb'))
#pickle.dump(GM12878y_train,open('./mid-data/GM12878/GM12878y_train.pkl','wb'))
#pickle.dump(GM12878X_test,open('./mid-data/GM12878/GM12878X_test.pkl','wb'))
#pickle.dump(GM12878y_test,open('./mid-data/GM12878/GM12878y_test.pkl','wb'))
#gm12878_lgb_train_protein.save_binary('./mid-data/GM12878/gm12878_lgb_train_protein.bin')
#gm12878_lgb_valid_protein.save_binary('./mid-data/GM12878/gm12878_lgb_valid_protein.bin')

In [179]:
pickle.dump(imr90_original_data_json,open('./mid-data/IMR90/imr90_original_data_json.pkl','wb'))

#pickle.dump(IMR90,open('./mid-data/IMR90/IMR90.pkl','wb'))
#pickle.dump(IMR90X_train,open('./mid-data/IMR90/IMR90X_train.pkl','wb'))
#pickle.dump(IMR90y_train,open('./mid-data/IMR90/IMR90y_train.pkl','wb'))
#pickle.dump(IMR90X_test,open('./mid-data/IMR90/IMR90X_test.pkl','wb'))
#pickle.dump(IMR90y_test,open('./mid-data/IMR90/IMR90y_test.pkl','wb'))
#imr90_lgb_train_protein.save_binary('./mid-data/IMR90/imr90_lgb_train_protein.bin')
#imr90_lgb_valid_protein.save_binary('./mid-data/IMR90/imr90_lgb_valid_protein.bin')

In [180]:
pickle.dump(huvec_original_data_json,open('./mid-data/HUVEC/huvec_original_data_json.pkl','wb'))

#pickle.dump(HUVEC,open('./mid-data/HUVEC/HUVEC.pkl','wb'))
#pickle.dump(HUVECX_train,open('./mid-data/HUVEC/HUVECX_train.pkl','wb'))
#pickle.dump(HUVECy_train,open('./mid-data/HUVEC/HUVECy_train.pkl','wb'))
#pickle.dump(HUVECX_test,open('./mid-data/HUVEC/HUVECX_test.pkl','wb'))
#pickle.dump(HUVECy_test,open('./mid-data/HUVEC/HUVECy_test.pkl','wb'))
#huvec_lgb_train_protein.save_binary('./mid-data/HUVEC/huvec_lgb_train_protein.bin')
#huvec_lgb_valid_protein.save_binary('./mid-data/HUVEC/huvec_lgb_valid_protein.bin')

In [181]:
pickle.dump(nhek_original_data_json,open('./mid-data/NHEK/nhek_original_data_json.pkl','wb'))

In [182]:
pickle.dump(helas3_original_data_json,open('./mid-data/HELAS3/helas3_original_data_json.pkl','wb'))

#pickle.dump(HELAS3,open('./mid-data/HELAS3/HELAS3.pkl','wb'))
#pickle.dump(HELAS3X_train,open('./mid-data/HELAS3/HELAS3X_train.pkl','wb'))
#pickle.dump(HELAS3y_train,open('./mid-data/HELAS3/HELAS3y_train.pkl','wb'))
#pickle.dump(HELAS3X_test,open('./mid-data/HELAS3/HELAS3X_test.pkl','wb'))
#pickle.dump(HELAS3y_test,open('./mid-data/HELAS3/HELAS3y_test.pkl','wb'))
#helas3_lgb_train_protein.save_binary('./mid-data/HELAS3/helas3_lgb_train_protein.bin')
#helas3_lgb_valid_protein.save_binary('./mid-data/HELAS3/helas3_lgb_valid_protein.bin')

* ##############################################################################################################################

# Use Sequence

## LGB

### k562

In [183]:
k562_seq_train_x = k562_original_data_json['X_train_seq']
k562_seq_train_y = k562_original_data_json['y_train_seq']

k562_seq_test_x  = k562_original_data_json['X_test_seq']
k562_seq_test_y = k562_original_data_json['y_test_seq']

k562_seq_train_lgb,k562_seq_valid_lgb,_ = generate_lgb_use_data(k562_seq_train_x,
                                                               k562_seq_train_y,
                                                               k562_seq_test_x,
                                                               k562_seq_test_y)

In [184]:
k562_lgb_seq = train_lgb(k562_seq_train_lgb,k562_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.686264	train's f1: 0.67136	val's binary_logloss: 0.68717	val's f1: 0.666667
[2]	train's binary_logloss: 0.680005	train's f1: 0.710266	val's binary_logloss: 0.68419	val's f1: 0.602649
[3]	train's binary_logloss: 0.673814	train's f1: 0.734293	val's binary_logloss: 0.679111	val's f1: 0.656347
[4]	train's binary_logloss: 0.667675	train's f1: 0.756132	val's binary_logloss: 0.675886	val's f1: 0.660606
[5]	train's binary_logloss: 0.66152	train's f1: 0.776692	val's binary_logloss: 0.671436	val's f1: 0.672673
[6]	train's binary_logloss: 0.656032	train's f1: 0.785092	val's binary_logloss: 0.666714	val's f1: 0.688623
[7]	train's binary_logloss: 0.650137	train's f1: 0.785589	val's binary_logloss: 0.662638	val's f1: 0.672727
[8]	train's binary_logloss: 0.644622	train's f1: 0.789197	val's binary_logloss: 0.658564	val's f1: 0.674847
[9]	train's binary_logloss: 0.639408	train's f1: 0.796491	val's binary_logloss: 0.654307	val's f1: 0.683077
[10]	train's binary_logloss: 0.6

[97]	train's binary_logloss: 0.38164	train's f1: 0.968717	val's binary_logloss: 0.546911	val's f1: 0.738095
[98]	train's binary_logloss: 0.37991	train's f1: 0.968739	val's binary_logloss: 0.546083	val's f1: 0.732733
[99]	train's binary_logloss: 0.378172	train's f1: 0.969442	val's binary_logloss: 0.546295	val's f1: 0.734328
[100]	train's binary_logloss: 0.376354	train's f1: 0.969484	val's binary_logloss: 0.546214	val's f1: 0.730539
[101]	train's binary_logloss: 0.374474	train's f1: 0.970165	val's binary_logloss: 0.545961	val's f1: 0.734328
[102]	train's binary_logloss: 0.372795	train's f1: 0.969442	val's binary_logloss: 0.545067	val's f1: 0.738095
[103]	train's binary_logloss: 0.370867	train's f1: 0.969782	val's binary_logloss: 0.545027	val's f1: 0.738095
[104]	train's binary_logloss: 0.36911	train's f1: 0.970805	val's binary_logloss: 0.544727	val's f1: 0.732143
[105]	train's binary_logloss: 0.367387	train's f1: 0.971529	val's binary_logloss: 0.543704	val's f1: 0.72997
[106]	train's bin

[194]	train's binary_logloss: 0.250151	train's f1: 0.99506	val's binary_logloss: 0.511125	val's f1: 0.755287
[195]	train's binary_logloss: 0.249057	train's f1: 0.995411	val's binary_logloss: 0.510694	val's f1: 0.755287
[196]	train's binary_logloss: 0.248116	train's f1: 0.995411	val's binary_logloss: 0.510088	val's f1: 0.755287
[197]	train's binary_logloss: 0.247077	train's f1: 0.995411	val's binary_logloss: 0.509534	val's f1: 0.751515
[198]	train's binary_logloss: 0.246156	train's f1: 0.995056	val's binary_logloss: 0.509509	val's f1: 0.751515
[199]	train's binary_logloss: 0.245126	train's f1: 0.995411	val's binary_logloss: 0.509494	val's f1: 0.755287
[200]	train's binary_logloss: 0.243824	train's f1: 0.995411	val's binary_logloss: 0.509112	val's f1: 0.755287
[201]	train's binary_logloss: 0.243037	train's f1: 0.995763	val's binary_logloss: 0.508777	val's f1: 0.755287
[202]	train's binary_logloss: 0.241908	train's f1: 0.996114	val's binary_logloss: 0.508406	val's f1: 0.755287
[203]	train

[289]	train's binary_logloss: 0.169199	train's f1: 0.999295	val's binary_logloss: 0.489986	val's f1: 0.765957
[290]	train's binary_logloss: 0.168673	train's f1: 0.999295	val's binary_logloss: 0.490089	val's f1: 0.765957
[291]	train's binary_logloss: 0.168051	train's f1: 0.999295	val's binary_logloss: 0.49004	val's f1: 0.762195
[292]	train's binary_logloss: 0.16736	train's f1: 0.999295	val's binary_logloss: 0.489755	val's f1: 0.75841
[293]	train's binary_logloss: 0.166782	train's f1: 0.999295	val's binary_logloss: 0.489642	val's f1: 0.75841
[294]	train's binary_logloss: 0.16611	train's f1: 0.999295	val's binary_logloss: 0.489616	val's f1: 0.760736
[295]	train's binary_logloss: 0.165346	train's f1: 0.999295	val's binary_logloss: 0.489391	val's f1: 0.760736
[296]	train's binary_logloss: 0.164707	train's f1: 0.999295	val's binary_logloss: 0.489738	val's f1: 0.763077
[297]	train's binary_logloss: 0.163876	train's f1: 0.999295	val's binary_logloss: 0.4897	val's f1: 0.760736
[298]	train's bin

[385]	train's binary_logloss: 0.116226	train's f1: 0.999295	val's binary_logloss: 0.480443	val's f1: 0.76161
[386]	train's binary_logloss: 0.115814	train's f1: 0.999295	val's binary_logloss: 0.480482	val's f1: 0.76161
[387]	train's binary_logloss: 0.115378	train's f1: 0.999295	val's binary_logloss: 0.480219	val's f1: 0.76161
[388]	train's binary_logloss: 0.114852	train's f1: 0.999295	val's binary_logloss: 0.480286	val's f1: 0.759259
[389]	train's binary_logloss: 0.114487	train's f1: 0.999295	val's binary_logloss: 0.48037	val's f1: 0.759259
[390]	train's binary_logloss: 0.114086	train's f1: 0.999295	val's binary_logloss: 0.480239	val's f1: 0.759259
[391]	train's binary_logloss: 0.113711	train's f1: 0.999647	val's binary_logloss: 0.480333	val's f1: 0.759259
[392]	train's binary_logloss: 0.113255	train's f1: 0.999647	val's binary_logloss: 0.4805	val's f1: 0.757764
[393]	train's binary_logloss: 0.112636	train's f1: 0.999647	val's binary_logloss: 0.479802	val's f1: 0.759259
[394]	train's bi

...

[2629]	train's binary_logloss: 3.1302e-05	train's f1: 1	val's binary_logloss: 0.686011	val's f1: 0.74375
[2630]	train's binary_logloss: 3.11859e-05	train's f1: 1	val's binary_logloss: 0.686518	val's f1: 0.739812
[2631]	train's binary_logloss: 3.10694e-05	train's f1: 1	val's binary_logloss: 0.686639	val's f1: 0.739812
[2632]	train's binary_logloss: 3.09492e-05	train's f1: 1	val's binary_logloss: 0.687173	val's f1: 0.739812
[2633]	train's binary_logloss: 3.08303e-05	train's f1: 1	val's binary_logloss: 0.687408	val's f1: 0.739812
[2634]	train's binary_logloss: 3.07158e-05	train's f1: 1	val's binary_logloss: 0.687561	val's f1: 0.739812
[2635]	train's binary_logloss: 3.05864e-05	train's f1: 1	val's binary_logloss: 0.687982	val's f1: 0.74375
[2636]	train's binary_logloss: 3.04829e-05	train's f1: 1	val's binary_logloss: 0.687745	val's f1: 0.74375
[2637]	train's binary_logloss: 3.03879e-05	train's f1: 1	val's binary_logloss: 0.688245	val's f1: 0.746082
[2638]	train's binary_logloss: 3.02868e-0

[2716]	train's binary_logloss: 2.28129e-05	train's f1: 1	val's binary_logloss: 0.697441	val's f1: 0.744479
[2717]	train's binary_logloss: 2.27393e-05	train's f1: 1	val's binary_logloss: 0.69756	val's f1: 0.744479
[2718]	train's binary_logloss: 2.26546e-05	train's f1: 1	val's binary_logloss: 0.69783	val's f1: 0.744479
[2719]	train's binary_logloss: 2.25788e-05	train's f1: 1	val's binary_logloss: 0.697737	val's f1: 0.744479
[2720]	train's binary_logloss: 2.24834e-05	train's f1: 1	val's binary_logloss: 0.697512	val's f1: 0.744479
[2721]	train's binary_logloss: 2.24085e-05	train's f1: 1	val's binary_logloss: 0.697981	val's f1: 0.744479
[2722]	train's binary_logloss: 2.23243e-05	train's f1: 1	val's binary_logloss: 0.698483	val's f1: 0.744479
[2723]	train's binary_logloss: 2.22376e-05	train's f1: 1	val's binary_logloss: 0.698474	val's f1: 0.744479
[2724]	train's binary_logloss: 2.21626e-05	train's f1: 1	val's binary_logloss: 0.698636	val's f1: 0.744479
[2725]	train's binary_logloss: 2.20868e

[2803]	train's binary_logloss: 1.68959e-05	train's f1: 1	val's binary_logloss: 0.707849	val's f1: 0.750789
[2804]	train's binary_logloss: 1.68332e-05	train's f1: 1	val's binary_logloss: 0.707834	val's f1: 0.750789
[2805]	train's binary_logloss: 1.67802e-05	train's f1: 1	val's binary_logloss: 0.70776	val's f1: 0.750789
[2806]	train's binary_logloss: 1.67217e-05	train's f1: 1	val's binary_logloss: 0.707973	val's f1: 0.750789
[2807]	train's binary_logloss: 1.66713e-05	train's f1: 1	val's binary_logloss: 0.70815	val's f1: 0.750789
[2808]	train's binary_logloss: 1.66152e-05	train's f1: 1	val's binary_logloss: 0.708376	val's f1: 0.750789
[2809]	train's binary_logloss: 1.65587e-05	train's f1: 1	val's binary_logloss: 0.707879	val's f1: 0.750789
[2810]	train's binary_logloss: 1.65019e-05	train's f1: 1	val's binary_logloss: 0.708149	val's f1: 0.750789
[2811]	train's binary_logloss: 1.64499e-05	train's f1: 1	val's binary_logloss: 0.708661	val's f1: 0.750789
[2812]	train's binary_logloss: 1.63908e

[2885]	train's binary_logloss: 1.30031e-05	train's f1: 1	val's binary_logloss: 0.720198	val's f1: 0.754717
[2886]	train's binary_logloss: 1.29683e-05	train's f1: 1	val's binary_logloss: 0.719805	val's f1: 0.754717
[2887]	train's binary_logloss: 1.29294e-05	train's f1: 1	val's binary_logloss: 0.719654	val's f1: 0.754717
[2888]	train's binary_logloss: 1.28936e-05	train's f1: 1	val's binary_logloss: 0.720151	val's f1: 0.754717
[2889]	train's binary_logloss: 1.28541e-05	train's f1: 1	val's binary_logloss: 0.720287	val's f1: 0.754717
[2890]	train's binary_logloss: 1.2822e-05	train's f1: 1	val's binary_logloss: 0.720924	val's f1: 0.754717
[2891]	train's binary_logloss: 1.27865e-05	train's f1: 1	val's binary_logloss: 0.721203	val's f1: 0.754717
[2892]	train's binary_logloss: 1.275e-05	train's f1: 1	val's binary_logloss: 0.721537	val's f1: 0.754717
[2893]	train's binary_logloss: 1.27183e-05	train's f1: 1	val's binary_logloss: 0.721907	val's f1: 0.752351
[2894]	train's binary_logloss: 1.2689e-0

[2966]	train's binary_logloss: 1.06747e-05	train's f1: 1	val's binary_logloss: 0.728231	val's f1: 0.75
[2967]	train's binary_logloss: 1.06517e-05	train's f1: 1	val's binary_logloss: 0.728553	val's f1: 0.75
[2968]	train's binary_logloss: 1.06275e-05	train's f1: 1	val's binary_logloss: 0.728572	val's f1: 0.752351
[2969]	train's binary_logloss: 1.05984e-05	train's f1: 1	val's binary_logloss: 0.728997	val's f1: 0.75
[2970]	train's binary_logloss: 1.0575e-05	train's f1: 1	val's binary_logloss: 0.729412	val's f1: 0.75
[2971]	train's binary_logloss: 1.05542e-05	train's f1: 1	val's binary_logloss: 0.729729	val's f1: 0.752351
[2972]	train's binary_logloss: 1.05319e-05	train's f1: 1	val's binary_logloss: 0.729892	val's f1: 0.752351
[2973]	train's binary_logloss: 1.0507e-05	train's f1: 1	val's binary_logloss: 0.729956	val's f1: 0.752351
[2974]	train's binary_logloss: 1.04882e-05	train's f1: 1	val's binary_logloss: 0.73026	val's f1: 0.752351
[2975]	train's binary_logloss: 1.04684e-05	train's f1: 1

In [185]:
k562_lgb_pred_seq = k562_lgb_seq.predict(k562_seq_test_x)
f1_score(k562_seq_test_y,prob2label(k562_lgb_pred_seq))

0.7652811735941321

### IMR90

In [186]:
imr90_seq_train_x = imr90_original_data_json['X_train_seq']
imr90_seq_train_y = imr90_original_data_json['y_train_seq']

imr90_seq_test_x  = imr90_original_data_json['X_test_seq']
imr90_seq_test_y = imr90_original_data_json['y_test_seq']

imr90_seq_train_lgb,imr90_seq_valid_lgb,_ = generate_lgb_use_data(imr90_seq_train_x,
                                                               imr90_seq_train_y,
                                                               imr90_seq_test_x,
                                                               imr90_seq_test_y)

In [187]:
imr90_lgb_seq = train_lgb(imr90_seq_train_lgb,imr90_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.683074	train's f1: 0.774707	val's binary_logloss: 0.687154	val's f1: 0.691358
[2]	train's binary_logloss: 0.673615	train's f1: 0.801502	val's binary_logloss: 0.682405	val's f1: 0.703557
[3]	train's binary_logloss: 0.66402	train's f1: 0.829839	val's binary_logloss: 0.678591	val's f1: 0.710744
[4]	train's binary_logloss: 0.655236	train's f1: 0.842105	val's binary_logloss: 0.675776	val's f1: 0.686192
[5]	train's binary_logloss: 0.646666	train's f1: 0.860072	val's binary_logloss: 0.674069	val's f1: 0.706383
[6]	train's binary_logloss: 0.637906	train's f1: 0.872329	val's binary_logloss: 0.669784	val's f1: 0.695652
[7]	train's binary_logloss: 0.629795	train's f1: 0.881374	val's binary_logloss: 0.668479	val's f1: 0.69869
[8]	train's binary_logloss: 0.62187	train's f1: 0.877871	val's binary_logloss: 0.666831	val's f1: 0.684444
[9]	train's binary_logloss: 0.613918	train's f1: 0.889355	val's binary_logloss: 0.663228	val's f1: 0.684685
[10]	train's binary_logloss: 0.

[81]	train's binary_logloss: 0.324842	train's f1: 0.986361	val's binary_logloss: 0.572428	val's f1: 0.72
[82]	train's binary_logloss: 0.322406	train's f1: 0.985823	val's binary_logloss: 0.572338	val's f1: 0.714286
[83]	train's binary_logloss: 0.319837	train's f1: 0.986361	val's binary_logloss: 0.571665	val's f1: 0.713656
[84]	train's binary_logloss: 0.3177	train's f1: 0.986376	val's binary_logloss: 0.570852	val's f1: 0.713656
[85]	train's binary_logloss: 0.31558	train's f1: 0.986376	val's binary_logloss: 0.5694	val's f1: 0.713656
[86]	train's binary_logloss: 0.313417	train's f1: 0.987452	val's binary_logloss: 0.569424	val's f1: 0.716814
[87]	train's binary_logloss: 0.311405	train's f1: 0.987991	val's binary_logloss: 0.569924	val's f1: 0.711111
[88]	train's binary_logloss: 0.309188	train's f1: 0.989095	val's binary_logloss: 0.568159	val's f1: 0.711111
[89]	train's binary_logloss: 0.306867	train's f1: 0.988004	val's binary_logloss: 0.566508	val's f1: 0.711111
[90]	train's binary_logloss:

[159]	train's binary_logloss: 0.188822	train's f1: 0.999453	val's binary_logloss: 0.530191	val's f1: 0.787611
[160]	train's binary_logloss: 0.187519	train's f1: 0.999453	val's binary_logloss: 0.528933	val's f1: 0.787611
[161]	train's binary_logloss: 0.186424	train's f1: 0.999453	val's binary_logloss: 0.528315	val's f1: 0.778761
[162]	train's binary_logloss: 0.185245	train's f1: 0.999453	val's binary_logloss: 0.528812	val's f1: 0.782222
[163]	train's binary_logloss: 0.184258	train's f1: 0.999453	val's binary_logloss: 0.528611	val's f1: 0.787611
[164]	train's binary_logloss: 0.183139	train's f1: 0.999453	val's binary_logloss: 0.529045	val's f1: 0.787611
[165]	train's binary_logloss: 0.181862	train's f1: 0.999453	val's binary_logloss: 0.528538	val's f1: 0.780702
[166]	train's binary_logloss: 0.180624	train's f1: 0.999453	val's binary_logloss: 0.527596	val's f1: 0.780702
[167]	train's binary_logloss: 0.179491	train's f1: 0.999453	val's binary_logloss: 0.527575	val's f1: 0.778761
[168]	trai

[239]	train's binary_logloss: 0.114927	train's f1: 1	val's binary_logloss: 0.50386	val's f1: 0.791304
[240]	train's binary_logloss: 0.114039	train's f1: 1	val's binary_logloss: 0.503768	val's f1: 0.791304
[241]	train's binary_logloss: 0.113396	train's f1: 1	val's binary_logloss: 0.503578	val's f1: 0.796537
[242]	train's binary_logloss: 0.112768	train's f1: 1	val's binary_logloss: 0.503847	val's f1: 0.791304
[243]	train's binary_logloss: 0.112096	train's f1: 1	val's binary_logloss: 0.503385	val's f1: 0.796537
[244]	train's binary_logloss: 0.111382	train's f1: 1	val's binary_logloss: 0.503072	val's f1: 0.796537
[245]	train's binary_logloss: 0.110754	train's f1: 1	val's binary_logloss: 0.502119	val's f1: 0.796537
[246]	train's binary_logloss: 0.110089	train's f1: 1	val's binary_logloss: 0.502562	val's f1: 0.796537
[247]	train's binary_logloss: 0.10953	train's f1: 1	val's binary_logloss: 0.502711	val's f1: 0.796537
[248]	train's binary_logloss: 0.108908	train's f1: 1	val's binary_logloss: 

[346]	train's binary_logloss: 0.0610648	train's f1: 1	val's binary_logloss: 0.488478	val's f1: 0.810573
[347]	train's binary_logloss: 0.0606937	train's f1: 1	val's binary_logloss: 0.487908	val's f1: 0.810573
[348]	train's binary_logloss: 0.0603725	train's f1: 1	val's binary_logloss: 0.487938	val's f1: 0.810573
[349]	train's binary_logloss: 0.0599173	train's f1: 1	val's binary_logloss: 0.488145	val's f1: 0.814159
[350]	train's binary_logloss: 0.0595705	train's f1: 1	val's binary_logloss: 0.488727	val's f1: 0.808889
[351]	train's binary_logloss: 0.0592246	train's f1: 1	val's binary_logloss: 0.488433	val's f1: 0.808889
[352]	train's binary_logloss: 0.0588273	train's f1: 1	val's binary_logloss: 0.48822	val's f1: 0.808889
[353]	train's binary_logloss: 0.0585155	train's f1: 1	val's binary_logloss: 0.488087	val's f1: 0.808889
[354]	train's binary_logloss: 0.058172	train's f1: 1	val's binary_logloss: 0.488625	val's f1: 0.814159
[355]	train's binary_logloss: 0.0578222	train's f1: 1	val's binary

...

[2590]	train's binary_logloss: 5.31159e-06	train's f1: 1	val's binary_logloss: 0.860944	val's f1: 0.791304
[2591]	train's binary_logloss: 5.30848e-06	train's f1: 1	val's binary_logloss: 0.860843	val's f1: 0.791304
[2592]	train's binary_logloss: 5.30521e-06	train's f1: 1	val's binary_logloss: 0.861056	val's f1: 0.791304
[2593]	train's binary_logloss: 5.3022e-06	train's f1: 1	val's binary_logloss: 0.861301	val's f1: 0.791304
[2594]	train's binary_logloss: 5.29856e-06	train's f1: 1	val's binary_logloss: 0.861146	val's f1: 0.791304
[2595]	train's binary_logloss: 5.29533e-06	train's f1: 1	val's binary_logloss: 0.861237	val's f1: 0.791304
[2596]	train's binary_logloss: 5.29234e-06	train's f1: 1	val's binary_logloss: 0.861215	val's f1: 0.791304
[2597]	train's binary_logloss: 5.28763e-06	train's f1: 1	val's binary_logloss: 0.861354	val's f1: 0.791304
[2598]	train's binary_logloss: 5.28439e-06	train's f1: 1	val's binary_logloss: 0.861397	val's f1: 0.791304
[2599]	train's binary_logloss: 5.28146

[2676]	train's binary_logloss: 5.04283e-06	train's f1: 1	val's binary_logloss: 0.864032	val's f1: 0.791304
[2677]	train's binary_logloss: 5.04021e-06	train's f1: 1	val's binary_logloss: 0.864143	val's f1: 0.791304
[2678]	train's binary_logloss: 5.03708e-06	train's f1: 1	val's binary_logloss: 0.864349	val's f1: 0.791304
[2679]	train's binary_logloss: 5.03459e-06	train's f1: 1	val's binary_logloss: 0.864382	val's f1: 0.791304
[2680]	train's binary_logloss: 5.03176e-06	train's f1: 1	val's binary_logloss: 0.864318	val's f1: 0.791304
[2681]	train's binary_logloss: 5.0295e-06	train's f1: 1	val's binary_logloss: 0.864333	val's f1: 0.791304
[2682]	train's binary_logloss: 5.02602e-06	train's f1: 1	val's binary_logloss: 0.864206	val's f1: 0.791304
[2683]	train's binary_logloss: 5.02299e-06	train's f1: 1	val's binary_logloss: 0.864482	val's f1: 0.791304
[2684]	train's binary_logloss: 5.02049e-06	train's f1: 1	val's binary_logloss: 0.864516	val's f1: 0.791304
[2685]	train's binary_logloss: 5.01741

[2762]	train's binary_logloss: 4.8055e-06	train's f1: 1	val's binary_logloss: 0.868098	val's f1: 0.791304
[2763]	train's binary_logloss: 4.80321e-06	train's f1: 1	val's binary_logloss: 0.868398	val's f1: 0.791304
[2764]	train's binary_logloss: 4.80117e-06	train's f1: 1	val's binary_logloss: 0.868337	val's f1: 0.791304
[2765]	train's binary_logloss: 4.79914e-06	train's f1: 1	val's binary_logloss: 0.868262	val's f1: 0.791304
[2766]	train's binary_logloss: 4.79621e-06	train's f1: 1	val's binary_logloss: 0.868426	val's f1: 0.791304
[2767]	train's binary_logloss: 4.79343e-06	train's f1: 1	val's binary_logloss: 0.868371	val's f1: 0.791304
[2768]	train's binary_logloss: 4.7913e-06	train's f1: 1	val's binary_logloss: 0.868236	val's f1: 0.791304
[2769]	train's binary_logloss: 4.78926e-06	train's f1: 1	val's binary_logloss: 0.868277	val's f1: 0.791304
[2770]	train's binary_logloss: 4.78607e-06	train's f1: 1	val's binary_logloss: 0.868468	val's f1: 0.791304
[2771]	train's binary_logloss: 4.78387e

[2848]	train's binary_logloss: 4.60471e-06	train's f1: 1	val's binary_logloss: 0.869683	val's f1: 0.791304
[2849]	train's binary_logloss: 4.6027e-06	train's f1: 1	val's binary_logloss: 0.869602	val's f1: 0.791304
[2850]	train's binary_logloss: 4.5999e-06	train's f1: 1	val's binary_logloss: 0.869532	val's f1: 0.791304
[2851]	train's binary_logloss: 4.59744e-06	train's f1: 1	val's binary_logloss: 0.869378	val's f1: 0.791304
[2852]	train's binary_logloss: 4.59564e-06	train's f1: 1	val's binary_logloss: 0.869524	val's f1: 0.791304
[2853]	train's binary_logloss: 4.59375e-06	train's f1: 1	val's binary_logloss: 0.869608	val's f1: 0.791304
[2854]	train's binary_logloss: 4.59097e-06	train's f1: 1	val's binary_logloss: 0.869686	val's f1: 0.791304
[2855]	train's binary_logloss: 4.58852e-06	train's f1: 1	val's binary_logloss: 0.869919	val's f1: 0.791304
[2856]	train's binary_logloss: 4.58624e-06	train's f1: 1	val's binary_logloss: 0.869874	val's f1: 0.791304
[2857]	train's binary_logloss: 4.58395e

[2932]	train's binary_logloss: 4.42676e-06	train's f1: 1	val's binary_logloss: 0.870539	val's f1: 0.796537
[2933]	train's binary_logloss: 4.42468e-06	train's f1: 1	val's binary_logloss: 0.870737	val's f1: 0.796537
[2934]	train's binary_logloss: 4.42213e-06	train's f1: 1	val's binary_logloss: 0.870656	val's f1: 0.796537
[2935]	train's binary_logloss: 4.42098e-06	train's f1: 1	val's binary_logloss: 0.870599	val's f1: 0.796537
[2936]	train's binary_logloss: 4.41834e-06	train's f1: 1	val's binary_logloss: 0.8706	val's f1: 0.796537
[2937]	train's binary_logloss: 4.41578e-06	train's f1: 1	val's binary_logloss: 0.870524	val's f1: 0.796537
[2938]	train's binary_logloss: 4.41388e-06	train's f1: 1	val's binary_logloss: 0.87081	val's f1: 0.796537
[2939]	train's binary_logloss: 4.41244e-06	train's f1: 1	val's binary_logloss: 0.871045	val's f1: 0.796537
[2940]	train's binary_logloss: 4.41062e-06	train's f1: 1	val's binary_logloss: 0.871233	val's f1: 0.796537
[2941]	train's binary_logloss: 4.40863e-

In [188]:
imr90_lgb_pred_seq = imr90_lgb_seq.predict(imr90_seq_test_x)
f1_score(imr90_seq_test_y,prob2label(imr90_lgb_pred_seq))

0.7717171717171718

### GM12878

In [189]:
gm12878_seq_train_x = gm12878_original_data_json['X_train_seq']
gm12878_seq_train_y = gm12878_original_data_json['y_train_seq']

gm12878_seq_test_x  = gm12878_original_data_json['X_test_seq']
gm12878_seq_test_y = gm12878_original_data_json['y_test_seq']

gm12878_seq_train_lgb,gm12878_seq_valid_lgb,_ = generate_lgb_use_data(gm12878_seq_train_x,
                                                               gm12878_seq_train_y,
                                                               gm12878_seq_test_x,
                                                               gm12878_seq_test_y)

In [190]:
gm12878_lgb_seq = train_lgb(gm12878_seq_train_lgb,gm12878_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.68613	train's f1: 0.112445	val's binary_logloss: 0.692953	val's f1: 0.0526316
[2]	train's binary_logloss: 0.679828	train's f1: 0.612013	val's binary_logloss: 0.690448	val's f1: 0.469799
[3]	train's binary_logloss: 0.673912	train's f1: 0.655063	val's binary_logloss: 0.688762	val's f1: 0.504854
[4]	train's binary_logloss: 0.668018	train's f1: 0.678043	val's binary_logloss: 0.687341	val's f1: 0.515723
[5]	train's binary_logloss: 0.662673	train's f1: 0.701559	val's binary_logloss: 0.685191	val's f1: 0.523077
[6]	train's binary_logloss: 0.657374	train's f1: 0.721455	val's binary_logloss: 0.682514	val's f1: 0.548193
[7]	train's binary_logloss: 0.651951	train's f1: 0.738087	val's binary_logloss: 0.680733	val's f1: 0.553571
[8]	train's binary_logloss: 0.64701	train's f1: 0.757968	val's binary_logloss: 0.679139	val's f1: 0.552941
[9]	train's binary_logloss: 0.641981	train's f1: 0.757586	val's binary_logloss: 0.67735	val's f1: 0.566474
[10]	train's binary_logloss: 0

[95]	train's binary_logloss: 0.408292	train's f1: 0.952637	val's binary_logloss: 0.605327	val's f1: 0.716667
[96]	train's binary_logloss: 0.406936	train's f1: 0.953277	val's binary_logloss: 0.605922	val's f1: 0.707521
[97]	train's binary_logloss: 0.405412	train's f1: 0.955003	val's binary_logloss: 0.605623	val's f1: 0.713092
[98]	train's binary_logloss: 0.403583	train's f1: 0.956317	val's binary_logloss: 0.605125	val's f1: 0.716667
[99]	train's binary_logloss: 0.401764	train's f1: 0.956668	val's binary_logloss: 0.605224	val's f1: 0.707521
[100]	train's binary_logloss: 0.400199	train's f1: 0.957425	val's binary_logloss: 0.604629	val's f1: 0.709497
[101]	train's binary_logloss: 0.39854	train's f1: 0.959437	val's binary_logloss: 0.604194	val's f1: 0.713092
[102]	train's binary_logloss: 0.396897	train's f1: 0.959115	val's binary_logloss: 0.603188	val's f1: 0.715084
[103]	train's binary_logloss: 0.395325	train's f1: 0.959786	val's binary_logloss: 0.602741	val's f1: 0.711111
[104]	train's bi

[191]	train's binary_logloss: 0.28125	train's f1: 0.991269	val's binary_logloss: 0.587603	val's f1: 0.718919
[192]	train's binary_logloss: 0.280168	train's f1: 0.99093	val's binary_logloss: 0.587455	val's f1: 0.710383
[193]	train's binary_logloss: 0.279011	train's f1: 0.99093	val's binary_logloss: 0.586446	val's f1: 0.710744
[194]	train's binary_logloss: 0.278139	train's f1: 0.991269	val's binary_logloss: 0.586404	val's f1: 0.708791
[195]	train's binary_logloss: 0.277079	train's f1: 0.991602	val's binary_logloss: 0.586029	val's f1: 0.715847
[196]	train's binary_logloss: 0.275932	train's f1: 0.991263	val's binary_logloss: 0.586284	val's f1: 0.71978
[197]	train's binary_logloss: 0.274765	train's f1: 0.991597	val's binary_logloss: 0.586407	val's f1: 0.71978
[198]	train's binary_logloss: 0.273754	train's f1: 0.991935	val's binary_logloss: 0.586182	val's f1: 0.721763
[199]	train's binary_logloss: 0.272888	train's f1: 0.991935	val's binary_logloss: 0.586178	val's f1: 0.721763
[200]	train's b

[290]	train's binary_logloss: 0.198071	train's f1: 0.998317	val's binary_logloss: 0.577719	val's f1: 0.701657
[291]	train's binary_logloss: 0.197414	train's f1: 0.998317	val's binary_logloss: 0.577773	val's f1: 0.701657
[292]	train's binary_logloss: 0.196713	train's f1: 0.998317	val's binary_logloss: 0.577218	val's f1: 0.701657
[293]	train's binary_logloss: 0.196009	train's f1: 0.998317	val's binary_logloss: 0.57699	val's f1: 0.701657
[294]	train's binary_logloss: 0.19524	train's f1: 0.998317	val's binary_logloss: 0.576643	val's f1: 0.705234
[295]	train's binary_logloss: 0.194671	train's f1: 0.998317	val's binary_logloss: 0.576957	val's f1: 0.701657
[296]	train's binary_logloss: 0.193915	train's f1: 0.998317	val's binary_logloss: 0.57655	val's f1: 0.701657
[297]	train's binary_logloss: 0.193255	train's f1: 0.998317	val's binary_logloss: 0.576473	val's f1: 0.701657
[298]	train's binary_logloss: 0.192697	train's f1: 0.998317	val's binary_logloss: 0.575836	val's f1: 0.703601
[299]	train's

[388]	train's binary_logloss: 0.141967	train's f1: 0.999327	val's binary_logloss: 0.567815	val's f1: 0.716253
[389]	train's binary_logloss: 0.141475	train's f1: 0.999327	val's binary_logloss: 0.567683	val's f1: 0.718232
[390]	train's binary_logloss: 0.141047	train's f1: 0.999327	val's binary_logloss: 0.567827	val's f1: 0.716253
[391]	train's binary_logloss: 0.140579	train's f1: 0.999327	val's binary_logloss: 0.567782	val's f1: 0.714681
[392]	train's binary_logloss: 0.14014	train's f1: 0.999327	val's binary_logloss: 0.567903	val's f1: 0.705556
[393]	train's binary_logloss: 0.139771	train's f1: 0.999327	val's binary_logloss: 0.568203	val's f1: 0.705556
[394]	train's binary_logloss: 0.13934	train's f1: 0.999664	val's binary_logloss: 0.568346	val's f1: 0.705556
[395]	train's binary_logloss: 0.138821	train's f1: 0.999664	val's binary_logloss: 0.567763	val's f1: 0.716667
[396]	train's binary_logloss: 0.138178	train's f1: 0.999327	val's binary_logloss: 0.567741	val's f1: 0.716667
[397]	train'

...

[2645]	train's binary_logloss: 8.71144e-05	train's f1: 1	val's binary_logloss: 0.820014	val's f1: 0.725762
[2646]	train's binary_logloss: 8.68302e-05	train's f1: 1	val's binary_logloss: 0.82039	val's f1: 0.725762
[2647]	train's binary_logloss: 8.65392e-05	train's f1: 1	val's binary_logloss: 0.820606	val's f1: 0.725762
[2648]	train's binary_logloss: 8.62527e-05	train's f1: 1	val's binary_logloss: 0.820737	val's f1: 0.725762
[2649]	train's binary_logloss: 8.59909e-05	train's f1: 1	val's binary_logloss: 0.820613	val's f1: 0.722222
[2650]	train's binary_logloss: 8.57104e-05	train's f1: 1	val's binary_logloss: 0.820844	val's f1: 0.722222
[2651]	train's binary_logloss: 8.53995e-05	train's f1: 1	val's binary_logloss: 0.821293	val's f1: 0.722222
[2652]	train's binary_logloss: 8.5136e-05	train's f1: 1	val's binary_logloss: 0.821544	val's f1: 0.722222
[2653]	train's binary_logloss: 8.48737e-05	train's f1: 1	val's binary_logloss: 0.821579	val's f1: 0.722222
[2654]	train's binary_logloss: 8.45927e

[2727]	train's binary_logloss: 6.61074e-05	train's f1: 1	val's binary_logloss: 0.831354	val's f1: 0.718663
[2728]	train's binary_logloss: 6.59106e-05	train's f1: 1	val's binary_logloss: 0.831041	val's f1: 0.718663
[2729]	train's binary_logloss: 6.57197e-05	train's f1: 1	val's binary_logloss: 0.830997	val's f1: 0.718663
[2730]	train's binary_logloss: 6.55274e-05	train's f1: 1	val's binary_logloss: 0.830942	val's f1: 0.718663
[2731]	train's binary_logloss: 6.53374e-05	train's f1: 1	val's binary_logloss: 0.830637	val's f1: 0.718663
[2732]	train's binary_logloss: 6.50756e-05	train's f1: 1	val's binary_logloss: 0.830781	val's f1: 0.718663
[2733]	train's binary_logloss: 6.48979e-05	train's f1: 1	val's binary_logloss: 0.830647	val's f1: 0.722222
[2734]	train's binary_logloss: 6.46758e-05	train's f1: 1	val's binary_logloss: 0.831385	val's f1: 0.718663
[2735]	train's binary_logloss: 6.44502e-05	train's f1: 1	val's binary_logloss: 0.831425	val's f1: 0.718663
[2736]	train's binary_logloss: 6.4255

[2811]	train's binary_logloss: 5.03937e-05	train's f1: 1	val's binary_logloss: 0.843319	val's f1: 0.718663
[2812]	train's binary_logloss: 5.02187e-05	train's f1: 1	val's binary_logloss: 0.843276	val's f1: 0.718663
[2813]	train's binary_logloss: 5.00779e-05	train's f1: 1	val's binary_logloss: 0.843297	val's f1: 0.718663
[2814]	train's binary_logloss: 4.99079e-05	train's f1: 1	val's binary_logloss: 0.843605	val's f1: 0.718663
[2815]	train's binary_logloss: 4.97639e-05	train's f1: 1	val's binary_logloss: 0.843686	val's f1: 0.718663
[2816]	train's binary_logloss: 4.96252e-05	train's f1: 1	val's binary_logloss: 0.84384	val's f1: 0.715084
[2817]	train's binary_logloss: 4.94698e-05	train's f1: 1	val's binary_logloss: 0.84396	val's f1: 0.715084
[2818]	train's binary_logloss: 4.92951e-05	train's f1: 1	val's binary_logloss: 0.843856	val's f1: 0.715084
[2819]	train's binary_logloss: 4.91388e-05	train's f1: 1	val's binary_logloss: 0.844257	val's f1: 0.715084
[2820]	train's binary_logloss: 4.89985e

[2894]	train's binary_logloss: 3.85163e-05	train's f1: 1	val's binary_logloss: 0.858489	val's f1: 0.72067
[2895]	train's binary_logloss: 3.8379e-05	train's f1: 1	val's binary_logloss: 0.858574	val's f1: 0.72067
[2896]	train's binary_logloss: 3.82523e-05	train's f1: 1	val's binary_logloss: 0.858276	val's f1: 0.72067
[2897]	train's binary_logloss: 3.81204e-05	train's f1: 1	val's binary_logloss: 0.858413	val's f1: 0.72067
[2898]	train's binary_logloss: 3.80033e-05	train's f1: 1	val's binary_logloss: 0.858374	val's f1: 0.72067
[2899]	train's binary_logloss: 3.78869e-05	train's f1: 1	val's binary_logloss: 0.858579	val's f1: 0.72067
[2900]	train's binary_logloss: 3.77765e-05	train's f1: 1	val's binary_logloss: 0.858963	val's f1: 0.724234
[2901]	train's binary_logloss: 3.76499e-05	train's f1: 1	val's binary_logloss: 0.85844	val's f1: 0.724234
[2902]	train's binary_logloss: 3.75367e-05	train's f1: 1	val's binary_logloss: 0.85898	val's f1: 0.724234
[2903]	train's binary_logloss: 3.74275e-05	tra

[2976]	train's binary_logloss: 2.96232e-05	train's f1: 1	val's binary_logloss: 0.872574	val's f1: 0.717087
[2977]	train's binary_logloss: 2.95377e-05	train's f1: 1	val's binary_logloss: 0.873066	val's f1: 0.713483
[2978]	train's binary_logloss: 2.94373e-05	train's f1: 1	val's binary_logloss: 0.873355	val's f1: 0.717087
[2979]	train's binary_logloss: 2.93445e-05	train's f1: 1	val's binary_logloss: 0.873526	val's f1: 0.713483
[2980]	train's binary_logloss: 2.9256e-05	train's f1: 1	val's binary_logloss: 0.873718	val's f1: 0.713483
[2981]	train's binary_logloss: 2.91604e-05	train's f1: 1	val's binary_logloss: 0.873871	val's f1: 0.713483
[2982]	train's binary_logloss: 2.9073e-05	train's f1: 1	val's binary_logloss: 0.873788	val's f1: 0.717087
[2983]	train's binary_logloss: 2.89842e-05	train's f1: 1	val's binary_logloss: 0.874331	val's f1: 0.713483
[2984]	train's binary_logloss: 2.88979e-05	train's f1: 1	val's binary_logloss: 0.874617	val's f1: 0.713483
[2985]	train's binary_logloss: 2.88019e

In [191]:
gm12878_lgb_pred_seq = gm12878_lgb_seq.predict(gm12878_seq_test_x)
f1_score(gm12878_seq_test_y,prob2label(gm12878_lgb_pred_seq))

0.7301231802911535

### HUVEC

In [192]:
huvec_seq_train_x = huvec_original_data_json['X_train_seq']
huvec_seq_train_y = huvec_original_data_json['y_train_seq']

huvec_seq_test_x  = huvec_original_data_json['X_test_seq']
huvec_seq_test_y = huvec_original_data_json['y_test_seq']

huvec_seq_train_lgb,huvec_seq_valid_lgb,_ = generate_lgb_use_data(huvec_seq_train_x,
                                                               huvec_seq_train_y,
                                                               huvec_seq_test_x,
                                                               huvec_seq_test_y)

In [193]:
huvec_lgb_seq = train_lgb(huvec_seq_train_lgb,huvec_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.684146	train's f1: 0.764268	val's binary_logloss: 0.687259	val's f1: 0.686567
[2]	train's binary_logloss: 0.675713	train's f1: 0.774417	val's binary_logloss: 0.68241	val's f1: 0.684615
[3]	train's binary_logloss: 0.66744	train's f1: 0.7716	val's binary_logloss: 0.676801	val's f1: 0.692015
[4]	train's binary_logloss: 0.659855	train's f1: 0.791254	val's binary_logloss: 0.672245	val's f1: 0.711111
[5]	train's binary_logloss: 0.652671	train's f1: 0.796445	val's binary_logloss: 0.668166	val's f1: 0.681992
[6]	train's binary_logloss: 0.646445	train's f1: 0.806929	val's binary_logloss: 0.665168	val's f1: 0.70632
[7]	train's binary_logloss: 0.639666	train's f1: 0.815723	val's binary_logloss: 0.66207	val's f1: 0.69434
[8]	train's binary_logloss: 0.632672	train's f1: 0.822779	val's binary_logloss: 0.658352	val's f1: 0.681992
[9]	train's binary_logloss: 0.62608	train's f1: 0.820229	val's binary_logloss: 0.655363	val's f1: 0.69962
[10]	train's binary_logloss: 0.620343

[78]	train's binary_logloss: 0.370277	train's f1: 0.96844	val's binary_logloss: 0.558425	val's f1: 0.74717
[79]	train's binary_logloss: 0.368106	train's f1: 0.968412	val's binary_logloss: 0.55745	val's f1: 0.74717
[80]	train's binary_logloss: 0.365634	train's f1: 0.96844	val's binary_logloss: 0.557015	val's f1: 0.744361
[81]	train's binary_logloss: 0.363135	train's f1: 0.968905	val's binary_logloss: 0.556461	val's f1: 0.744361
[82]	train's binary_logloss: 0.360844	train's f1: 0.969779	val's binary_logloss: 0.555485	val's f1: 0.744361
[83]	train's binary_logloss: 0.358895	train's f1: 0.968877	val's binary_logloss: 0.556018	val's f1: 0.739623
[84]	train's binary_logloss: 0.356762	train's f1: 0.970681	val's binary_logloss: 0.555575	val's f1: 0.741573
[85]	train's binary_logloss: 0.354538	train's f1: 0.972411	val's binary_logloss: 0.555507	val's f1: 0.741573
[86]	train's binary_logloss: 0.352181	train's f1: 0.973291	val's binary_logloss: 0.55429	val's f1: 0.745247
[87]	train's binary_loglo

[175]	train's binary_logloss: 0.21316	train's f1: 0.998642	val's binary_logloss: 0.542684	val's f1: 0.753846
[176]	train's binary_logloss: 0.212186	train's f1: 0.998642	val's binary_logloss: 0.543205	val's f1: 0.751938
[177]	train's binary_logloss: 0.211213	train's f1: 0.998641	val's binary_logloss: 0.543088	val's f1: 0.751938
[178]	train's binary_logloss: 0.210105	train's f1: 0.998641	val's binary_logloss: 0.54327	val's f1: 0.749035
[179]	train's binary_logloss: 0.208972	train's f1: 0.999093	val's binary_logloss: 0.542988	val's f1: 0.749035
[180]	train's binary_logloss: 0.207831	train's f1: 0.999093	val's binary_logloss: 0.542866	val's f1: 0.756757
[181]	train's binary_logloss: 0.206644	train's f1: 0.999547	val's binary_logloss: 0.543031	val's f1: 0.756757
[182]	train's binary_logloss: 0.205445	train's f1: 0.999547	val's binary_logloss: 0.543332	val's f1: 0.756757
[183]	train's binary_logloss: 0.204381	train's f1: 0.999547	val's binary_logloss: 0.54275	val's f1: 0.764479
[184]	train's

[275]	train's binary_logloss: 0.127273	train's f1: 1	val's binary_logloss: 0.532338	val's f1: 0.761538
[276]	train's binary_logloss: 0.126674	train's f1: 1	val's binary_logloss: 0.532333	val's f1: 0.761538
[277]	train's binary_logloss: 0.12593	train's f1: 1	val's binary_logloss: 0.532803	val's f1: 0.756757
[278]	train's binary_logloss: 0.125284	train's f1: 1	val's binary_logloss: 0.532834	val's f1: 0.756757
[279]	train's binary_logloss: 0.12459	train's f1: 1	val's binary_logloss: 0.533236	val's f1: 0.756757
[280]	train's binary_logloss: 0.124041	train's f1: 1	val's binary_logloss: 0.533818	val's f1: 0.751938
[281]	train's binary_logloss: 0.123349	train's f1: 1	val's binary_logloss: 0.533591	val's f1: 0.756757
[282]	train's binary_logloss: 0.122646	train's f1: 1	val's binary_logloss: 0.533596	val's f1: 0.756757
[283]	train's binary_logloss: 0.12214	train's f1: 1	val's binary_logloss: 0.533816	val's f1: 0.756757
[284]	train's binary_logloss: 0.121561	train's f1: 1	val's binary_logloss: 0

[374]	train's binary_logloss: 0.0778135	train's f1: 1	val's binary_logloss: 0.540657	val's f1: 0.749035
[375]	train's binary_logloss: 0.0774501	train's f1: 1	val's binary_logloss: 0.540404	val's f1: 0.749035
[376]	train's binary_logloss: 0.0770666	train's f1: 1	val's binary_logloss: 0.5402	val's f1: 0.751938
[377]	train's binary_logloss: 0.0765787	train's f1: 1	val's binary_logloss: 0.540116	val's f1: 0.751938
[378]	train's binary_logloss: 0.076177	train's f1: 1	val's binary_logloss: 0.54039	val's f1: 0.751938
[379]	train's binary_logloss: 0.0758893	train's f1: 1	val's binary_logloss: 0.541113	val's f1: 0.751938
[380]	train's binary_logloss: 0.0755154	train's f1: 1	val's binary_logloss: 0.540438	val's f1: 0.751938
[381]	train's binary_logloss: 0.074992	train's f1: 1	val's binary_logloss: 0.540296	val's f1: 0.751938
[382]	train's binary_logloss: 0.0745473	train's f1: 1	val's binary_logloss: 0.540286	val's f1: 0.749035
[383]	train's binary_logloss: 0.0741948	train's f1: 1	val's binary_lo

...

[2481]	train's binary_logloss: 7.99063e-06	train's f1: 1	val's binary_logloss: 1.02171	val's f1: 0.755725
[2482]	train's binary_logloss: 7.97838e-06	train's f1: 1	val's binary_logloss: 1.02124	val's f1: 0.755725
[2483]	train's binary_logloss: 7.96708e-06	train's f1: 1	val's binary_logloss: 1.0211	val's f1: 0.755725
[2484]	train's binary_logloss: 7.95691e-06	train's f1: 1	val's binary_logloss: 1.02132	val's f1: 0.755725
[2485]	train's binary_logloss: 7.94622e-06	train's f1: 1	val's binary_logloss: 1.02122	val's f1: 0.755725
[2486]	train's binary_logloss: 7.93466e-06	train's f1: 1	val's binary_logloss: 1.02136	val's f1: 0.755725
[2487]	train's binary_logloss: 7.92333e-06	train's f1: 1	val's binary_logloss: 1.02149	val's f1: 0.755725
[2488]	train's binary_logloss: 7.91052e-06	train's f1: 1	val's binary_logloss: 1.0216	val's f1: 0.755725
[2489]	train's binary_logloss: 7.89988e-06	train's f1: 1	val's binary_logloss: 1.02177	val's f1: 0.755725
[2490]	train's binary_logloss: 7.88877e-06	train

[2585]	train's binary_logloss: 7.01059e-06	train's f1: 1	val's binary_logloss: 1.02874	val's f1: 0.755725
[2586]	train's binary_logloss: 7.0035e-06	train's f1: 1	val's binary_logloss: 1.02901	val's f1: 0.755725
[2587]	train's binary_logloss: 6.99511e-06	train's f1: 1	val's binary_logloss: 1.02906	val's f1: 0.755725
[2588]	train's binary_logloss: 6.98704e-06	train's f1: 1	val's binary_logloss: 1.02949	val's f1: 0.755725
[2589]	train's binary_logloss: 6.97791e-06	train's f1: 1	val's binary_logloss: 1.02906	val's f1: 0.755725
[2590]	train's binary_logloss: 6.97096e-06	train's f1: 1	val's binary_logloss: 1.02898	val's f1: 0.755725
[2591]	train's binary_logloss: 6.96414e-06	train's f1: 1	val's binary_logloss: 1.02924	val's f1: 0.755725
[2592]	train's binary_logloss: 6.95728e-06	train's f1: 1	val's binary_logloss: 1.02917	val's f1: 0.755725
[2593]	train's binary_logloss: 6.94962e-06	train's f1: 1	val's binary_logloss: 1.02935	val's f1: 0.755725
[2594]	train's binary_logloss: 6.94247e-06	trai

[2690]	train's binary_logloss: 6.29624e-06	train's f1: 1	val's binary_logloss: 1.03513	val's f1: 0.755725
[2691]	train's binary_logloss: 6.29e-06	train's f1: 1	val's binary_logloss: 1.03511	val's f1: 0.755725
[2692]	train's binary_logloss: 6.28309e-06	train's f1: 1	val's binary_logloss: 1.03497	val's f1: 0.755725
[2693]	train's binary_logloss: 6.27727e-06	train's f1: 1	val's binary_logloss: 1.03487	val's f1: 0.755725
[2694]	train's binary_logloss: 6.27173e-06	train's f1: 1	val's binary_logloss: 1.03469	val's f1: 0.755725
[2695]	train's binary_logloss: 6.26617e-06	train's f1: 1	val's binary_logloss: 1.0348	val's f1: 0.755725
[2696]	train's binary_logloss: 6.26102e-06	train's f1: 1	val's binary_logloss: 1.03492	val's f1: 0.755725
[2697]	train's binary_logloss: 6.25528e-06	train's f1: 1	val's binary_logloss: 1.03527	val's f1: 0.755725
[2698]	train's binary_logloss: 6.24928e-06	train's f1: 1	val's binary_logloss: 1.03529	val's f1: 0.755725
[2699]	train's binary_logloss: 6.24452e-06	train's

[2798]	train's binary_logloss: 5.73883e-06	train's f1: 1	val's binary_logloss: 1.04161	val's f1: 0.755725
[2799]	train's binary_logloss: 5.73383e-06	train's f1: 1	val's binary_logloss: 1.04151	val's f1: 0.755725
[2800]	train's binary_logloss: 5.72897e-06	train's f1: 1	val's binary_logloss: 1.04132	val's f1: 0.755725
[2801]	train's binary_logloss: 5.72452e-06	train's f1: 1	val's binary_logloss: 1.04164	val's f1: 0.755725
[2802]	train's binary_logloss: 5.72002e-06	train's f1: 1	val's binary_logloss: 1.04177	val's f1: 0.755725
[2803]	train's binary_logloss: 5.71475e-06	train's f1: 1	val's binary_logloss: 1.04177	val's f1: 0.755725
[2804]	train's binary_logloss: 5.70959e-06	train's f1: 1	val's binary_logloss: 1.04195	val's f1: 0.755725
[2805]	train's binary_logloss: 5.70412e-06	train's f1: 1	val's binary_logloss: 1.04212	val's f1: 0.755725
[2806]	train's binary_logloss: 5.69878e-06	train's f1: 1	val's binary_logloss: 1.04224	val's f1: 0.755725
[2807]	train's binary_logloss: 5.69446e-06	tra

[2909]	train's binary_logloss: 5.29271e-06	train's f1: 1	val's binary_logloss: 1.04747	val's f1: 0.755725
[2910]	train's binary_logloss: 5.28981e-06	train's f1: 1	val's binary_logloss: 1.04744	val's f1: 0.755725
[2911]	train's binary_logloss: 5.28619e-06	train's f1: 1	val's binary_logloss: 1.04754	val's f1: 0.755725
[2912]	train's binary_logloss: 5.28297e-06	train's f1: 1	val's binary_logloss: 1.0477	val's f1: 0.755725
[2913]	train's binary_logloss: 5.27986e-06	train's f1: 1	val's binary_logloss: 1.04787	val's f1: 0.755725
[2914]	train's binary_logloss: 5.27615e-06	train's f1: 1	val's binary_logloss: 1.04795	val's f1: 0.755725
[2915]	train's binary_logloss: 5.27209e-06	train's f1: 1	val's binary_logloss: 1.04827	val's f1: 0.755725
[2916]	train's binary_logloss: 5.26866e-06	train's f1: 1	val's binary_logloss: 1.0482	val's f1: 0.755725
[2917]	train's binary_logloss: 5.2651e-06	train's f1: 1	val's binary_logloss: 1.04833	val's f1: 0.755725
[2918]	train's binary_logloss: 5.26129e-06	train'

In [194]:
huvec_lgb_pred_seq = huvec_lgb_seq.predict(huvec_seq_test_x)
f1_score(huvec_seq_test_y,prob2label(huvec_lgb_pred_seq))

0.7365079365079364

### NHEK

In [195]:
nhek_seq_train_x = nhek_original_data_json['X_train_seq']
nhek_seq_train_y = nhek_original_data_json['y_train_seq']

nhek_seq_test_x  = nhek_original_data_json['X_test_seq']
nhek_seq_test_y = nhek_original_data_json['y_test_seq']

nhek_seq_train_lgb,nhek_seq_valid_lgb,_ = generate_lgb_use_data(nhek_seq_train_x,
                                                               nhek_seq_train_y,
                                                               nhek_seq_test_x,
                                                               nhek_seq_test_y)

In [196]:
nhek_lgb_seq = train_lgb(nhek_seq_train_lgb,nhek_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.6813	train's f1: 0.695312	val's binary_logloss: 0.684927	val's f1: 0.696517
[2]	train's binary_logloss: 0.669894	train's f1: 0.792102	val's binary_logloss: 0.67584	val's f1: 0.756757
[3]	train's binary_logloss: 0.659179	train's f1: 0.807298	val's binary_logloss: 0.667337	val's f1: 0.776786
[4]	train's binary_logloss: 0.649005	train's f1: 0.820571	val's binary_logloss: 0.661382	val's f1: 0.762332
[5]	train's binary_logloss: 0.639029	train's f1: 0.818942	val's binary_logloss: 0.654867	val's f1: 0.782609
[6]	train's binary_logloss: 0.629738	train's f1: 0.824053	val's binary_logloss: 0.648507	val's f1: 0.760181
[7]	train's binary_logloss: 0.62017	train's f1: 0.837158	val's binary_logloss: 0.642473	val's f1: 0.79646
[8]	train's binary_logloss: 0.611398	train's f1: 0.837336	val's binary_logloss: 0.636095	val's f1: 0.777293
[9]	train's binary_logloss: 0.602992	train's f1: 0.845116	val's binary_logloss: 0.63121	val's f1: 0.767857
[10]	train's binary_logloss: 0.594

[80]	train's binary_logloss: 0.294174	train's f1: 0.982571	val's binary_logloss: 0.453576	val's f1: 0.875536
[81]	train's binary_logloss: 0.291859	train's f1: 0.983125	val's binary_logloss: 0.452356	val's f1: 0.880342
[82]	train's binary_logloss: 0.289446	train's f1: 0.983125	val's binary_logloss: 0.451833	val's f1: 0.869565
[83]	train's binary_logloss: 0.28734	train's f1: 0.983678	val's binary_logloss: 0.451805	val's f1: 0.87931
[84]	train's binary_logloss: 0.284638	train's f1: 0.98366	val's binary_logloss: 0.451043	val's f1: 0.874459
[85]	train's binary_logloss: 0.282732	train's f1: 0.984213	val's binary_logloss: 0.451155	val's f1: 0.874459
[86]	train's binary_logloss: 0.280415	train's f1: 0.985302	val's binary_logloss: 0.449379	val's f1: 0.875536
[87]	train's binary_logloss: 0.278041	train's f1: 0.985302	val's binary_logloss: 0.448863	val's f1: 0.874459
[88]	train's binary_logloss: 0.275688	train's f1: 0.985854	val's binary_logloss: 0.446898	val's f1: 0.865801
[89]	train's binary_lo

[158]	train's binary_logloss: 0.165282	train's f1: 0.998911	val's binary_logloss: 0.400651	val's f1: 0.86087
[159]	train's binary_logloss: 0.164208	train's f1: 0.998911	val's binary_logloss: 0.399641	val's f1: 0.86087
[160]	train's binary_logloss: 0.162982	train's f1: 0.998911	val's binary_logloss: 0.399175	val's f1: 0.86087
[161]	train's binary_logloss: 0.161866	train's f1: 0.998911	val's binary_logloss: 0.39912	val's f1: 0.86087
[162]	train's binary_logloss: 0.16068	train's f1: 0.998911	val's binary_logloss: 0.399093	val's f1: 0.86087
[163]	train's binary_logloss: 0.159486	train's f1: 0.998911	val's binary_logloss: 0.398296	val's f1: 0.86087
[164]	train's binary_logloss: 0.158386	train's f1: 0.998911	val's binary_logloss: 0.398529	val's f1: 0.865801
[165]	train's binary_logloss: 0.157345	train's f1: 0.998911	val's binary_logloss: 0.39815	val's f1: 0.86087
[166]	train's binary_logloss: 0.156147	train's f1: 0.999455	val's binary_logloss: 0.397851	val's f1: 0.857143
[167]	train's binary

[239]	train's binary_logloss: 0.0934233	train's f1: 1	val's binary_logloss: 0.371746	val's f1: 0.864629
[240]	train's binary_logloss: 0.0927345	train's f1: 1	val's binary_logloss: 0.371168	val's f1: 0.868421
[241]	train's binary_logloss: 0.0920107	train's f1: 1	val's binary_logloss: 0.370609	val's f1: 0.868421
[242]	train's binary_logloss: 0.0913841	train's f1: 1	val's binary_logloss: 0.370999	val's f1: 0.868421
[243]	train's binary_logloss: 0.0907017	train's f1: 1	val's binary_logloss: 0.37117	val's f1: 0.864629
[244]	train's binary_logloss: 0.0901279	train's f1: 1	val's binary_logloss: 0.371077	val's f1: 0.864629
[245]	train's binary_logloss: 0.0895912	train's f1: 1	val's binary_logloss: 0.371644	val's f1: 0.864629
[246]	train's binary_logloss: 0.0889235	train's f1: 1	val's binary_logloss: 0.372017	val's f1: 0.864629
[247]	train's binary_logloss: 0.0883767	train's f1: 1	val's binary_logloss: 0.371402	val's f1: 0.86087
[248]	train's binary_logloss: 0.0878264	train's f1: 1	val's binary

[339]	train's binary_logloss: 0.0478684	train's f1: 1	val's binary_logloss: 0.354893	val's f1: 0.859649
[340]	train's binary_logloss: 0.0475304	train's f1: 1	val's binary_logloss: 0.354754	val's f1: 0.859649
[341]	train's binary_logloss: 0.0472344	train's f1: 1	val's binary_logloss: 0.354027	val's f1: 0.859649
[342]	train's binary_logloss: 0.0469796	train's f1: 1	val's binary_logloss: 0.353967	val's f1: 0.859649
[343]	train's binary_logloss: 0.0467155	train's f1: 1	val's binary_logloss: 0.353463	val's f1: 0.859649
[344]	train's binary_logloss: 0.0464624	train's f1: 1	val's binary_logloss: 0.353595	val's f1: 0.859649
[345]	train's binary_logloss: 0.046124	train's f1: 1	val's binary_logloss: 0.352668	val's f1: 0.863436
[346]	train's binary_logloss: 0.0458503	train's f1: 1	val's binary_logloss: 0.352433	val's f1: 0.863436
[347]	train's binary_logloss: 0.0454932	train's f1: 1	val's binary_logloss: 0.352594	val's f1: 0.859649
[348]	train's binary_logloss: 0.0451925	train's f1: 1	val's binar

...

[2623]	train's binary_logloss: 4.22026e-06	train's f1: 1	val's binary_logloss: 0.557876	val's f1: 0.872247
[2624]	train's binary_logloss: 4.21779e-06	train's f1: 1	val's binary_logloss: 0.557904	val's f1: 0.872247
[2625]	train's binary_logloss: 4.2155e-06	train's f1: 1	val's binary_logloss: 0.557846	val's f1: 0.872247
[2626]	train's binary_logloss: 4.21344e-06	train's f1: 1	val's binary_logloss: 0.557908	val's f1: 0.872247
[2627]	train's binary_logloss: 4.21145e-06	train's f1: 1	val's binary_logloss: 0.557864	val's f1: 0.872247
[2628]	train's binary_logloss: 4.20942e-06	train's f1: 1	val's binary_logloss: 0.558	val's f1: 0.872247
[2629]	train's binary_logloss: 4.20726e-06	train's f1: 1	val's binary_logloss: 0.557963	val's f1: 0.872247
[2630]	train's binary_logloss: 4.20502e-06	train's f1: 1	val's binary_logloss: 0.557999	val's f1: 0.872247
[2631]	train's binary_logloss: 4.20314e-06	train's f1: 1	val's binary_logloss: 0.557974	val's f1: 0.872247
[2632]	train's binary_logloss: 4.20116e-0

[2704]	train's binary_logloss: 4.05696e-06	train's f1: 1	val's binary_logloss: 0.559158	val's f1: 0.872247
[2705]	train's binary_logloss: 4.05434e-06	train's f1: 1	val's binary_logloss: 0.559018	val's f1: 0.872247
[2706]	train's binary_logloss: 4.05253e-06	train's f1: 1	val's binary_logloss: 0.55896	val's f1: 0.872247
[2707]	train's binary_logloss: 4.05076e-06	train's f1: 1	val's binary_logloss: 0.559231	val's f1: 0.872247
[2708]	train's binary_logloss: 4.04841e-06	train's f1: 1	val's binary_logloss: 0.559271	val's f1: 0.872247
[2709]	train's binary_logloss: 4.04674e-06	train's f1: 1	val's binary_logloss: 0.559246	val's f1: 0.872247
[2710]	train's binary_logloss: 4.045e-06	train's f1: 1	val's binary_logloss: 0.559361	val's f1: 0.872247
[2711]	train's binary_logloss: 4.04261e-06	train's f1: 1	val's binary_logloss: 0.559291	val's f1: 0.872247
[2712]	train's binary_logloss: 4.04051e-06	train's f1: 1	val's binary_logloss: 0.559473	val's f1: 0.872247
[2713]	train's binary_logloss: 4.03836e-

[2788]	train's binary_logloss: 3.90167e-06	train's f1: 1	val's binary_logloss: 0.561224	val's f1: 0.872247
[2789]	train's binary_logloss: 3.90023e-06	train's f1: 1	val's binary_logloss: 0.561125	val's f1: 0.872247
[2790]	train's binary_logloss: 3.89807e-06	train's f1: 1	val's binary_logloss: 0.56108	val's f1: 0.872247
[2791]	train's binary_logloss: 3.89676e-06	train's f1: 1	val's binary_logloss: 0.56113	val's f1: 0.872247
[2792]	train's binary_logloss: 3.89487e-06	train's f1: 1	val's binary_logloss: 0.560964	val's f1: 0.872247
[2793]	train's binary_logloss: 3.89355e-06	train's f1: 1	val's binary_logloss: 0.561066	val's f1: 0.872247
[2794]	train's binary_logloss: 3.89211e-06	train's f1: 1	val's binary_logloss: 0.561103	val's f1: 0.872247
[2795]	train's binary_logloss: 3.89051e-06	train's f1: 1	val's binary_logloss: 0.561251	val's f1: 0.872247
[2796]	train's binary_logloss: 3.88835e-06	train's f1: 1	val's binary_logloss: 0.561169	val's f1: 0.872247
[2797]	train's binary_logloss: 3.88712e

[2871]	train's binary_logloss: 3.77553e-06	train's f1: 1	val's binary_logloss: 0.562238	val's f1: 0.868421
[2872]	train's binary_logloss: 3.77385e-06	train's f1: 1	val's binary_logloss: 0.562293	val's f1: 0.868421
[2873]	train's binary_logloss: 3.77246e-06	train's f1: 1	val's binary_logloss: 0.562281	val's f1: 0.868421
[2874]	train's binary_logloss: 3.77132e-06	train's f1: 1	val's binary_logloss: 0.562319	val's f1: 0.868421
[2875]	train's binary_logloss: 3.77005e-06	train's f1: 1	val's binary_logloss: 0.562375	val's f1: 0.868421
[2876]	train's binary_logloss: 3.76871e-06	train's f1: 1	val's binary_logloss: 0.562229	val's f1: 0.868421
[2877]	train's binary_logloss: 3.76763e-06	train's f1: 1	val's binary_logloss: 0.562162	val's f1: 0.868421
[2878]	train's binary_logloss: 3.76603e-06	train's f1: 1	val's binary_logloss: 0.562134	val's f1: 0.868421
[2879]	train's binary_logloss: 3.76473e-06	train's f1: 1	val's binary_logloss: 0.562083	val's f1: 0.868421
[2880]	train's binary_logloss: 3.7635

[2955]	train's binary_logloss: 3.66079e-06	train's f1: 1	val's binary_logloss: 0.56377	val's f1: 0.868421
[2956]	train's binary_logloss: 3.65951e-06	train's f1: 1	val's binary_logloss: 0.563717	val's f1: 0.868421
[2957]	train's binary_logloss: 3.65796e-06	train's f1: 1	val's binary_logloss: 0.563794	val's f1: 0.868421
[2958]	train's binary_logloss: 3.65658e-06	train's f1: 1	val's binary_logloss: 0.563543	val's f1: 0.868421
[2959]	train's binary_logloss: 3.6551e-06	train's f1: 1	val's binary_logloss: 0.563462	val's f1: 0.868421
[2960]	train's binary_logloss: 3.65399e-06	train's f1: 1	val's binary_logloss: 0.563563	val's f1: 0.868421
[2961]	train's binary_logloss: 3.65263e-06	train's f1: 1	val's binary_logloss: 0.563554	val's f1: 0.868421
[2962]	train's binary_logloss: 3.65148e-06	train's f1: 1	val's binary_logloss: 0.56361	val's f1: 0.868421
[2963]	train's binary_logloss: 3.65036e-06	train's f1: 1	val's binary_logloss: 0.563652	val's f1: 0.868421
[2964]	train's binary_logloss: 3.64877e-

In [197]:
nhek_lgb_pred_seq = nhek_lgb_seq.predict(nhek_seq_test_x)
f1_score(nhek_seq_test_y,prob2label(nhek_lgb_pred_seq))

0.8550185873605949

### Heka-S3

In [198]:
helas3_seq_train_x = helas3_original_data_json['X_train_seq']
helas3_seq_train_y = helas3_original_data_json['y_train_seq']

helas3_seq_test_x  = helas3_original_data_json['X_test_seq']
helas3_seq_test_y = helas3_original_data_json['y_test_seq']

helas3_seq_train_lgb,helas3_seq_valid_lgb,_ = generate_lgb_use_data(helas3_seq_train_x,
                                                               helas3_seq_train_y,
                                                               helas3_seq_test_x,
                                                               helas3_seq_test_y)

In [199]:
helas3_lgb_seq = train_lgb(helas3_seq_train_lgb,helas3_seq_valid_lgb,
                         lgb_param,num_round,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.684057	train's f1: 0.777029	val's binary_logloss: 0.687401	val's f1: 0.688525
[2]	train's binary_logloss: 0.6755	train's f1: 0.786897	val's binary_logloss: 0.682607	val's f1: 0.696774
[3]	train's binary_logloss: 0.667071	train's f1: 0.793103	val's binary_logloss: 0.677883	val's f1: 0.688525
[4]	train's binary_logloss: 0.659237	train's f1: 0.786394	val's binary_logloss: 0.673183	val's f1: 0.662162
[5]	train's binary_logloss: 0.651506	train's f1: 0.798246	val's binary_logloss: 0.668584	val's f1: 0.671141
[6]	train's binary_logloss: 0.644205	train's f1: 0.806156	val's binary_logloss: 0.663974	val's f1: 0.684564
[7]	train's binary_logloss: 0.636873	train's f1: 0.808199	val's binary_logloss: 0.660145	val's f1: 0.693333
[8]	train's binary_logloss: 0.630159	train's f1: 0.810771	val's binary_logloss: 0.656395	val's f1: 0.693333
[9]	train's binary_logloss: 0.623127	train's f1: 0.817181	val's binary_logloss: 0.652038	val's f1: 0.68942
[10]	train's binary_logloss: 0.

[101]	train's binary_logloss: 0.333761	train's f1: 0.979175	val's binary_logloss: 0.530498	val's f1: 0.722973
[102]	train's binary_logloss: 0.331794	train's f1: 0.97879	val's binary_logloss: 0.529917	val's f1: 0.727891
[103]	train's binary_logloss: 0.329724	train's f1: 0.979961	val's binary_logloss: 0.528291	val's f1: 0.732877
[104]	train's binary_logloss: 0.328156	train's f1: 0.979945	val's binary_logloss: 0.52862	val's f1: 0.730375
[105]	train's binary_logloss: 0.326226	train's f1: 0.980747	val's binary_logloss: 0.528349	val's f1: 0.734694
[106]	train's binary_logloss: 0.324448	train's f1: 0.98189	val's binary_logloss: 0.5285	val's f1: 0.730375
[107]	train's binary_logloss: 0.322537	train's f1: 0.98189	val's binary_logloss: 0.528277	val's f1: 0.730375
[108]	train's binary_logloss: 0.320574	train's f1: 0.98229	val's binary_logloss: 0.5272	val's f1: 0.726027
[109]	train's binary_logloss: 0.318769	train's f1: 0.982677	val's binary_logloss: 0.526246	val's f1: 0.730375
[110]	train's binar

[198]	train's binary_logloss: 0.205738	train's f1: 0.996845	val's binary_logloss: 0.505962	val's f1: 0.733564
[199]	train's binary_logloss: 0.204747	train's f1: 0.996845	val's binary_logloss: 0.505973	val's f1: 0.731034
[200]	train's binary_logloss: 0.203608	train's f1: 0.996845	val's binary_logloss: 0.505918	val's f1: 0.731034
[201]	train's binary_logloss: 0.202717	train's f1: 0.996845	val's binary_logloss: 0.506109	val's f1: 0.731034
[202]	train's binary_logloss: 0.201721	train's f1: 0.996845	val's binary_logloss: 0.505671	val's f1: 0.731034
[203]	train's binary_logloss: 0.200656	train's f1: 0.996845	val's binary_logloss: 0.50546	val's f1: 0.731034
[204]	train's binary_logloss: 0.199637	train's f1: 0.996845	val's binary_logloss: 0.505075	val's f1: 0.731034
[205]	train's binary_logloss: 0.198615	train's f1: 0.996845	val's binary_logloss: 0.504889	val's f1: 0.731034
[206]	train's binary_logloss: 0.197545	train's f1: 0.997239	val's binary_logloss: 0.504804	val's f1: 0.728522
[207]	train

[297]	train's binary_logloss: 0.12971	train's f1: 0.99921	val's binary_logloss: 0.493128	val's f1: 0.732203
[298]	train's binary_logloss: 0.129083	train's f1: 0.99921	val's binary_logloss: 0.492995	val's f1: 0.736486
[299]	train's binary_logloss: 0.128534	train's f1: 0.99921	val's binary_logloss: 0.493094	val's f1: 0.736486
[300]	train's binary_logloss: 0.127887	train's f1: 0.99921	val's binary_logloss: 0.493134	val's f1: 0.736486
[301]	train's binary_logloss: 0.127358	train's f1: 0.99921	val's binary_logloss: 0.49352	val's f1: 0.736486
[302]	train's binary_logloss: 0.126644	train's f1: 0.99921	val's binary_logloss: 0.492978	val's f1: 0.734007
[303]	train's binary_logloss: 0.126112	train's f1: 0.99921	val's binary_logloss: 0.492936	val's f1: 0.734007
[304]	train's binary_logloss: 0.125427	train's f1: 0.99921	val's binary_logloss: 0.492763	val's f1: 0.736486
[305]	train's binary_logloss: 0.124854	train's f1: 0.99921	val's binary_logloss: 0.492478	val's f1: 0.736486
[306]	train's binary_

[396]	train's binary_logloss: 0.0825622	train's f1: 1	val's binary_logloss: 0.492157	val's f1: 0.724832
[397]	train's binary_logloss: 0.0822874	train's f1: 1	val's binary_logloss: 0.492128	val's f1: 0.722973
[398]	train's binary_logloss: 0.081941	train's f1: 1	val's binary_logloss: 0.492735	val's f1: 0.720539
[399]	train's binary_logloss: 0.0815826	train's f1: 1	val's binary_logloss: 0.49236	val's f1: 0.725424
[400]	train's binary_logloss: 0.0812294	train's f1: 1	val's binary_logloss: 0.492386	val's f1: 0.727891
[401]	train's binary_logloss: 0.0808805	train's f1: 1	val's binary_logloss: 0.492257	val's f1: 0.725424
[402]	train's binary_logloss: 0.0804356	train's f1: 1	val's binary_logloss: 0.491968	val's f1: 0.725424
[403]	train's binary_logloss: 0.0801576	train's f1: 1	val's binary_logloss: 0.492073	val's f1: 0.725424
[404]	train's binary_logloss: 0.0797923	train's f1: 1	val's binary_logloss: 0.492003	val's f1: 0.722973
[405]	train's binary_logloss: 0.0794837	train's f1: 1	val's binary

...

[2585]	train's binary_logloss: 8.99431e-06	train's f1: 1	val's binary_logloss: 0.845114	val's f1: 0.749117
[2586]	train's binary_logloss: 8.97706e-06	train's f1: 1	val's binary_logloss: 0.845534	val's f1: 0.749117
[2587]	train's binary_logloss: 8.96362e-06	train's f1: 1	val's binary_logloss: 0.845278	val's f1: 0.749117
[2588]	train's binary_logloss: 8.9474e-06	train's f1: 1	val's binary_logloss: 0.845368	val's f1: 0.749117
[2589]	train's binary_logloss: 8.92901e-06	train's f1: 1	val's binary_logloss: 0.84542	val's f1: 0.749117
[2590]	train's binary_logloss: 8.91505e-06	train's f1: 1	val's binary_logloss: 0.845797	val's f1: 0.749117
[2591]	train's binary_logloss: 8.90109e-06	train's f1: 1	val's binary_logloss: 0.845853	val's f1: 0.749117
[2592]	train's binary_logloss: 8.88837e-06	train's f1: 1	val's binary_logloss: 0.845776	val's f1: 0.749117
[2593]	train's binary_logloss: 8.8702e-06	train's f1: 1	val's binary_logloss: 0.845885	val's f1: 0.749117
[2594]	train's binary_logloss: 8.85581e-

[2683]	train's binary_logloss: 7.72072e-06	train's f1: 1	val's binary_logloss: 0.853765	val's f1: 0.746479
[2684]	train's binary_logloss: 7.70963e-06	train's f1: 1	val's binary_logloss: 0.853725	val's f1: 0.746479
[2685]	train's binary_logloss: 7.69939e-06	train's f1: 1	val's binary_logloss: 0.85368	val's f1: 0.746479
[2686]	train's binary_logloss: 7.68795e-06	train's f1: 1	val's binary_logloss: 0.853816	val's f1: 0.746479
[2687]	train's binary_logloss: 7.67716e-06	train's f1: 1	val's binary_logloss: 0.85418	val's f1: 0.746479
[2688]	train's binary_logloss: 7.66699e-06	train's f1: 1	val's binary_logloss: 0.854246	val's f1: 0.746479
[2689]	train's binary_logloss: 7.65631e-06	train's f1: 1	val's binary_logloss: 0.8544	val's f1: 0.746479
[2690]	train's binary_logloss: 7.64725e-06	train's f1: 1	val's binary_logloss: 0.854662	val's f1: 0.746479
[2691]	train's binary_logloss: 7.6366e-06	train's f1: 1	val's binary_logloss: 0.854617	val's f1: 0.746479
[2692]	train's binary_logloss: 7.62572e-06

[2786]	train's binary_logloss: 6.77508e-06	train's f1: 1	val's binary_logloss: 0.861592	val's f1: 0.750877
[2787]	train's binary_logloss: 6.76794e-06	train's f1: 1	val's binary_logloss: 0.861792	val's f1: 0.748252
[2788]	train's binary_logloss: 6.75957e-06	train's f1: 1	val's binary_logloss: 0.861845	val's f1: 0.750877
[2789]	train's binary_logloss: 6.75221e-06	train's f1: 1	val's binary_logloss: 0.861876	val's f1: 0.74386
[2790]	train's binary_logloss: 6.74466e-06	train's f1: 1	val's binary_logloss: 0.862012	val's f1: 0.748252
[2791]	train's binary_logloss: 6.73699e-06	train's f1: 1	val's binary_logloss: 0.862066	val's f1: 0.748252
[2792]	train's binary_logloss: 6.72867e-06	train's f1: 1	val's binary_logloss: 0.862149	val's f1: 0.748252
[2793]	train's binary_logloss: 6.72073e-06	train's f1: 1	val's binary_logloss: 0.86212	val's f1: 0.748252
[2794]	train's binary_logloss: 6.71387e-06	train's f1: 1	val's binary_logloss: 0.862287	val's f1: 0.748252
[2795]	train's binary_logloss: 6.70509e

[2892]	train's binary_logloss: 6.04612e-06	train's f1: 1	val's binary_logloss: 0.868761	val's f1: 0.748252
[2893]	train's binary_logloss: 6.04067e-06	train's f1: 1	val's binary_logloss: 0.868796	val's f1: 0.748252
[2894]	train's binary_logloss: 6.03523e-06	train's f1: 1	val's binary_logloss: 0.869041	val's f1: 0.748252
[2895]	train's binary_logloss: 6.02993e-06	train's f1: 1	val's binary_logloss: 0.869177	val's f1: 0.748252
[2896]	train's binary_logloss: 6.02521e-06	train's f1: 1	val's binary_logloss: 0.869506	val's f1: 0.748252
[2897]	train's binary_logloss: 6.0201e-06	train's f1: 1	val's binary_logloss: 0.869403	val's f1: 0.748252
[2898]	train's binary_logloss: 6.0138e-06	train's f1: 1	val's binary_logloss: 0.869476	val's f1: 0.748252
[2899]	train's binary_logloss: 6.00731e-06	train's f1: 1	val's binary_logloss: 0.86959	val's f1: 0.748252
[2900]	train's binary_logloss: 6.00126e-06	train's f1: 1	val's binary_logloss: 0.869389	val's f1: 0.748252
[2901]	train's binary_logloss: 5.99702e-

[3000]	train's binary_logloss: 5.4912e-06	train's f1: 1	val's binary_logloss: 0.873681	val's f1: 0.752613


In [200]:
helas3_lgb_pred_seq = helas3_lgb_seq.predict(helas3_seq_test_x)
f1_score(helas3_seq_test_y,prob2label(helas3_lgb_pred_seq))

0.7880512091038406

## SVM

In [279]:
k562_svm_seq = svm(k562_seq_train_x,k562_seq_train_y,None,None)
imr90_svm_seq = svm(imr90_seq_train_x,imr90_seq_train_y,None,None)
gm12878_svm_seq = svm(gm12878_seq_train_x,gm12878_seq_train_y,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [280]:
huvec_svm_seq = svm(huvec_seq_train_x,huvec_seq_train_y,None,None)
nhek_svm_seq = svm(nhek_seq_train_x,nhek_seq_train_y,None,None)
helas3_svm_seq = svm(helas3_seq_train_x,helas3_seq_train_y,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [281]:
k562_svm_pred_seq = k562_svm_seq.predict(k562_seq_test_x)
f1_score(k562_seq_test_y,k562_svm_pred_seq)

0.6633663366336634

In [ ]:
imr90_svm_pred_seq = imr90_svm_seq.predict(imr90_seq_test_x)
f1_score(imr90_seq_test_y,imr90_svm_pred_seq)

In [283]:
gm12878_svm_pred_seq = gm12878_svm_seq.predict(gm12878_seq_test_x)
f1_score(gm12878_seq_test_y,gm12878_svm_pred_seq)

0.6758286176232821

In [ ]:
huvec_svm_pred_seq = huvec_svm_seq.predict(huvec_seq_test_x)
f1_score(huvec_seq_test_y,huvec_svm_pred_seq)

In [ ]:
nhek_svm_pred_seq = nhek_svm_seq.predict(nhek_seq_test_x)
f1_score(nhek_seq_test_y,nhek_svm_pred_seq)

In [286]:
helas3_svm_pred_seq = helas3_svm_seq.predict(helas3_seq_test_x)
f1_score(helas3_seq_test_y,helas3_svm_pred_seq)

0.470404984423676

## Adaboost

In [287]:
k562_ada_seq = adaboost(k562_seq_train_x,k562_seq_train_y,None,None)
imr90_ada_seq = adaboost(imr90_seq_train_x,imr90_seq_train_y,None,None)
gm12878_ada_seq = adaboost(gm12878_seq_train_x,gm12878_seq_train_y,None,None)

In [288]:
huvec_ada_seq = adaboost(huvec_seq_train_x,huvec_seq_train_y,None,None)
nhek_ada_seq = adaboost(nhek_seq_train_x,nhek_seq_train_y,None,None)
helas3_ada_seq = adaboost(helas3_seq_train_x,helas3_seq_train_y,None,None)

In [289]:
k562_ada_pred_seq = k562_ada_seq.predict(k562_seq_test_x)
f1_score(k562_seq_test_y,k562_ada_pred_seq)

0.7113276492082825

In [290]:

imr90_ada_pred_seq = imr90_ada_seq.predict(imr90_seq_test_x)
f1_score(imr90_seq_test_y,imr90_ada_pred_seq)

0.6802443991853361

In [291]:
gm12878_ada_pred_seq = gm12878_ada_seq.predict(gm12878_seq_test_x)
f1_score(gm12878_seq_test_y,gm12878_ada_pred_seq)

0.6695938529088914

In [292]:
huvec_ada_pred_seq = huvec_ada_seq.predict(huvec_seq_test_x)
f1_score(huvec_seq_test_y,huvec_ada_pred_seq)

0.6764227642276422

In [293]:
nhek_ada_pred_seq = nhek_ada_seq.predict(nhek_seq_test_x)
f1_score(nhek_seq_test_y,nhek_ada_pred_seq)

0.7757352941176471

In [294]:
helas3_ada_pred_seq = helas3_ada_seq.predict(helas3_seq_test_x)
f1_score(helas3_seq_test_y,helas3_ada_pred_seq)

0.7275204359673024

# Save Model

## Save model

In [201]:
k562_lgb_seq.save_model('./model/LGB/k562_seq_lgb.txt', num_iteration=k562_lgb_seq.best_iteration)
imr90_lgb_seq.save_model('./model/LGB/img90_seq_lgb.txt', num_iteration=imr90_lgb_seq.best_iteration)
gm12878_lgb_seq.save_model('./model/LGB/gm12878_seq_lgb.txt', num_iteration=gm12878_lgb_seq.best_iteration)

In [202]:
huvec_lgb_seq.save_model('./model/LGB/huvec_seq_lgb.txt', num_iteration=huvec_lgb_seq.best_iteration)
nhek_lgb_seq.save_model('./model/LGB/nhek_seq_lgb.txt', num_iteration=nhek_lgb_seq.best_iteration)
helas3_lgb_seq.save_model('./model/LGB/helas3_seq_lgb.txt', num_iteration=helas3_lgb_seq.best_iteration)

In [295]:
joblib.dump(k562_svm_seq,'./model/RF/k562_svm_seq.model')
joblib.dump(imr90_svm_seq,'./model/RF/imr90_svm_seq.model')
joblib.dump(gm12878_svm_seq,'./model/RF/gm12878_svm_seq.model')

['./model/RF/gm12878_svm_seq.model']

In [296]:
joblib.dump(huvec_svm_seq,'./model/RF/huvec_svm_seq.model')
joblib.dump(nhek_svm_seq,'./model/RF/nhek_svm_seq.model')
joblib.dump(helas3_svm_seq,'./model/RF/helas3_svm_seq.model')

['./model/RF/helas3_svm_seq.model']

In [297]:
joblib.dump(k562_ada_seq,'./model/Adaboost/k562_ada_seq.model')
joblib.dump(imr90_ada_seq,'./model/Adaboost/imr90_ada_seq.model')
joblib.dump(gm12878_ada_seq,'./model/Adaboost/gm12878_ada_seq.model')

['./model/Adaboost/gm12878_ada_seq.model']

In [298]:
joblib.dump(huvec_ada_seq,'./model/Adaboost/huvec_ada_seq.model')
joblib.dump(nhek_ada_seq,'./model/Adaboost/nhek_ada_seq.model')
joblib.dump(helas3_ada_seq,'./model/Adaboost/helas3_ada_seq.model')

['./model/Adaboost/helas3_ada_seq.model']

## Save Data

* ########################################################################################

# Protein+Sequence

In [13]:
def get_lgb_feature_imp(model,boundry):
    feature_imp_val = model.feature_importance()
    feature_name = model.feature_name()
    feature_imp = np.c_[feature_name,feature_imp_val]
    feature_imp = pd.DataFrame(feature_imp,columns=['feature_name','feature_score'])
    feature_imp = feature_imp.sort_values(by='feature_score',ascending=False)
    feature_imp['feature_score'] = feature_imp['feature_score'].astype(float)
    feature_imp = feature_imp[feature_imp['feature_score']>=boundry]
    return feature_imp

In [14]:
k562_lgb_protein = lgb.Booster(model_file='./model/LGB/k562_protein_lgb.txt')
k562_protein_features = get_lgb_feature_imp(k562_lgb_protein,10)
k562_protein_features = k562_protein_features['feature_name'].tolist()

k562_lgb_seq = lgb.Booster(model_file='./model/LGB/k562_seq_lgb.txt')
k562_seq_features = get_lgb_feature_imp(k562_lgb_seq,150)
k562_seq_features = k562_seq_features['feature_name'].tolist()

In [15]:
imr90_lgb_protein = lgb.Booster(model_file='./model/LGB/img90_protein_lgb.txt')
imr90_protein_features = get_lgb_feature_imp(imr90_lgb_protein,10)
imr90_protein_features = imr90_protein_features['feature_name'].tolist()

imr90_lgb_seq = lgb.Booster(model_file='./model/LGB/img90_seq_lgb.txt')
imr90_seq_features = get_lgb_feature_imp(imr90_lgb_seq,100)
imr90_seq_features = imr90_seq_features['feature_name'].tolist()

In [16]:
gm12878_lgb_protein = lgb.Booster(model_file='./model/LGB/gm12878_protein_lgb.txt')
gm12878_protein_features = get_lgb_feature_imp(gm12878_lgb_protein,10)
gm12878_protein_features = gm12878_protein_features['feature_name'].tolist()

gm12878_lgb_seq = lgb.Booster(model_file='./model/LGB/gm12878_seq_lgb.txt')
gm12878_seq_features = get_lgb_feature_imp(gm12878_lgb_seq,150)
gm12878_seq_features = gm12878_seq_features['feature_name'].tolist()

In [17]:
huvec_lgb_protein = lgb.Booster(model_file='./model/LGB/huvec_protein_lgb.txt')
huvec_protein_features = get_lgb_feature_imp(huvec_lgb_protein,10)
huvec_protein_features = huvec_protein_features['feature_name'].tolist()

huvec_lgb_seq = lgb.Booster(model_file='./model/LGB/huvec_seq_lgb.txt')
huvec_seq_features = get_lgb_feature_imp(huvec_lgb_seq,50)
huvec_seq_features = huvec_seq_features['feature_name'].tolist()

In [18]:
nhek_lgb_protein = lgb.Booster(model_file='./model/LGB/nhek_protein_lgb.txt')
nhek_protein_features = get_lgb_feature_imp(nhek_lgb_protein,10)
nhek_protein_features = nhek_protein_features['feature_name'].tolist()

nhek_lgb_seq = lgb.Booster(model_file='./model/LGB/nhek_seq_lgb.txt')
nhek_seq_features = get_lgb_feature_imp(nhek_lgb_seq,100)
nhek_seq_features = nhek_seq_features['feature_name'].tolist()

In [20]:
helas3_lgb_protein = lgb.Booster(model_file='./model/LGB/helas3_protein_lgb.txt')
helas3_protein_features = get_lgb_feature_imp(helas3_lgb_protein,10)
helas3_protein_features = helas3_protein_features['feature_name'].tolist()

helas3_lgb_seq = lgb.Booster(model_file='./model/LGB/helas3_seq_lgb.txt')
helas3_seq_features = get_lgb_feature_imp(helas3_lgb_seq,100)
helas3_seq_features = helas3_seq_features['feature_name'].tolist()

In [ ]:
#############################################

In [21]:
k562_protein_features.extend(k562_seq_features)
k562_use_features = k562_protein_features

gm12878_protein_features.extend(gm12878_seq_features)
gm12878_use_features = gm12878_protein_features

imr90_protein_features.extend(imr90_seq_features)
imr90_use_features = imr90_protein_features


In [22]:
huvec_protein_features.extend(huvec_seq_features)
huvec_use_features = huvec_protein_features

nhek_protein_features.extend(nhek_seq_features)
nhek_use_features = nhek_protein_features

helas3_protein_features.extend(helas3_seq_features)
helas3_use_features = helas3_protein_features

In [25]:
### Save used
save_used_dict = {'k562':k562_use_features,
                 'imr90':imr90_use_features,
                 'gm12878':gm12878_use_features,
                 'huvec':huvec_use_features,
                 'nhek':nhek_use_features,
                 'helas3':helas3_use_features}

pickle.dump(save_used_dict,open('./mid-data/used_feature.pkl','wb'))

## LGB

### k562

In [211]:
#k562_merged_train_x,k562_merged_test_x,k562_merged_train_y,k562_merged_test_y = spit_merged(K562_merged)

k562_merged_train_x = k562_original_data_json['X_train_all']
k562_merged_train_y = k562_original_data_json['y_train_all']
k562_merged_test_x = k562_original_data_json['X_test_all']
k562_merged_test_y = k562_original_data_json['y_test_all']

k562_merged_train_x = k562_merged_train_x[k562_use_features]
k562_merged_test_x = k562_merged_test_x[k562_use_features]


k562_merged_train_lgb,k562_merged_valid_lgb,_ = generate_lgb_use_data(k562_merged_train_x,
                                                               k562_merged_train_y,
                                                               k562_merged_test_x,
                                                               k562_merged_test_y)

In [212]:
k562_lgb_merged = train_lgb(k562_merged_train_lgb,k562_merged_valid_lgb,
                         lgb_param,num_round+700,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.681356	train's f1: 0.799441	val's binary_logloss: 0.685004	val's f1: 0.713864
[2]	train's binary_logloss: 0.670186	train's f1: 0.808496	val's binary_logloss: 0.677736	val's f1: 0.718563
[3]	train's binary_logloss: 0.659647	train's f1: 0.816197	val's binary_logloss: 0.669461	val's f1: 0.727273
[4]	train's binary_logloss: 0.649071	train's f1: 0.820244	val's binary_logloss: 0.662564	val's f1: 0.735905
[5]	train's binary_logloss: 0.638676	train's f1: 0.832576	val's binary_logloss: 0.655058	val's f1: 0.735905
[6]	train's binary_logloss: 0.628261	train's f1: 0.838391	val's binary_logloss: 0.648103	val's f1: 0.742515
[7]	train's binary_logloss: 0.618724	train's f1: 0.848268	val's binary_logloss: 0.640466	val's f1: 0.762195
[8]	train's binary_logloss: 0.609094	train's f1: 0.855404	val's binary_logloss: 0.634722	val's f1: 0.770642
[9]	train's binary_logloss: 0.599894	train's f1: 0.863751	val's binary_logloss: 0.627488	val's f1: 0.780186
[10]	train's binary_logloss:

[78]	train's binary_logloss: 0.258726	train's f1: 0.986224	val's binary_logloss: 0.414984	val's f1: 0.859701
[79]	train's binary_logloss: 0.256193	train's f1: 0.986582	val's binary_logloss: 0.413813	val's f1: 0.859701
[80]	train's binary_logloss: 0.253566	train's f1: 0.98693	val's binary_logloss: 0.411828	val's f1: 0.862275
[81]	train's binary_logloss: 0.251165	train's f1: 0.987646	val's binary_logloss: 0.410108	val's f1: 0.870871
[82]	train's binary_logloss: 0.2487	train's f1: 0.987288	val's binary_logloss: 0.408235	val's f1: 0.864048
[83]	train's binary_logloss: 0.246266	train's f1: 0.987637	val's binary_logloss: 0.406217	val's f1: 0.86747
[84]	train's binary_logloss: 0.243781	train's f1: 0.987637	val's binary_logloss: 0.405101	val's f1: 0.866667
[85]	train's binary_logloss: 0.241402	train's f1: 0.988693	val's binary_logloss: 0.403385	val's f1: 0.866667
[86]	train's binary_logloss: 0.238976	train's f1: 0.989764	val's binary_logloss: 0.401881	val's f1: 0.866667
[87]	train's binary_log

[155]	train's binary_logloss: 0.125559	train's f1: 0.999647	val's binary_logloss: 0.33657	val's f1: 0.889571
[156]	train's binary_logloss: 0.124463	train's f1: 0.999647	val's binary_logloss: 0.335846	val's f1: 0.895062
[157]	train's binary_logloss: 0.123354	train's f1: 0.999647	val's binary_logloss: 0.335491	val's f1: 0.892308
[158]	train's binary_logloss: 0.122147	train's f1: 0.999647	val's binary_logloss: 0.334963	val's f1: 0.892308
[159]	train's binary_logloss: 0.121149	train's f1: 0.999647	val's binary_logloss: 0.333942	val's f1: 0.897833
[160]	train's binary_logloss: 0.120167	train's f1: 0.999647	val's binary_logloss: 0.333824	val's f1: 0.897833
[161]	train's binary_logloss: 0.119084	train's f1: 0.999647	val's binary_logloss: 0.333105	val's f1: 0.897833
[162]	train's binary_logloss: 0.118044	train's f1: 1	val's binary_logloss: 0.33242	val's f1: 0.895062
[163]	train's binary_logloss: 0.116968	train's f1: 1	val's binary_logloss: 0.331891	val's f1: 0.895062
[164]	train's binary_loglo

[239]	train's binary_logloss: 0.0611706	train's f1: 1	val's binary_logloss: 0.304622	val's f1: 0.892308
[240]	train's binary_logloss: 0.0606204	train's f1: 1	val's binary_logloss: 0.304099	val's f1: 0.892308
[241]	train's binary_logloss: 0.0601083	train's f1: 1	val's binary_logloss: 0.303588	val's f1: 0.892308
[242]	train's binary_logloss: 0.0595779	train's f1: 1	val's binary_logloss: 0.303073	val's f1: 0.892308
[243]	train's binary_logloss: 0.0590452	train's f1: 1	val's binary_logloss: 0.302478	val's f1: 0.889571
[244]	train's binary_logloss: 0.0585722	train's f1: 1	val's binary_logloss: 0.302399	val's f1: 0.886154
[245]	train's binary_logloss: 0.0580708	train's f1: 1	val's binary_logloss: 0.302036	val's f1: 0.886154
[246]	train's binary_logloss: 0.0575976	train's f1: 1	val's binary_logloss: 0.302277	val's f1: 0.886154
[247]	train's binary_logloss: 0.057061	train's f1: 1	val's binary_logloss: 0.301644	val's f1: 0.888889
[248]	train's binary_logloss: 0.0565815	train's f1: 1	val's binar

[320]	train's binary_logloss: 0.031182	train's f1: 1	val's binary_logloss: 0.289136	val's f1: 0.895062
[321]	train's binary_logloss: 0.0309343	train's f1: 1	val's binary_logloss: 0.289618	val's f1: 0.895062
[322]	train's binary_logloss: 0.0306827	train's f1: 1	val's binary_logloss: 0.289463	val's f1: 0.895062
[323]	train's binary_logloss: 0.0304349	train's f1: 1	val's binary_logloss: 0.289179	val's f1: 0.897833
[324]	train's binary_logloss: 0.0301733	train's f1: 1	val's binary_logloss: 0.289046	val's f1: 0.895062
[325]	train's binary_logloss: 0.0299245	train's f1: 1	val's binary_logloss: 0.289126	val's f1: 0.895062
[326]	train's binary_logloss: 0.0296733	train's f1: 1	val's binary_logloss: 0.288962	val's f1: 0.895062
[327]	train's binary_logloss: 0.0294351	train's f1: 1	val's binary_logloss: 0.288788	val's f1: 0.897833
[328]	train's binary_logloss: 0.0292189	train's f1: 1	val's binary_logloss: 0.288708	val's f1: 0.895062
[329]	train's binary_logloss: 0.0289804	train's f1: 1	val's binar

...

[3237]	train's binary_logloss: 1.51558e-06	train's f1: 1	val's binary_logloss: 0.456567	val's f1: 0.897833
[3238]	train's binary_logloss: 1.51528e-06	train's f1: 1	val's binary_logloss: 0.456617	val's f1: 0.897833
[3239]	train's binary_logloss: 1.51493e-06	train's f1: 1	val's binary_logloss: 0.456587	val's f1: 0.897833
[3240]	train's binary_logloss: 1.51461e-06	train's f1: 1	val's binary_logloss: 0.45658	val's f1: 0.897833
[3241]	train's binary_logloss: 1.51429e-06	train's f1: 1	val's binary_logloss: 0.456648	val's f1: 0.897833
[3242]	train's binary_logloss: 1.51394e-06	train's f1: 1	val's binary_logloss: 0.456665	val's f1: 0.897833
[3243]	train's binary_logloss: 1.51361e-06	train's f1: 1	val's binary_logloss: 0.45669	val's f1: 0.897833
[3244]	train's binary_logloss: 1.51328e-06	train's f1: 1	val's binary_logloss: 0.45674	val's f1: 0.897833
[3245]	train's binary_logloss: 1.51296e-06	train's f1: 1	val's binary_logloss: 0.456776	val's f1: 0.897833
[3246]	train's binary_logloss: 1.51245e-

[3333]	train's binary_logloss: 1.4807e-06	train's f1: 1	val's binary_logloss: 0.457361	val's f1: 0.897833
[3334]	train's binary_logloss: 1.48039e-06	train's f1: 1	val's binary_logloss: 0.457319	val's f1: 0.897833
[3335]	train's binary_logloss: 1.48004e-06	train's f1: 1	val's binary_logloss: 0.457216	val's f1: 0.897833
[3336]	train's binary_logloss: 1.47955e-06	train's f1: 1	val's binary_logloss: 0.457226	val's f1: 0.897833
[3337]	train's binary_logloss: 1.47921e-06	train's f1: 1	val's binary_logloss: 0.457241	val's f1: 0.897833
[3338]	train's binary_logloss: 1.47888e-06	train's f1: 1	val's binary_logloss: 0.457232	val's f1: 0.897833
[3339]	train's binary_logloss: 1.47859e-06	train's f1: 1	val's binary_logloss: 0.457264	val's f1: 0.897833
[3340]	train's binary_logloss: 1.47801e-06	train's f1: 1	val's binary_logloss: 0.457232	val's f1: 0.897833
[3341]	train's binary_logloss: 1.47766e-06	train's f1: 1	val's binary_logloss: 0.457209	val's f1: 0.897833
[3342]	train's binary_logloss: 1.47738

[3429]	train's binary_logloss: 1.44921e-06	train's f1: 1	val's binary_logloss: 0.458216	val's f1: 0.897833
[3430]	train's binary_logloss: 1.44893e-06	train's f1: 1	val's binary_logloss: 0.458207	val's f1: 0.897833
[3431]	train's binary_logloss: 1.44866e-06	train's f1: 1	val's binary_logloss: 0.458205	val's f1: 0.897833
[3432]	train's binary_logloss: 1.44836e-06	train's f1: 1	val's binary_logloss: 0.458241	val's f1: 0.897833
[3433]	train's binary_logloss: 1.44794e-06	train's f1: 1	val's binary_logloss: 0.458292	val's f1: 0.897833
[3434]	train's binary_logloss: 1.44762e-06	train's f1: 1	val's binary_logloss: 0.45825	val's f1: 0.897833
[3435]	train's binary_logloss: 1.44732e-06	train's f1: 1	val's binary_logloss: 0.45824	val's f1: 0.897833
[3436]	train's binary_logloss: 1.44701e-06	train's f1: 1	val's binary_logloss: 0.458216	val's f1: 0.897833
[3437]	train's binary_logloss: 1.4467e-06	train's f1: 1	val's binary_logloss: 0.45826	val's f1: 0.897833
[3438]	train's binary_logloss: 1.44641e-0

[3524]	train's binary_logloss: 1.41996e-06	train's f1: 1	val's binary_logloss: 0.458703	val's f1: 0.897833
[3525]	train's binary_logloss: 1.41964e-06	train's f1: 1	val's binary_logloss: 0.458681	val's f1: 0.897833
[3526]	train's binary_logloss: 1.41903e-06	train's f1: 1	val's binary_logloss: 0.458751	val's f1: 0.897833
[3527]	train's binary_logloss: 1.41874e-06	train's f1: 1	val's binary_logloss: 0.458746	val's f1: 0.897833
[3528]	train's binary_logloss: 1.41847e-06	train's f1: 1	val's binary_logloss: 0.458781	val's f1: 0.897833
[3529]	train's binary_logloss: 1.41821e-06	train's f1: 1	val's binary_logloss: 0.458774	val's f1: 0.897833
[3530]	train's binary_logloss: 1.41788e-06	train's f1: 1	val's binary_logloss: 0.458782	val's f1: 0.897833
[3531]	train's binary_logloss: 1.4176e-06	train's f1: 1	val's binary_logloss: 0.458844	val's f1: 0.897833
[3532]	train's binary_logloss: 1.41729e-06	train's f1: 1	val's binary_logloss: 0.458838	val's f1: 0.897833
[3533]	train's binary_logloss: 1.41701

[3619]	train's binary_logloss: 1.39224e-06	train's f1: 1	val's binary_logloss: 0.459663	val's f1: 0.897833
[3620]	train's binary_logloss: 1.39187e-06	train's f1: 1	val's binary_logloss: 0.459646	val's f1: 0.897833
[3621]	train's binary_logloss: 1.3916e-06	train's f1: 1	val's binary_logloss: 0.459654	val's f1: 0.897833
[3622]	train's binary_logloss: 1.39133e-06	train's f1: 1	val's binary_logloss: 0.459649	val's f1: 0.897833
[3623]	train's binary_logloss: 1.39098e-06	train's f1: 1	val's binary_logloss: 0.459602	val's f1: 0.897833
[3624]	train's binary_logloss: 1.39069e-06	train's f1: 1	val's binary_logloss: 0.459607	val's f1: 0.897833
[3625]	train's binary_logloss: 1.39042e-06	train's f1: 1	val's binary_logloss: 0.459611	val's f1: 0.897833
[3626]	train's binary_logloss: 1.39016e-06	train's f1: 1	val's binary_logloss: 0.459659	val's f1: 0.897833
[3627]	train's binary_logloss: 1.3899e-06	train's f1: 1	val's binary_logloss: 0.459626	val's f1: 0.897833
[3628]	train's binary_logloss: 1.38963e

In [213]:
k562_lgb_pred_merged = k562_lgb_merged.predict(k562_merged_test_x,num_iteration=k562_lgb_merged.best_iteration)
f1_score(k562_merged_test_y,prob2label(k562_lgb_pred_merged))

0.905055487053021

In [214]:
roc_auc_score(k562_merged_test_y,k562_lgb_pred_merged)

0.9570553324294595

### IMR90

In [217]:
imr90_merged_train_x = imr90_original_data_json['X_train_all']
imr90_merged_train_y = imr90_original_data_json['y_train_all']
imr90_merged_test_x = imr90_original_data_json['X_test_all']
imr90_merged_test_y = imr90_original_data_json['y_test_all']

imr90_merged_train_x = imr90_merged_train_x[imr90_use_features]
imr90_merged_test_x = imr90_merged_test_x[imr90_use_features]

imr90_merged_train_lgb,imr90_merged_valid_lgb,_ = generate_lgb_use_data(imr90_merged_train_x,
                                                               imr90_merged_train_y,
                                                               imr90_merged_test_x,
                                                               imr90_merged_test_y)

In [218]:
imr90_lgb_merged = train_lgb(imr90_merged_train_lgb,imr90_merged_valid_lgb,
                         lgb_param,num_round+800,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.680788	train's f1: 0.798137	val's binary_logloss: 0.683681	val's f1: 0.748899
[2]	train's binary_logloss: 0.668536	train's f1: 0.807835	val's binary_logloss: 0.677087	val's f1: 0.741379
[3]	train's binary_logloss: 0.657076	train's f1: 0.847475	val's binary_logloss: 0.671415	val's f1: 0.739496
[4]	train's binary_logloss: 0.646312	train's f1: 0.832897	val's binary_logloss: 0.663451	val's f1: 0.751092
[5]	train's binary_logloss: 0.635419	train's f1: 0.857895	val's binary_logloss: 0.656532	val's f1: 0.753247
[6]	train's binary_logloss: 0.624638	train's f1: 0.857595	val's binary_logloss: 0.651486	val's f1: 0.735931
[7]	train's binary_logloss: 0.614531	train's f1: 0.858351	val's binary_logloss: 0.647121	val's f1: 0.748899
[8]	train's binary_logloss: 0.605143	train's f1: 0.865719	val's binary_logloss: 0.642265	val's f1: 0.763158
[9]	train's binary_logloss: 0.595667	train's f1: 0.86747	val's binary_logloss: 0.637975	val's f1: 0.748899
[10]	train's binary_logloss: 

[85]	train's binary_logloss: 0.23169	train's f1: 0.993443	val's binary_logloss: 0.466031	val's f1: 0.817778
[86]	train's binary_logloss: 0.229115	train's f1: 0.993435	val's binary_logloss: 0.465267	val's f1: 0.815789
[87]	train's binary_logloss: 0.226543	train's f1: 0.993986	val's binary_logloss: 0.464164	val's f1: 0.819383
[88]	train's binary_logloss: 0.224153	train's f1: 0.993986	val's binary_logloss: 0.463374	val's f1: 0.819383
[89]	train's binary_logloss: 0.221674	train's f1: 0.993986	val's binary_logloss: 0.461431	val's f1: 0.821429
[90]	train's binary_logloss: 0.219443	train's f1: 0.99453	val's binary_logloss: 0.46022	val's f1: 0.823009
[91]	train's binary_logloss: 0.217135	train's f1: 0.99453	val's binary_logloss: 0.45969	val's f1: 0.817778
[92]	train's binary_logloss: 0.215074	train's f1: 0.995079	val's binary_logloss: 0.458755	val's f1: 0.823009
[93]	train's binary_logloss: 0.212684	train's f1: 0.995079	val's binary_logloss: 0.457775	val's f1: 0.819383
[94]	train's binary_logl

[169]	train's binary_logloss: 0.101142	train's f1: 1	val's binary_logloss: 0.423975	val's f1: 0.828194
[170]	train's binary_logloss: 0.100269	train's f1: 1	val's binary_logloss: 0.423965	val's f1: 0.828194
[171]	train's binary_logloss: 0.0993224	train's f1: 1	val's binary_logloss: 0.423628	val's f1: 0.828194
[172]	train's binary_logloss: 0.0983673	train's f1: 1	val's binary_logloss: 0.422837	val's f1: 0.828194
[173]	train's binary_logloss: 0.0974473	train's f1: 1	val's binary_logloss: 0.423024	val's f1: 0.828194
[174]	train's binary_logloss: 0.0965242	train's f1: 1	val's binary_logloss: 0.422924	val's f1: 0.828194
[175]	train's binary_logloss: 0.0956394	train's f1: 1	val's binary_logloss: 0.422855	val's f1: 0.828194
[176]	train's binary_logloss: 0.0947474	train's f1: 1	val's binary_logloss: 0.422624	val's f1: 0.824561
[177]	train's binary_logloss: 0.0938023	train's f1: 1	val's binary_logloss: 0.421859	val's f1: 0.824561
[178]	train's binary_logloss: 0.092936	train's f1: 1	val's binary_

[252]	train's binary_logloss: 0.0473078	train's f1: 1	val's binary_logloss: 0.417475	val's f1: 0.828194
[253]	train's binary_logloss: 0.04688	train's f1: 1	val's binary_logloss: 0.417909	val's f1: 0.828194
[254]	train's binary_logloss: 0.0464607	train's f1: 1	val's binary_logloss: 0.417365	val's f1: 0.828194
[255]	train's binary_logloss: 0.0460449	train's f1: 1	val's binary_logloss: 0.417604	val's f1: 0.833333
[256]	train's binary_logloss: 0.0456306	train's f1: 1	val's binary_logloss: 0.417565	val's f1: 0.833333
[257]	train's binary_logloss: 0.0452204	train's f1: 1	val's binary_logloss: 0.417671	val's f1: 0.833333
[258]	train's binary_logloss: 0.0448533	train's f1: 1	val's binary_logloss: 0.417975	val's f1: 0.833333
[259]	train's binary_logloss: 0.0444727	train's f1: 1	val's binary_logloss: 0.418724	val's f1: 0.833333
[260]	train's binary_logloss: 0.0440688	train's f1: 1	val's binary_logloss: 0.417784	val's f1: 0.833333
[261]	train's binary_logloss: 0.0437034	train's f1: 1	val's binary

[336]	train's binary_logloss: 0.0228577	train's f1: 1	val's binary_logloss: 0.420545	val's f1: 0.833333
[337]	train's binary_logloss: 0.0226413	train's f1: 1	val's binary_logloss: 0.420752	val's f1: 0.833333
[338]	train's binary_logloss: 0.0224499	train's f1: 1	val's binary_logloss: 0.421343	val's f1: 0.833333
[339]	train's binary_logloss: 0.0222791	train's f1: 1	val's binary_logloss: 0.421825	val's f1: 0.833333
[340]	train's binary_logloss: 0.0220807	train's f1: 1	val's binary_logloss: 0.421334	val's f1: 0.833333
[341]	train's binary_logloss: 0.0218787	train's f1: 1	val's binary_logloss: 0.421163	val's f1: 0.833333
[342]	train's binary_logloss: 0.0216861	train's f1: 1	val's binary_logloss: 0.420516	val's f1: 0.837004
[343]	train's binary_logloss: 0.0215047	train's f1: 1	val's binary_logloss: 0.421121	val's f1: 0.840708
[344]	train's binary_logloss: 0.0213045	train's f1: 1	val's binary_logloss: 0.421316	val's f1: 0.833333
[345]	train's binary_logloss: 0.0211157	train's f1: 1	val's bina

...

[3410]	train's binary_logloss: 2.28546e-06	train's f1: 1	val's binary_logloss: 0.832258	val's f1: 0.824561
[3411]	train's binary_logloss: 2.28509e-06	train's f1: 1	val's binary_logloss: 0.832319	val's f1: 0.824561
[3412]	train's binary_logloss: 2.2847e-06	train's f1: 1	val's binary_logloss: 0.832307	val's f1: 0.824561
[3413]	train's binary_logloss: 2.28425e-06	train's f1: 1	val's binary_logloss: 0.832376	val's f1: 0.824561
[3414]	train's binary_logloss: 2.2838e-06	train's f1: 1	val's binary_logloss: 0.832517	val's f1: 0.824561
[3415]	train's binary_logloss: 2.28336e-06	train's f1: 1	val's binary_logloss: 0.832628	val's f1: 0.824561
[3416]	train's binary_logloss: 2.28293e-06	train's f1: 1	val's binary_logloss: 0.832548	val's f1: 0.824561
[3417]	train's binary_logloss: 2.28259e-06	train's f1: 1	val's binary_logloss: 0.832483	val's f1: 0.824561
[3418]	train's binary_logloss: 2.28223e-06	train's f1: 1	val's binary_logloss: 0.832505	val's f1: 0.824561
[3419]	train's binary_logloss: 2.28186e

[3498]	train's binary_logloss: 2.24967e-06	train's f1: 1	val's binary_logloss: 0.834648	val's f1: 0.824561
[3499]	train's binary_logloss: 2.24911e-06	train's f1: 1	val's binary_logloss: 0.8347	val's f1: 0.824561
[3500]	train's binary_logloss: 2.24876e-06	train's f1: 1	val's binary_logloss: 0.834718	val's f1: 0.824561
[3501]	train's binary_logloss: 2.24837e-06	train's f1: 1	val's binary_logloss: 0.83477	val's f1: 0.824561
[3502]	train's binary_logloss: 2.24796e-06	train's f1: 1	val's binary_logloss: 0.834812	val's f1: 0.824561
[3503]	train's binary_logloss: 2.2475e-06	train's f1: 1	val's binary_logloss: 0.834772	val's f1: 0.824561
[3504]	train's binary_logloss: 2.24713e-06	train's f1: 1	val's binary_logloss: 0.834741	val's f1: 0.824561
[3505]	train's binary_logloss: 2.24677e-06	train's f1: 1	val's binary_logloss: 0.834549	val's f1: 0.824561
[3506]	train's binary_logloss: 2.24637e-06	train's f1: 1	val's binary_logloss: 0.834656	val's f1: 0.824561
[3507]	train's binary_logloss: 2.24592e-0

[3584]	train's binary_logloss: 2.21672e-06	train's f1: 1	val's binary_logloss: 0.836054	val's f1: 0.824561
[3585]	train's binary_logloss: 2.21639e-06	train's f1: 1	val's binary_logloss: 0.836176	val's f1: 0.824561
[3586]	train's binary_logloss: 2.21599e-06	train's f1: 1	val's binary_logloss: 0.836173	val's f1: 0.824561
[3587]	train's binary_logloss: 2.21556e-06	train's f1: 1	val's binary_logloss: 0.836176	val's f1: 0.824561
[3588]	train's binary_logloss: 2.21517e-06	train's f1: 1	val's binary_logloss: 0.836233	val's f1: 0.824561
[3589]	train's binary_logloss: 2.21477e-06	train's f1: 1	val's binary_logloss: 0.836381	val's f1: 0.824561
[3590]	train's binary_logloss: 2.21444e-06	train's f1: 1	val's binary_logloss: 0.836378	val's f1: 0.824561
[3591]	train's binary_logloss: 2.2141e-06	train's f1: 1	val's binary_logloss: 0.836526	val's f1: 0.824561
[3592]	train's binary_logloss: 2.21381e-06	train's f1: 1	val's binary_logloss: 0.836597	val's f1: 0.824561
[3593]	train's binary_logloss: 2.21349

[3672]	train's binary_logloss: 2.18432e-06	train's f1: 1	val's binary_logloss: 0.838037	val's f1: 0.824561
[3673]	train's binary_logloss: 2.18399e-06	train's f1: 1	val's binary_logloss: 0.838005	val's f1: 0.824561
[3674]	train's binary_logloss: 2.18359e-06	train's f1: 1	val's binary_logloss: 0.838121	val's f1: 0.824561
[3675]	train's binary_logloss: 2.18317e-06	train's f1: 1	val's binary_logloss: 0.838136	val's f1: 0.824561
[3676]	train's binary_logloss: 2.18284e-06	train's f1: 1	val's binary_logloss: 0.838173	val's f1: 0.824561
[3677]	train's binary_logloss: 2.1825e-06	train's f1: 1	val's binary_logloss: 0.838195	val's f1: 0.824561
[3678]	train's binary_logloss: 2.18215e-06	train's f1: 1	val's binary_logloss: 0.838184	val's f1: 0.824561
[3679]	train's binary_logloss: 2.18174e-06	train's f1: 1	val's binary_logloss: 0.838257	val's f1: 0.824561
[3680]	train's binary_logloss: 2.18132e-06	train's f1: 1	val's binary_logloss: 0.838327	val's f1: 0.824561
[3681]	train's binary_logloss: 2.18093

[3760]	train's binary_logloss: 2.15152e-06	train's f1: 1	val's binary_logloss: 0.839693	val's f1: 0.828194
[3761]	train's binary_logloss: 2.15117e-06	train's f1: 1	val's binary_logloss: 0.839696	val's f1: 0.828194
[3762]	train's binary_logloss: 2.15079e-06	train's f1: 1	val's binary_logloss: 0.839709	val's f1: 0.828194
[3763]	train's binary_logloss: 2.15044e-06	train's f1: 1	val's binary_logloss: 0.839788	val's f1: 0.828194
[3764]	train's binary_logloss: 2.15001e-06	train's f1: 1	val's binary_logloss: 0.839841	val's f1: 0.828194
[3765]	train's binary_logloss: 2.14967e-06	train's f1: 1	val's binary_logloss: 0.839943	val's f1: 0.828194
[3766]	train's binary_logloss: 2.14926e-06	train's f1: 1	val's binary_logloss: 0.839799	val's f1: 0.828194
[3767]	train's binary_logloss: 2.149e-06	train's f1: 1	val's binary_logloss: 0.839868	val's f1: 0.828194
[3768]	train's binary_logloss: 2.14869e-06	train's f1: 1	val's binary_logloss: 0.83989	val's f1: 0.828194
[3769]	train's binary_logloss: 2.14835e-

In [219]:
imr90_lgb_pred_merged = imr90_lgb_merged.predict(imr90_merged_test_x,num_iteration=imr90_lgb_merged.best_iteration)
f1_score(imr90_merged_test_y,prob2label(imr90_lgb_pred_merged))

0.8459958932238193

### GM1878

In [232]:
gm12878_merged_train_x = gm12878_original_data_json['X_train_all']
gm12878_merged_train_y = gm12878_original_data_json['y_train_all']
gm12878_merged_test_x = gm12878_original_data_json['X_test_all']
gm12878_merged_test_y = gm12878_original_data_json['y_test_all']

gm12878_merged_train_x = gm12878_merged_train_x[gm12878_use_features]
gm12878_merged_test_x = gm12878_merged_test_x[gm12878_use_features]

gm12878_merged_train_lgb,gm12878_merged_valid_lgb,_ = generate_lgb_use_data(gm12878_merged_train_x,
                                                               gm12878_merged_train_y,
                                                               gm12878_merged_test_x,
                                                               gm12878_merged_test_y)

In [233]:
gm12878_lgb_merged = train_lgb(gm12878_merged_train_lgb,gm12878_merged_valid_lgb,
                         lgb_param,num_round+800,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.683514	train's f1: 0.148515	val's binary_logloss: 0.688463	val's f1: 0.113402
[2]	train's binary_logloss: 0.674594	train's f1: 0.673379	val's binary_logloss: 0.682561	val's f1: 0.583051
[3]	train's binary_logloss: 0.666012	train's f1: 0.732122	val's binary_logloss: 0.677284	val's f1: 0.612795
[4]	train's binary_logloss: 0.657616	train's f1: 0.75056	val's binary_logloss: 0.670458	val's f1: 0.634615
[5]	train's binary_logloss: 0.649617	train's f1: 0.766655	val's binary_logloss: 0.665849	val's f1: 0.660436
[6]	train's binary_logloss: 0.641834	train's f1: 0.780772	val's binary_logloss: 0.660194	val's f1: 0.660436
[7]	train's binary_logloss: 0.634436	train's f1: 0.780594	val's binary_logloss: 0.655591	val's f1: 0.67284
[8]	train's binary_logloss: 0.627169	train's f1: 0.79298	val's binary_logloss: 0.650463	val's f1: 0.680982
[9]	train's binary_logloss: 0.620368	train's f1: 0.796309	val's binary_logloss: 0.646481	val's f1: 0.700599
[10]	train's binary_logloss: 0.

[80]	train's binary_logloss: 0.334195	train's f1: 0.957282	val's binary_logloss: 0.482786	val's f1: 0.815864
[81]	train's binary_logloss: 0.331635	train's f1: 0.958277	val's binary_logloss: 0.481512	val's f1: 0.810198
[82]	train's binary_logloss: 0.329218	train's f1: 0.959623	val's binary_logloss: 0.480047	val's f1: 0.813559
[83]	train's binary_logloss: 0.326829	train's f1: 0.959569	val's binary_logloss: 0.479556	val's f1: 0.813559
[84]	train's binary_logloss: 0.324688	train's f1: 0.960969	val's binary_logloss: 0.479007	val's f1: 0.816901
[85]	train's binary_logloss: 0.322294	train's f1: 0.960969	val's binary_logloss: 0.478232	val's f1: 0.815864
[86]	train's binary_logloss: 0.320078	train's f1: 0.961266	val's binary_logloss: 0.477206	val's f1: 0.815864
[87]	train's binary_logloss: 0.317658	train's f1: 0.96229	val's binary_logloss: 0.475483	val's f1: 0.813559
[88]	train's binary_logloss: 0.315236	train's f1: 0.96431	val's binary_logloss: 0.474964	val's f1: 0.813559
[89]	train's binary_l

[160]	train's binary_logloss: 0.197232	train's f1: 0.994631	val's binary_logloss: 0.429672	val's f1: 0.837989
[161]	train's binary_logloss: 0.196067	train's f1: 0.994631	val's binary_logloss: 0.429002	val's f1: 0.837989
[162]	train's binary_logloss: 0.19495	train's f1: 0.994631	val's binary_logloss: 0.428735	val's f1: 0.837989
[163]	train's binary_logloss: 0.193661	train's f1: 0.994631	val's binary_logloss: 0.427422	val's f1: 0.831461
[164]	train's binary_logloss: 0.19246	train's f1: 0.994965	val's binary_logloss: 0.426406	val's f1: 0.834734
[165]	train's binary_logloss: 0.19133	train's f1: 0.994965	val's binary_logloss: 0.426259	val's f1: 0.834734
[166]	train's binary_logloss: 0.190261	train's f1: 0.995299	val's binary_logloss: 0.426053	val's f1: 0.834734
[167]	train's binary_logloss: 0.189084	train's f1: 0.995299	val's binary_logloss: 0.425636	val's f1: 0.834734
[168]	train's binary_logloss: 0.187835	train's f1: 0.99597	val's binary_logloss: 0.425163	val's f1: 0.834734
[169]	train's 

[239]	train's binary_logloss: 0.12434	train's f1: 1	val's binary_logloss: 0.396055	val's f1: 0.826816
[240]	train's binary_logloss: 0.123689	train's f1: 1	val's binary_logloss: 0.395557	val's f1: 0.824513
[241]	train's binary_logloss: 0.122958	train's f1: 1	val's binary_logloss: 0.395058	val's f1: 0.824513
[242]	train's binary_logloss: 0.122222	train's f1: 1	val's binary_logloss: 0.394468	val's f1: 0.831461
[243]	train's binary_logloss: 0.121506	train's f1: 1	val's binary_logloss: 0.393937	val's f1: 0.829132
[244]	train's binary_logloss: 0.120848	train's f1: 1	val's binary_logloss: 0.393685	val's f1: 0.829132
[245]	train's binary_logloss: 0.12018	train's f1: 1	val's binary_logloss: 0.393606	val's f1: 0.832402
[246]	train's binary_logloss: 0.119513	train's f1: 1	val's binary_logloss: 0.393032	val's f1: 0.839437
[247]	train's binary_logloss: 0.118781	train's f1: 1	val's binary_logloss: 0.392666	val's f1: 0.836158
[248]	train's binary_logloss: 0.118029	train's f1: 1	val's binary_logloss: 

[334]	train's binary_logloss: 0.0740132	train's f1: 1	val's binary_logloss: 0.369628	val's f1: 0.840336
[335]	train's binary_logloss: 0.0736366	train's f1: 1	val's binary_logloss: 0.369764	val's f1: 0.840336
[336]	train's binary_logloss: 0.0732271	train's f1: 1	val's binary_logloss: 0.369437	val's f1: 0.840336
[337]	train's binary_logloss: 0.072857	train's f1: 1	val's binary_logloss: 0.36891	val's f1: 0.840336
[338]	train's binary_logloss: 0.0724708	train's f1: 1	val's binary_logloss: 0.368706	val's f1: 0.840336
[339]	train's binary_logloss: 0.0721116	train's f1: 1	val's binary_logloss: 0.368639	val's f1: 0.842697
[340]	train's binary_logloss: 0.0717356	train's f1: 1	val's binary_logloss: 0.368753	val's f1: 0.842697
[341]	train's binary_logloss: 0.0713559	train's f1: 1	val's binary_logloss: 0.368802	val's f1: 0.842697
[342]	train's binary_logloss: 0.0709166	train's f1: 1	val's binary_logloss: 0.368327	val's f1: 0.842697
[343]	train's binary_logloss: 0.0704932	train's f1: 1	val's binary

...

[3333]	train's binary_logloss: 2.37018e-06	train's f1: 1	val's binary_logloss: 0.527584	val's f1: 0.858726
[3334]	train's binary_logloss: 2.36899e-06	train's f1: 1	val's binary_logloss: 0.527567	val's f1: 0.858726
[3335]	train's binary_logloss: 2.36823e-06	train's f1: 1	val's binary_logloss: 0.527539	val's f1: 0.858726
[3336]	train's binary_logloss: 2.36703e-06	train's f1: 1	val's binary_logloss: 0.527491	val's f1: 0.858726
[3337]	train's binary_logloss: 2.36605e-06	train's f1: 1	val's binary_logloss: 0.527468	val's f1: 0.858726
[3338]	train's binary_logloss: 2.36478e-06	train's f1: 1	val's binary_logloss: 0.527411	val's f1: 0.858726
[3339]	train's binary_logloss: 2.36398e-06	train's f1: 1	val's binary_logloss: 0.527415	val's f1: 0.858726
[3340]	train's binary_logloss: 2.36291e-06	train's f1: 1	val's binary_logloss: 0.527414	val's f1: 0.858726
[3341]	train's binary_logloss: 2.36205e-06	train's f1: 1	val's binary_logloss: 0.527407	val's f1: 0.858726
[3342]	train's binary_logloss: 2.3612

[3442]	train's binary_logloss: 2.26842e-06	train's f1: 1	val's binary_logloss: 0.5301	val's f1: 0.858726
[3443]	train's binary_logloss: 2.26764e-06	train's f1: 1	val's binary_logloss: 0.530117	val's f1: 0.858726
[3444]	train's binary_logloss: 2.26692e-06	train's f1: 1	val's binary_logloss: 0.529999	val's f1: 0.858726
[3445]	train's binary_logloss: 2.2661e-06	train's f1: 1	val's binary_logloss: 0.52995	val's f1: 0.858726
[3446]	train's binary_logloss: 2.26534e-06	train's f1: 1	val's binary_logloss: 0.530133	val's f1: 0.858726
[3447]	train's binary_logloss: 2.26436e-06	train's f1: 1	val's binary_logloss: 0.530151	val's f1: 0.858726
[3448]	train's binary_logloss: 2.26345e-06	train's f1: 1	val's binary_logloss: 0.530255	val's f1: 0.858726
[3449]	train's binary_logloss: 2.26247e-06	train's f1: 1	val's binary_logloss: 0.530335	val's f1: 0.858726
[3450]	train's binary_logloss: 2.26171e-06	train's f1: 1	val's binary_logloss: 0.53038	val's f1: 0.858726
[3451]	train's binary_logloss: 2.26078e-06

[3553]	train's binary_logloss: 2.17853e-06	train's f1: 1	val's binary_logloss: 0.532323	val's f1: 0.858726
[3554]	train's binary_logloss: 2.17775e-06	train's f1: 1	val's binary_logloss: 0.532219	val's f1: 0.858726
[3555]	train's binary_logloss: 2.1769e-06	train's f1: 1	val's binary_logloss: 0.532236	val's f1: 0.858726
[3556]	train's binary_logloss: 2.17596e-06	train's f1: 1	val's binary_logloss: 0.532214	val's f1: 0.858726
[3557]	train's binary_logloss: 2.17516e-06	train's f1: 1	val's binary_logloss: 0.532156	val's f1: 0.858726
[3558]	train's binary_logloss: 2.17419e-06	train's f1: 1	val's binary_logloss: 0.53214	val's f1: 0.858726
[3559]	train's binary_logloss: 2.1734e-06	train's f1: 1	val's binary_logloss: 0.532256	val's f1: 0.858726
[3560]	train's binary_logloss: 2.17252e-06	train's f1: 1	val's binary_logloss: 0.532163	val's f1: 0.858726
[3561]	train's binary_logloss: 2.1718e-06	train's f1: 1	val's binary_logloss: 0.532217	val's f1: 0.858726
[3562]	train's binary_logloss: 2.17113e-0

[3662]	train's binary_logloss: 2.09727e-06	train's f1: 1	val's binary_logloss: 0.533563	val's f1: 0.861878
[3663]	train's binary_logloss: 2.09662e-06	train's f1: 1	val's binary_logloss: 0.533578	val's f1: 0.861878
[3664]	train's binary_logloss: 2.0961e-06	train's f1: 1	val's binary_logloss: 0.533581	val's f1: 0.861878
[3665]	train's binary_logloss: 2.09566e-06	train's f1: 1	val's binary_logloss: 0.533635	val's f1: 0.861878
[3666]	train's binary_logloss: 2.09486e-06	train's f1: 1	val's binary_logloss: 0.533499	val's f1: 0.861878
[3667]	train's binary_logloss: 2.09425e-06	train's f1: 1	val's binary_logloss: 0.533606	val's f1: 0.861878
[3668]	train's binary_logloss: 2.09362e-06	train's f1: 1	val's binary_logloss: 0.533578	val's f1: 0.861878
[3669]	train's binary_logloss: 2.09302e-06	train's f1: 1	val's binary_logloss: 0.533598	val's f1: 0.861878
[3670]	train's binary_logloss: 2.09215e-06	train's f1: 1	val's binary_logloss: 0.533567	val's f1: 0.861878
[3671]	train's binary_logloss: 2.09147

[3772]	train's binary_logloss: 2.02786e-06	train's f1: 1	val's binary_logloss: 0.535349	val's f1: 0.861878
[3773]	train's binary_logloss: 2.02724e-06	train's f1: 1	val's binary_logloss: 0.535339	val's f1: 0.861878
[3774]	train's binary_logloss: 2.02648e-06	train's f1: 1	val's binary_logloss: 0.535445	val's f1: 0.861878
[3775]	train's binary_logloss: 2.02604e-06	train's f1: 1	val's binary_logloss: 0.53546	val's f1: 0.861878
[3776]	train's binary_logloss: 2.02546e-06	train's f1: 1	val's binary_logloss: 0.535584	val's f1: 0.861878
[3777]	train's binary_logloss: 2.02495e-06	train's f1: 1	val's binary_logloss: 0.535557	val's f1: 0.861878
[3778]	train's binary_logloss: 2.02422e-06	train's f1: 1	val's binary_logloss: 0.535503	val's f1: 0.861878
[3779]	train's binary_logloss: 2.02351e-06	train's f1: 1	val's binary_logloss: 0.535531	val's f1: 0.861878
[3780]	train's binary_logloss: 2.02266e-06	train's f1: 1	val's binary_logloss: 0.535625	val's f1: 0.861878
[3781]	train's binary_logloss: 2.02214

In [234]:
gm12878_lgb_pred_merged = gm12878_lgb_merged.predict(gm12878_merged_test_x,num_iteration=gm12878_lgb_merged.best_iteration)
f1_score(gm12878_merged_test_y,prob2label(gm12878_lgb_pred_merged))

0.8539576365663322

### Hela-S3

In [237]:
helas3_merged_train_x = helas3_original_data_json['X_train_all']
helas3_merged_train_y = helas3_original_data_json['y_train_all']
helas3_merged_test_x = helas3_original_data_json['X_test_all']
helas3_merged_test_y = helas3_original_data_json['y_test_all']

helas3_merged_train_x = helas3_merged_train_x[helas3_use_features]
helas3_merged_test_x = helas3_merged_test_x[helas3_use_features]

helas3_merged_train_lgb,helas3_merged_valid_lgb,_ = generate_lgb_use_data(helas3_merged_train_x,
                                                               helas3_merged_train_y,
                                                               helas3_merged_test_x,
                                                               helas3_merged_test_y)

In [238]:
helas3_lgb_merged = train_lgb(helas3_merged_train_lgb,helas3_merged_valid_lgb,
                         lgb_param,num_round+700,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.679881	train's f1: 0.809208	val's binary_logloss: 0.684755	val's f1: 0.707395
[2]	train's binary_logloss: 0.667331	train's f1: 0.841864	val's binary_logloss: 0.676679	val's f1: 0.707071
[3]	train's binary_logloss: 0.655556	train's f1: 0.824233	val's binary_logloss: 0.668795	val's f1: 0.717949
[4]	train's binary_logloss: 0.64352	train's f1: 0.855361	val's binary_logloss: 0.659982	val's f1: 0.741259
[5]	train's binary_logloss: 0.632013	train's f1: 0.864044	val's binary_logloss: 0.652566	val's f1: 0.765957
[6]	train's binary_logloss: 0.619937	train's f1: 0.880999	val's binary_logloss: 0.645275	val's f1: 0.752688
[7]	train's binary_logloss: 0.609177	train's f1: 0.88332	val's binary_logloss: 0.637719	val's f1: 0.76259
[8]	train's binary_logloss: 0.598072	train's f1: 0.8935	val's binary_logloss: 0.631364	val's f1: 0.778571
[9]	train's binary_logloss: 0.588207	train's f1: 0.894902	val's binary_logloss: 0.624974	val's f1: 0.781362
[10]	train's binary_logloss: 0.57

[85]	train's binary_logloss: 0.232099	train's f1: 0.981147	val's binary_logloss: 0.409278	val's f1: 0.857143
[86]	train's binary_logloss: 0.229766	train's f1: 0.981932	val's binary_logloss: 0.407483	val's f1: 0.861314
[87]	train's binary_logloss: 0.227734	train's f1: 0.982718	val's binary_logloss: 0.406398	val's f1: 0.861314
[88]	train's binary_logloss: 0.225594	train's f1: 0.982718	val's binary_logloss: 0.404796	val's f1: 0.869565
[89]	train's binary_logloss: 0.22337	train's f1: 0.983117	val's binary_logloss: 0.403236	val's f1: 0.865455
[90]	train's binary_logloss: 0.221086	train's f1: 0.983504	val's binary_logloss: 0.400855	val's f1: 0.869565
[91]	train's binary_logloss: 0.218905	train's f1: 0.98389	val's binary_logloss: 0.399851	val's f1: 0.869565
[92]	train's binary_logloss: 0.216743	train's f1: 0.984676	val's binary_logloss: 0.397983	val's f1: 0.869565
[93]	train's binary_logloss: 0.214725	train's f1: 0.984664	val's binary_logloss: 0.395932	val's f1: 0.872727
[94]	train's binary_l

[168]	train's binary_logloss: 0.109749	train's f1: 0.99921	val's binary_logloss: 0.341863	val's f1: 0.872727
[169]	train's binary_logloss: 0.108812	train's f1: 0.99921	val's binary_logloss: 0.34119	val's f1: 0.876812
[170]	train's binary_logloss: 0.107982	train's f1: 0.99921	val's binary_logloss: 0.340959	val's f1: 0.876812
[171]	train's binary_logloss: 0.107064	train's f1: 0.99921	val's binary_logloss: 0.340459	val's f1: 0.88
[172]	train's binary_logloss: 0.106178	train's f1: 0.99921	val's binary_logloss: 0.340042	val's f1: 0.876812
[173]	train's binary_logloss: 0.105256	train's f1: 0.99921	val's binary_logloss: 0.339813	val's f1: 0.883212
[174]	train's binary_logloss: 0.10427	train's f1: 0.99921	val's binary_logloss: 0.33896	val's f1: 0.883212
[175]	train's binary_logloss: 0.103376	train's f1: 0.99921	val's binary_logloss: 0.337794	val's f1: 0.883212
[176]	train's binary_logloss: 0.102596	train's f1: 0.99921	val's binary_logloss: 0.337489	val's f1: 0.883212
[177]	train's binary_loglo

[253]	train's binary_logloss: 0.0543276	train's f1: 1	val's binary_logloss: 0.308059	val's f1: 0.889706
[254]	train's binary_logloss: 0.0539222	train's f1: 1	val's binary_logloss: 0.308097	val's f1: 0.889706
[255]	train's binary_logloss: 0.0534512	train's f1: 1	val's binary_logloss: 0.308154	val's f1: 0.889706
[256]	train's binary_logloss: 0.0530366	train's f1: 1	val's binary_logloss: 0.307993	val's f1: 0.893773
[257]	train's binary_logloss: 0.0526159	train's f1: 1	val's binary_logloss: 0.307861	val's f1: 0.893773
[258]	train's binary_logloss: 0.0521526	train's f1: 1	val's binary_logloss: 0.307834	val's f1: 0.893773
[259]	train's binary_logloss: 0.0517434	train's f1: 1	val's binary_logloss: 0.307788	val's f1: 0.89781
[260]	train's binary_logloss: 0.0513268	train's f1: 1	val's binary_logloss: 0.307763	val's f1: 0.89781
[261]	train's binary_logloss: 0.0509327	train's f1: 1	val's binary_logloss: 0.307224	val's f1: 0.893773
[262]	train's binary_logloss: 0.0505657	train's f1: 1	val's binary

[336]	train's binary_logloss: 0.028325	train's f1: 1	val's binary_logloss: 0.293852	val's f1: 0.904412
[337]	train's binary_logloss: 0.0280934	train's f1: 1	val's binary_logloss: 0.293904	val's f1: 0.901099
[338]	train's binary_logloss: 0.0278658	train's f1: 1	val's binary_logloss: 0.293516	val's f1: 0.901099
[339]	train's binary_logloss: 0.0276348	train's f1: 1	val's binary_logloss: 0.293496	val's f1: 0.901099
[340]	train's binary_logloss: 0.027421	train's f1: 1	val's binary_logloss: 0.293008	val's f1: 0.901099
[341]	train's binary_logloss: 0.0272167	train's f1: 1	val's binary_logloss: 0.29298	val's f1: 0.901099
[342]	train's binary_logloss: 0.0270135	train's f1: 1	val's binary_logloss: 0.293205	val's f1: 0.897059
[343]	train's binary_logloss: 0.026783	train's f1: 1	val's binary_logloss: 0.293137	val's f1: 0.897059
[344]	train's binary_logloss: 0.0265612	train's f1: 1	val's binary_logloss: 0.293121	val's f1: 0.901099
[345]	train's binary_logloss: 0.0263726	train's f1: 1	val's binary_l

...

[3322]	train's binary_logloss: 1.90049e-06	train's f1: 1	val's binary_logloss: 0.475355	val's f1: 0.901818
[3323]	train's binary_logloss: 1.9e-06	train's f1: 1	val's binary_logloss: 0.47532	val's f1: 0.901818
[3324]	train's binary_logloss: 1.89943e-06	train's f1: 1	val's binary_logloss: 0.475351	val's f1: 0.901818
[3325]	train's binary_logloss: 1.89887e-06	train's f1: 1	val's binary_logloss: 0.475422	val's f1: 0.901818
[3326]	train's binary_logloss: 1.89832e-06	train's f1: 1	val's binary_logloss: 0.475466	val's f1: 0.901818
[3327]	train's binary_logloss: 1.89799e-06	train's f1: 1	val's binary_logloss: 0.475505	val's f1: 0.901818
[3328]	train's binary_logloss: 1.89769e-06	train's f1: 1	val's binary_logloss: 0.475518	val's f1: 0.901818
[3329]	train's binary_logloss: 1.89712e-06	train's f1: 1	val's binary_logloss: 0.475467	val's f1: 0.901818
[3330]	train's binary_logloss: 1.89677e-06	train's f1: 1	val's binary_logloss: 0.475541	val's f1: 0.901818
[3331]	train's binary_logloss: 1.89606e-06

[3431]	train's binary_logloss: 1.84955e-06	train's f1: 1	val's binary_logloss: 0.476619	val's f1: 0.901818
[3432]	train's binary_logloss: 1.84926e-06	train's f1: 1	val's binary_logloss: 0.476569	val's f1: 0.901818
[3433]	train's binary_logloss: 1.84869e-06	train's f1: 1	val's binary_logloss: 0.476628	val's f1: 0.901818
[3434]	train's binary_logloss: 1.84833e-06	train's f1: 1	val's binary_logloss: 0.476653	val's f1: 0.901818
[3435]	train's binary_logloss: 1.84781e-06	train's f1: 1	val's binary_logloss: 0.476637	val's f1: 0.901818
[3436]	train's binary_logloss: 1.84754e-06	train's f1: 1	val's binary_logloss: 0.476678	val's f1: 0.901818
[3437]	train's binary_logloss: 1.84709e-06	train's f1: 1	val's binary_logloss: 0.476698	val's f1: 0.901818
[3438]	train's binary_logloss: 1.84684e-06	train's f1: 1	val's binary_logloss: 0.47672	val's f1: 0.901818
[3439]	train's binary_logloss: 1.84652e-06	train's f1: 1	val's binary_logloss: 0.476713	val's f1: 0.901818
[3440]	train's binary_logloss: 1.84605

[3514]	train's binary_logloss: 1.81457e-06	train's f1: 1	val's binary_logloss: 0.477459	val's f1: 0.901818
[3515]	train's binary_logloss: 1.81403e-06	train's f1: 1	val's binary_logloss: 0.477489	val's f1: 0.901818
[3516]	train's binary_logloss: 1.81376e-06	train's f1: 1	val's binary_logloss: 0.477498	val's f1: 0.901818
[3517]	train's binary_logloss: 1.81348e-06	train's f1: 1	val's binary_logloss: 0.477479	val's f1: 0.901818
[3518]	train's binary_logloss: 1.81323e-06	train's f1: 1	val's binary_logloss: 0.477505	val's f1: 0.901818
[3519]	train's binary_logloss: 1.81271e-06	train's f1: 1	val's binary_logloss: 0.477485	val's f1: 0.901818
[3520]	train's binary_logloss: 1.81214e-06	train's f1: 1	val's binary_logloss: 0.47754	val's f1: 0.901818
[3521]	train's binary_logloss: 1.81165e-06	train's f1: 1	val's binary_logloss: 0.477497	val's f1: 0.901818
[3522]	train's binary_logloss: 1.8111e-06	train's f1: 1	val's binary_logloss: 0.477566	val's f1: 0.901818
[3523]	train's binary_logloss: 1.81061e

[3594]	train's binary_logloss: 1.78164e-06	train's f1: 1	val's binary_logloss: 0.478339	val's f1: 0.901818
[3595]	train's binary_logloss: 1.7812e-06	train's f1: 1	val's binary_logloss: 0.478266	val's f1: 0.901818
[3596]	train's binary_logloss: 1.78075e-06	train's f1: 1	val's binary_logloss: 0.478275	val's f1: 0.901818
[3597]	train's binary_logloss: 1.78042e-06	train's f1: 1	val's binary_logloss: 0.478298	val's f1: 0.901818
[3598]	train's binary_logloss: 1.77998e-06	train's f1: 1	val's binary_logloss: 0.478271	val's f1: 0.901818
[3599]	train's binary_logloss: 1.77975e-06	train's f1: 1	val's binary_logloss: 0.478336	val's f1: 0.901818
[3600]	train's binary_logloss: 1.77926e-06	train's f1: 1	val's binary_logloss: 0.478263	val's f1: 0.901818
[3601]	train's binary_logloss: 1.77901e-06	train's f1: 1	val's binary_logloss: 0.478212	val's f1: 0.901818
[3602]	train's binary_logloss: 1.77877e-06	train's f1: 1	val's binary_logloss: 0.478254	val's f1: 0.901818
[3603]	train's binary_logloss: 1.77838

[3675]	train's binary_logloss: 1.75185e-06	train's f1: 1	val's binary_logloss: 0.478753	val's f1: 0.901818
[3676]	train's binary_logloss: 1.75136e-06	train's f1: 1	val's binary_logloss: 0.478784	val's f1: 0.901818
[3677]	train's binary_logloss: 1.75108e-06	train's f1: 1	val's binary_logloss: 0.478828	val's f1: 0.901818
[3678]	train's binary_logloss: 1.75074e-06	train's f1: 1	val's binary_logloss: 0.478854	val's f1: 0.901818
[3679]	train's binary_logloss: 1.75051e-06	train's f1: 1	val's binary_logloss: 0.478958	val's f1: 0.901818
[3680]	train's binary_logloss: 1.75e-06	train's f1: 1	val's binary_logloss: 0.478928	val's f1: 0.901818
[3681]	train's binary_logloss: 1.74977e-06	train's f1: 1	val's binary_logloss: 0.47895	val's f1: 0.901818
[3682]	train's binary_logloss: 1.74947e-06	train's f1: 1	val's binary_logloss: 0.478859	val's f1: 0.901818
[3683]	train's binary_logloss: 1.74919e-06	train's f1: 1	val's binary_logloss: 0.478936	val's f1: 0.901818
[3684]	train's binary_logloss: 1.74868e-0

In [239]:
helas3_lgb_pred_merged = helas3_lgb_merged.predict(helas3_merged_test_x,num_iteration=helas3_lgb_merged.best_iteration)
f1_score(helas3_merged_test_y,prob2label(helas3_lgb_pred_merged))

0.8962536023054756

### HUVEC

In [242]:
huvec_merged_train_x = huvec_original_data_json['X_train_all']
huvec_merged_train_y = huvec_original_data_json['y_train_all']
huvec_merged_test_x = huvec_original_data_json['X_test_all']
huvec_merged_test_y = huvec_original_data_json['y_test_all']

huvec_merged_train_x = huvec_merged_train_x[huvec_use_features]
huvec_merged_test_x = huvec_merged_test_x[huvec_use_features]

huvec_merged_train_lgb,huvec_merged_valid_lgb,_ = generate_lgb_use_data(huvec_merged_train_x,
                                                               huvec_merged_train_y,
                                                               huvec_merged_test_x,
                                                               huvec_merged_test_y)

In [243]:
huvec_lgb_merged = train_lgb(huvec_merged_train_lgb,huvec_merged_valid_lgb,
                         lgb_param,num_round+1000,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.679137	train's f1: 0.83531	val's binary_logloss: 0.683714	val's f1: 0.742424
[2]	train's binary_logloss: 0.665802	train's f1: 0.841745	val's binary_logloss: 0.674596	val's f1: 0.760148
[3]	train's binary_logloss: 0.653212	train's f1: 0.852604	val's binary_logloss: 0.666845	val's f1: 0.723077
[4]	train's binary_logloss: 0.640883	train's f1: 0.857397	val's binary_logloss: 0.658591	val's f1: 0.727969
[5]	train's binary_logloss: 0.629475	train's f1: 0.860904	val's binary_logloss: 0.651472	val's f1: 0.75188
[6]	train's binary_logloss: 0.618367	train's f1: 0.872424	val's binary_logloss: 0.643538	val's f1: 0.747082
[7]	train's binary_logloss: 0.607077	train's f1: 0.884294	val's binary_logloss: 0.635822	val's f1: 0.762646
[8]	train's binary_logloss: 0.596744	train's f1: 0.888791	val's binary_logloss: 0.629549	val's f1: 0.752941
[9]	train's binary_logloss: 0.586379	train's f1: 0.889476	val's binary_logloss: 0.622548	val's f1: 0.75969
[10]	train's binary_logloss: 0.

[89]	train's binary_logloss: 0.217615	train's f1: 0.987353	val's binary_logloss: 0.41604	val's f1: 0.839216
[90]	train's binary_logloss: 0.215427	train's f1: 0.988246	val's binary_logloss: 0.415259	val's f1: 0.826772
[91]	train's binary_logloss: 0.213276	train's f1: 0.988693	val's binary_logloss: 0.414145	val's f1: 0.835938
[92]	train's binary_logloss: 0.211038	train's f1: 0.98915	val's binary_logloss: 0.413205	val's f1: 0.839216
[93]	train's binary_logloss: 0.208972	train's f1: 0.990063	val's binary_logloss: 0.412705	val's f1: 0.839216
[94]	train's binary_logloss: 0.206873	train's f1: 0.989616	val's binary_logloss: 0.412091	val's f1: 0.839216
[95]	train's binary_logloss: 0.204785	train's f1: 0.990967	val's binary_logloss: 0.411245	val's f1: 0.839216
[96]	train's binary_logloss: 0.2028	train's f1: 0.991414	val's binary_logloss: 0.410935	val's f1: 0.839216
[97]	train's binary_logloss: 0.200697	train's f1: 0.991414	val's binary_logloss: 0.410118	val's f1: 0.839216
[98]	train's binary_log

[176]	train's binary_logloss: 0.0959026	train's f1: 1	val's binary_logloss: 0.364506	val's f1: 0.849421
[177]	train's binary_logloss: 0.095104	train's f1: 1	val's binary_logloss: 0.36428	val's f1: 0.853846
[178]	train's binary_logloss: 0.0942821	train's f1: 1	val's binary_logloss: 0.363642	val's f1: 0.850575
[179]	train's binary_logloss: 0.0934631	train's f1: 1	val's binary_logloss: 0.362576	val's f1: 0.846154
[180]	train's binary_logloss: 0.0926567	train's f1: 1	val's binary_logloss: 0.361771	val's f1: 0.850575
[181]	train's binary_logloss: 0.0918646	train's f1: 1	val's binary_logloss: 0.361604	val's f1: 0.850575
[182]	train's binary_logloss: 0.0910493	train's f1: 1	val's binary_logloss: 0.36073	val's f1: 0.850575
[183]	train's binary_logloss: 0.0902122	train's f1: 1	val's binary_logloss: 0.360404	val's f1: 0.853846
[184]	train's binary_logloss: 0.0893698	train's f1: 1	val's binary_logloss: 0.359928	val's f1: 0.853846
[185]	train's binary_logloss: 0.0886183	train's f1: 1	val's binary_

[266]	train's binary_logloss: 0.0443814	train's f1: 1	val's binary_logloss: 0.345517	val's f1: 0.850575
[267]	train's binary_logloss: 0.0440202	train's f1: 1	val's binary_logloss: 0.345712	val's f1: 0.850575
[268]	train's binary_logloss: 0.0436133	train's f1: 1	val's binary_logloss: 0.345403	val's f1: 0.850575
[269]	train's binary_logloss: 0.0432503	train's f1: 1	val's binary_logloss: 0.345995	val's f1: 0.850575
[270]	train's binary_logloss: 0.0428696	train's f1: 1	val's binary_logloss: 0.345963	val's f1: 0.850575
[271]	train's binary_logloss: 0.0424962	train's f1: 1	val's binary_logloss: 0.346386	val's f1: 0.850575
[272]	train's binary_logloss: 0.0421502	train's f1: 1	val's binary_logloss: 0.346098	val's f1: 0.850575
[273]	train's binary_logloss: 0.0418164	train's f1: 1	val's binary_logloss: 0.345991	val's f1: 0.850575
[274]	train's binary_logloss: 0.0414658	train's f1: 1	val's binary_logloss: 0.345636	val's f1: 0.850575
[275]	train's binary_logloss: 0.0411363	train's f1: 1	val's bina

[355]	train's binary_logloss: 0.0209359	train's f1: 1	val's binary_logloss: 0.341672	val's f1: 0.847328
[356]	train's binary_logloss: 0.0207605	train's f1: 1	val's binary_logloss: 0.342081	val's f1: 0.847328
[357]	train's binary_logloss: 0.0205971	train's f1: 1	val's binary_logloss: 0.34229	val's f1: 0.847328
[358]	train's binary_logloss: 0.0204426	train's f1: 1	val's binary_logloss: 0.34162	val's f1: 0.842912
[359]	train's binary_logloss: 0.0202751	train's f1: 1	val's binary_logloss: 0.341312	val's f1: 0.842912
[360]	train's binary_logloss: 0.0201058	train's f1: 1	val's binary_logloss: 0.341089	val's f1: 0.842912
[361]	train's binary_logloss: 0.0199467	train's f1: 1	val's binary_logloss: 0.340931	val's f1: 0.842912
[362]	train's binary_logloss: 0.0197875	train's f1: 1	val's binary_logloss: 0.34051	val's f1: 0.847328
[363]	train's binary_logloss: 0.0196056	train's f1: 1	val's binary_logloss: 0.340159	val's f1: 0.847328
[364]	train's binary_logloss: 0.0194283	train's f1: 1	val's binary_

...

[3625]	train's binary_logloss: 1.89409e-06	train's f1: 1	val's binary_logloss: 0.58696	val's f1: 0.86692
[3626]	train's binary_logloss: 1.8938e-06	train's f1: 1	val's binary_logloss: 0.586976	val's f1: 0.86692
[3627]	train's binary_logloss: 1.89349e-06	train's f1: 1	val's binary_logloss: 0.586948	val's f1: 0.86692
[3628]	train's binary_logloss: 1.89314e-06	train's f1: 1	val's binary_logloss: 0.586973	val's f1: 0.86692
[3629]	train's binary_logloss: 1.89285e-06	train's f1: 1	val's binary_logloss: 0.586995	val's f1: 0.86692
[3630]	train's binary_logloss: 1.89253e-06	train's f1: 1	val's binary_logloss: 0.586963	val's f1: 0.86692
[3631]	train's binary_logloss: 1.89224e-06	train's f1: 1	val's binary_logloss: 0.587026	val's f1: 0.86692
[3632]	train's binary_logloss: 1.89187e-06	train's f1: 1	val's binary_logloss: 0.587021	val's f1: 0.86692
[3633]	train's binary_logloss: 1.89155e-06	train's f1: 1	val's binary_logloss: 0.587039	val's f1: 0.86692
[3634]	train's binary_logloss: 1.89117e-06	train

[3704]	train's binary_logloss: 1.86799e-06	train's f1: 1	val's binary_logloss: 0.587772	val's f1: 0.86692
[3705]	train's binary_logloss: 1.86773e-06	train's f1: 1	val's binary_logloss: 0.587787	val's f1: 0.86692
[3706]	train's binary_logloss: 1.86744e-06	train's f1: 1	val's binary_logloss: 0.587776	val's f1: 0.86692
[3707]	train's binary_logloss: 1.86713e-06	train's f1: 1	val's binary_logloss: 0.587744	val's f1: 0.86692
[3708]	train's binary_logloss: 1.86679e-06	train's f1: 1	val's binary_logloss: 0.58777	val's f1: 0.870229
[3709]	train's binary_logloss: 1.86651e-06	train's f1: 1	val's binary_logloss: 0.587846	val's f1: 0.86692
[3710]	train's binary_logloss: 1.86623e-06	train's f1: 1	val's binary_logloss: 0.58778	val's f1: 0.86692
[3711]	train's binary_logloss: 1.86593e-06	train's f1: 1	val's binary_logloss: 0.587765	val's f1: 0.870229
[3712]	train's binary_logloss: 1.86559e-06	train's f1: 1	val's binary_logloss: 0.587789	val's f1: 0.86692
[3713]	train's binary_logloss: 1.86532e-06	tra

[3784]	train's binary_logloss: 1.84311e-06	train's f1: 1	val's binary_logloss: 0.588097	val's f1: 0.870229
[3785]	train's binary_logloss: 1.84277e-06	train's f1: 1	val's binary_logloss: 0.588138	val's f1: 0.870229
[3786]	train's binary_logloss: 1.84235e-06	train's f1: 1	val's binary_logloss: 0.588156	val's f1: 0.870229
[3787]	train's binary_logloss: 1.84202e-06	train's f1: 1	val's binary_logloss: 0.588119	val's f1: 0.870229
[3788]	train's binary_logloss: 1.84177e-06	train's f1: 1	val's binary_logloss: 0.588112	val's f1: 0.870229
[3789]	train's binary_logloss: 1.84148e-06	train's f1: 1	val's binary_logloss: 0.588134	val's f1: 0.870229
[3790]	train's binary_logloss: 1.8412e-06	train's f1: 1	val's binary_logloss: 0.588068	val's f1: 0.870229
[3791]	train's binary_logloss: 1.84089e-06	train's f1: 1	val's binary_logloss: 0.588146	val's f1: 0.870229
[3792]	train's binary_logloss: 1.84063e-06	train's f1: 1	val's binary_logloss: 0.588151	val's f1: 0.870229
[3793]	train's binary_logloss: 1.84032

[3864]	train's binary_logloss: 1.81903e-06	train's f1: 1	val's binary_logloss: 0.588445	val's f1: 0.870229
[3865]	train's binary_logloss: 1.81865e-06	train's f1: 1	val's binary_logloss: 0.588498	val's f1: 0.870229
[3866]	train's binary_logloss: 1.81832e-06	train's f1: 1	val's binary_logloss: 0.588492	val's f1: 0.86692
[3867]	train's binary_logloss: 1.81801e-06	train's f1: 1	val's binary_logloss: 0.588387	val's f1: 0.870229
[3868]	train's binary_logloss: 1.81766e-06	train's f1: 1	val's binary_logloss: 0.588322	val's f1: 0.86692
[3869]	train's binary_logloss: 1.81726e-06	train's f1: 1	val's binary_logloss: 0.588339	val's f1: 0.86692
[3870]	train's binary_logloss: 1.81701e-06	train's f1: 1	val's binary_logloss: 0.588361	val's f1: 0.870229
[3871]	train's binary_logloss: 1.81675e-06	train's f1: 1	val's binary_logloss: 0.588408	val's f1: 0.86692
[3872]	train's binary_logloss: 1.81643e-06	train's f1: 1	val's binary_logloss: 0.588388	val's f1: 0.870229
[3873]	train's binary_logloss: 1.81619e-0

[3944]	train's binary_logloss: 1.7954e-06	train's f1: 1	val's binary_logloss: 0.589353	val's f1: 0.86692
[3945]	train's binary_logloss: 1.79512e-06	train's f1: 1	val's binary_logloss: 0.589338	val's f1: 0.870229
[3946]	train's binary_logloss: 1.79487e-06	train's f1: 1	val's binary_logloss: 0.589449	val's f1: 0.870229
[3947]	train's binary_logloss: 1.79461e-06	train's f1: 1	val's binary_logloss: 0.589442	val's f1: 0.870229
[3948]	train's binary_logloss: 1.79433e-06	train's f1: 1	val's binary_logloss: 0.589455	val's f1: 0.870229
[3949]	train's binary_logloss: 1.79404e-06	train's f1: 1	val's binary_logloss: 0.589376	val's f1: 0.870229
[3950]	train's binary_logloss: 1.79375e-06	train's f1: 1	val's binary_logloss: 0.589468	val's f1: 0.86692
[3951]	train's binary_logloss: 1.7935e-06	train's f1: 1	val's binary_logloss: 0.589454	val's f1: 0.86692
[3952]	train's binary_logloss: 1.79324e-06	train's f1: 1	val's binary_logloss: 0.589514	val's f1: 0.86692
[3953]	train's binary_logloss: 1.79292e-06	

In [244]:
huvec_lgb_pred_merged = huvec_lgb_merged.predict(huvec_merged_test_x,num_iteration=huvec_lgb_merged.best_iteration)
f1_score(huvec_merged_test_y,prob2label(huvec_lgb_pred_merged))

0.8655737704918033

### NHEK

In [248]:
nhek_merged_train_x = nhek_original_data_json['X_train_all']
nhek_merged_train_y = nhek_original_data_json['y_train_all']
nhek_merged_test_x = nhek_original_data_json['X_test_all']
nhek_merged_test_y = nhek_original_data_json['y_test_all']

nhek_merged_train_x = nhek_merged_train_x[nhek_use_features]
nhek_merged_test_x = nhek_merged_test_x[nhek_use_features]

nhek_merged_train_lgb,nhek_merged_valid_lgb,_ = generate_lgb_use_data(nhek_merged_train_x,
                                                               nhek_merged_train_y,
                                                               nhek_merged_test_x,
                                                               nhek_merged_test_y)

In [249]:
nhek_lgb_merged = train_lgb(nhek_merged_train_lgb,nhek_merged_valid_lgb,
                         lgb_param,num_round+1000,early_stop,nfold,is_cv=False)

[1]	train's binary_logloss: 0.677654	train's f1: 0.835457	val's binary_logloss: 0.681806	val's f1: 0.777778
[2]	train's binary_logloss: 0.662868	train's f1: 0.858089	val's binary_logloss: 0.670045	val's f1: 0.796296
[3]	train's binary_logloss: 0.648591	train's f1: 0.862069	val's binary_logloss: 0.65853	val's f1: 0.80543
[4]	train's binary_logloss: 0.635287	train's f1: 0.867639	val's binary_logloss: 0.648756	val's f1: 0.807175
[5]	train's binary_logloss: 0.622208	train's f1: 0.877062	val's binary_logloss: 0.637702	val's f1: 0.817391
[6]	train's binary_logloss: 0.609518	train's f1: 0.89364	val's binary_logloss: 0.629227	val's f1: 0.831858
[7]	train's binary_logloss: 0.597285	train's f1: 0.899258	val's binary_logloss: 0.620165	val's f1: 0.842105
[8]	train's binary_logloss: 0.585408	train's f1: 0.903672	val's binary_logloss: 0.611568	val's f1: 0.843478
[9]	train's binary_logloss: 0.573343	train's f1: 0.912281	val's binary_logloss: 0.603252	val's f1: 0.865801
[10]	train's binary_logloss: 0.

[93]	train's binary_logloss: 0.165508	train's f1: 0.996177	val's binary_logloss: 0.30516	val's f1: 0.929204
[94]	train's binary_logloss: 0.163707	train's f1: 0.996177	val's binary_logloss: 0.304322	val's f1: 0.933333
[95]	train's binary_logloss: 0.161702	train's f1: 0.996177	val's binary_logloss: 0.302767	val's f1: 0.929204
[96]	train's binary_logloss: 0.159668	train's f1: 0.996177	val's binary_logloss: 0.301443	val's f1: 0.929204
[97]	train's binary_logloss: 0.157746	train's f1: 0.996177	val's binary_logloss: 0.299613	val's f1: 0.929204
[98]	train's binary_logloss: 0.155958	train's f1: 0.996725	val's binary_logloss: 0.29808	val's f1: 0.929204
[99]	train's binary_logloss: 0.153967	train's f1: 0.997272	val's binary_logloss: 0.295956	val's f1: 0.929204
[100]	train's binary_logloss: 0.152095	train's f1: 0.997272	val's binary_logloss: 0.294409	val's f1: 0.933333
[101]	train's binary_logloss: 0.150328	train's f1: 0.997819	val's binary_logloss: 0.293185	val's f1: 0.929204
[102]	train's binar

[181]	train's binary_logloss: 0.0603297	train's f1: 1	val's binary_logloss: 0.227492	val's f1: 0.955752
[182]	train's binary_logloss: 0.0596299	train's f1: 1	val's binary_logloss: 0.22692	val's f1: 0.955752
[183]	train's binary_logloss: 0.0589399	train's f1: 1	val's binary_logloss: 0.22622	val's f1: 0.96
[184]	train's binary_logloss: 0.0582764	train's f1: 1	val's binary_logloss: 0.225554	val's f1: 0.96
[185]	train's binary_logloss: 0.0576253	train's f1: 1	val's binary_logloss: 0.224294	val's f1: 0.96
[186]	train's binary_logloss: 0.056996	train's f1: 1	val's binary_logloss: 0.223665	val's f1: 0.96
[187]	train's binary_logloss: 0.0563673	train's f1: 1	val's binary_logloss: 0.223016	val's f1: 0.96
[188]	train's binary_logloss: 0.0557075	train's f1: 1	val's binary_logloss: 0.222968	val's f1: 0.96
[189]	train's binary_logloss: 0.0550839	train's f1: 1	val's binary_logloss: 0.223047	val's f1: 0.955752
[190]	train's binary_logloss: 0.0545077	train's f1: 1	val's binary_logloss: 0.222175	val's 

[271]	train's binary_logloss: 0.0231791	train's f1: 1	val's binary_logloss: 0.194677	val's f1: 0.955752
[272]	train's binary_logloss: 0.022924	train's f1: 1	val's binary_logloss: 0.194206	val's f1: 0.955752
[273]	train's binary_logloss: 0.0226714	train's f1: 1	val's binary_logloss: 0.193714	val's f1: 0.955752
[274]	train's binary_logloss: 0.022437	train's f1: 1	val's binary_logloss: 0.193697	val's f1: 0.955752
[275]	train's binary_logloss: 0.0222112	train's f1: 1	val's binary_logloss: 0.193421	val's f1: 0.955752
[276]	train's binary_logloss: 0.021989	train's f1: 1	val's binary_logloss: 0.1929	val's f1: 0.955752
[277]	train's binary_logloss: 0.0217513	train's f1: 1	val's binary_logloss: 0.192306	val's f1: 0.955752
[278]	train's binary_logloss: 0.0215509	train's f1: 1	val's binary_logloss: 0.191354	val's f1: 0.955752
[279]	train's binary_logloss: 0.0213448	train's f1: 1	val's binary_logloss: 0.191303	val's f1: 0.955752
[280]	train's binary_logloss: 0.0211168	train's f1: 1	val's binary_lo

[363]	train's binary_logloss: 0.00886867	train's f1: 1	val's binary_logloss: 0.17607	val's f1: 0.951111
[364]	train's binary_logloss: 0.00877095	train's f1: 1	val's binary_logloss: 0.176369	val's f1: 0.951111
[365]	train's binary_logloss: 0.0086872	train's f1: 1	val's binary_logloss: 0.17635	val's f1: 0.951111
[366]	train's binary_logloss: 0.0086033	train's f1: 1	val's binary_logloss: 0.176169	val's f1: 0.951111
[367]	train's binary_logloss: 0.00850737	train's f1: 1	val's binary_logloss: 0.176129	val's f1: 0.951111
[368]	train's binary_logloss: 0.00842401	train's f1: 1	val's binary_logloss: 0.176108	val's f1: 0.951111
[369]	train's binary_logloss: 0.00834555	train's f1: 1	val's binary_logloss: 0.175918	val's f1: 0.951111
[370]	train's binary_logloss: 0.00825722	train's f1: 1	val's binary_logloss: 0.175315	val's f1: 0.951111
[371]	train's binary_logloss: 0.00817079	train's f1: 1	val's binary_logloss: 0.175203	val's f1: 0.951111
[372]	train's binary_logloss: 0.00808625	train's f1: 1	val'

...

[3642]	train's binary_logloss: 1.90852e-06	train's f1: 1	val's binary_logloss: 0.245154	val's f1: 0.955357
[3643]	train's binary_logloss: 1.90823e-06	train's f1: 1	val's binary_logloss: 0.245119	val's f1: 0.955357
[3644]	train's binary_logloss: 1.90791e-06	train's f1: 1	val's binary_logloss: 0.245154	val's f1: 0.955357
[3645]	train's binary_logloss: 1.90747e-06	train's f1: 1	val's binary_logloss: 0.245151	val's f1: 0.955357
[3646]	train's binary_logloss: 1.90717e-06	train's f1: 1	val's binary_logloss: 0.245167	val's f1: 0.955357
[3647]	train's binary_logloss: 1.9068e-06	train's f1: 1	val's binary_logloss: 0.24507	val's f1: 0.955357
[3648]	train's binary_logloss: 1.90648e-06	train's f1: 1	val's binary_logloss: 0.245045	val's f1: 0.955357
[3649]	train's binary_logloss: 1.90639e-06	train's f1: 1	val's binary_logloss: 0.245032	val's f1: 0.955357
[3650]	train's binary_logloss: 1.9059e-06	train's f1: 1	val's binary_logloss: 0.245078	val's f1: 0.955357
[3651]	train's binary_logloss: 1.90553e-

[3730]	train's binary_logloss: 1.87749e-06	train's f1: 1	val's binary_logloss: 0.245521	val's f1: 0.955357
[3731]	train's binary_logloss: 1.87714e-06	train's f1: 1	val's binary_logloss: 0.245549	val's f1: 0.955357
[3732]	train's binary_logloss: 1.87681e-06	train's f1: 1	val's binary_logloss: 0.245581	val's f1: 0.955357
[3733]	train's binary_logloss: 1.87653e-06	train's f1: 1	val's binary_logloss: 0.245629	val's f1: 0.955357
[3734]	train's binary_logloss: 1.87619e-06	train's f1: 1	val's binary_logloss: 0.245662	val's f1: 0.955357
[3735]	train's binary_logloss: 1.87582e-06	train's f1: 1	val's binary_logloss: 0.245669	val's f1: 0.955357
[3736]	train's binary_logloss: 1.87573e-06	train's f1: 1	val's binary_logloss: 0.245669	val's f1: 0.955357
[3737]	train's binary_logloss: 1.87565e-06	train's f1: 1	val's binary_logloss: 0.245675	val's f1: 0.955357
[3738]	train's binary_logloss: 1.87526e-06	train's f1: 1	val's binary_logloss: 0.24566	val's f1: 0.955357
[3739]	train's binary_logloss: 1.87496

[3820]	train's binary_logloss: 1.85018e-06	train's f1: 1	val's binary_logloss: 0.246321	val's f1: 0.955357
[3821]	train's binary_logloss: 1.84975e-06	train's f1: 1	val's binary_logloss: 0.246338	val's f1: 0.955357
[3822]	train's binary_logloss: 1.84967e-06	train's f1: 1	val's binary_logloss: 0.246344	val's f1: 0.955357
[3823]	train's binary_logloss: 1.84938e-06	train's f1: 1	val's binary_logloss: 0.24636	val's f1: 0.955357
[3824]	train's binary_logloss: 1.84904e-06	train's f1: 1	val's binary_logloss: 0.246267	val's f1: 0.955357
[3825]	train's binary_logloss: 1.84896e-06	train's f1: 1	val's binary_logloss: 0.246299	val's f1: 0.955357
[3826]	train's binary_logloss: 1.84862e-06	train's f1: 1	val's binary_logloss: 0.246309	val's f1: 0.955357
[3827]	train's binary_logloss: 1.84828e-06	train's f1: 1	val's binary_logloss: 0.246334	val's f1: 0.955357
[3828]	train's binary_logloss: 1.84776e-06	train's f1: 1	val's binary_logloss: 0.246275	val's f1: 0.955357
[3829]	train's binary_logloss: 1.84749

[3906]	train's binary_logloss: 1.82449e-06	train's f1: 1	val's binary_logloss: 0.246907	val's f1: 0.955357
[3907]	train's binary_logloss: 1.8242e-06	train's f1: 1	val's binary_logloss: 0.246918	val's f1: 0.955357
[3908]	train's binary_logloss: 1.82386e-06	train's f1: 1	val's binary_logloss: 0.246959	val's f1: 0.955357
[3909]	train's binary_logloss: 1.82347e-06	train's f1: 1	val's binary_logloss: 0.246988	val's f1: 0.955357
[3910]	train's binary_logloss: 1.82339e-06	train's f1: 1	val's binary_logloss: 0.246955	val's f1: 0.955357
[3911]	train's binary_logloss: 1.82307e-06	train's f1: 1	val's binary_logloss: 0.246949	val's f1: 0.955357
[3912]	train's binary_logloss: 1.82299e-06	train's f1: 1	val's binary_logloss: 0.246936	val's f1: 0.955357
[3913]	train's binary_logloss: 1.82262e-06	train's f1: 1	val's binary_logloss: 0.246955	val's f1: 0.955357
[3914]	train's binary_logloss: 1.82226e-06	train's f1: 1	val's binary_logloss: 0.246943	val's f1: 0.955357
[3915]	train's binary_logloss: 1.82218

[3994]	train's binary_logloss: 1.79931e-06	train's f1: 1	val's binary_logloss: 0.247497	val's f1: 0.955357
[3995]	train's binary_logloss: 1.79923e-06	train's f1: 1	val's binary_logloss: 0.247488	val's f1: 0.955357
[3996]	train's binary_logloss: 1.79895e-06	train's f1: 1	val's binary_logloss: 0.247439	val's f1: 0.955357
[3997]	train's binary_logloss: 1.79869e-06	train's f1: 1	val's binary_logloss: 0.247515	val's f1: 0.955357
[3998]	train's binary_logloss: 1.79838e-06	train's f1: 1	val's binary_logloss: 0.247504	val's f1: 0.955357
[3999]	train's binary_logloss: 1.79804e-06	train's f1: 1	val's binary_logloss: 0.247453	val's f1: 0.955357
[4000]	train's binary_logloss: 1.79796e-06	train's f1: 1	val's binary_logloss: 0.24748	val's f1: 0.955357


In [250]:
nhek_lgb_pred_merged = nhek_lgb_merged.predict(nhek_merged_test_x,num_iteration=nhek_lgb_merged.best_iteration)
f1_score(nhek_merged_test_y,prob2label(nhek_lgb_pred_merged))

0.9236363636363637

## SVM

In [299]:
k562_svm_merged = svm(k562_merged_train_x,k562_merged_train_y,None,None)
imr90_svm_merged = svm(imr90_merged_train_x,imr90_merged_train_y,None,None)
gm12878_svm_merged = svm(gm12878_merged_train_x,gm12878_merged_train_y,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [300]:
huvec_svm_merged = svm(huvec_merged_train_x,huvec_merged_train_y,None,None)
nhek_svm_merged = svm(nhek_merged_train_x,nhek_merged_train_y,None,None)
helas3_svm_merged = svm(helas3_merged_train_x,helas3_merged_train_y,None,None)

/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)
/opt/current-env/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:931: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  "the number of iterations.", ConvergenceWarning)


In [301]:
k562_svm_pred_merged = k562_svm_merged.predict(k562_merged_test_x)
f1_score(k562_merged_test_y,k562_svm_pred_merged)

0.6568848758465011

In [302]:
imr90_svm_pred_merged = imr90_svm_merged.predict(imr90_merged_test_x)
f1_score(imr90_merged_test_y,imr90_svm_pred_merged)

0.6271186440677966

In [303]:
gm12878_svm_pred_merged = gm12878_svm_merged.predict(gm12878_merged_test_x)
f1_score(gm12878_merged_test_y,gm12878_svm_pred_merged)

0.6995594713656387

In [304]:
huvec_svm_pred_merged = huvec_svm_merged.predict(huvec_merged_test_x)
f1_score(huvec_merged_test_y,huvec_svm_pred_merged)

0.6243093922651933

In [305]:
nhek_svm_pred_merged = nhek_svm_merged.predict(nhek_merged_test_x)
f1_score(nhek_merged_test_y,nhek_svm_pred_merged)

0.598326359832636

## AdaBboost

In [306]:
k562_ada_merged = adaboost(k562_merged_train_x,k562_merged_train_y,None,None)
imr90_ada_merged = adaboost(imr90_merged_train_x,imr90_merged_train_y,None,None)
gm12878_ada_merged = adaboost(gm12878_merged_train_x,gm12878_merged_train_y,None,None)

In [307]:
huvec_ada_merged = adaboost(huvec_merged_train_x,huvec_merged_train_y,None,None)
nhek_ada_merged = adaboost(nhek_merged_train_x,nhek_merged_train_y,None,None)
helas3_ada_merged = adaboost(helas3_merged_train_x,helas3_merged_train_y,None,None)

In [308]:
k562_ada_pred_merged = k562_ada_merged.predict(k562_merged_test_x)
f1_score(k562_merged_test_y,k562_ada_pred_merged)

0.8339222614840989

In [309]:
imr90_ada_pred_merged = imr90_ada_merged.predict(imr90_merged_test_x)
f1_score(imr90_merged_test_y,imr90_ada_pred_merged)

0.7588932806324111

In [310]:
gm12878_ada_pred_merged = gm12878_ada_merged.predict(gm12878_merged_test_x)
f1_score(gm12878_merged_test_y,gm12878_ada_pred_merged)

0.7845993756503642

In [311]:
huvec_ada_pred_merged = huvec_ada_merged.predict(huvec_merged_test_x)
f1_score(huvec_merged_test_y,huvec_ada_pred_merged)

0.7735537190082645

In [312]:
nhek_ada_pred_merged = nhek_ada_merged.predict(nhek_merged_test_x)
f1_score(nhek_merged_test_y,nhek_ada_pred_merged)

0.857638888888889

In [313]:
helas3_ada_pred_merged = helas3_ada_merged.predict(helas3_merged_test_x)
f1_score(helas3_merged_test_y,helas3_ada_pred_merged)

0.8368794326241136

# Save Model and Data

## Save Model

In [314]:
k562_lgb_merged.save_model('./model/LGB/k562_merged_lgb.txt', num_iteration=k562_lgb_merged.best_iteration)
imr90_lgb_merged.save_model('./model/LGB/img90_merged_lgb.txt', num_iteration=imr90_lgb_merged.best_iteration)
gm12878_lgb_merged.save_model('./model/LGB/gm12878_merged_lgb.txt', num_iteration=gm12878_lgb_merged.best_iteration)

In [315]:
huvec_lgb_merged.save_model('./model/LGB/huvec_merged_lgb.txt', num_iteration=huvec_lgb_merged.best_iteration)
nhek_lgb_merged.save_model('./model/LGB/nhek_merged_lgb.txt', num_iteration=nhek_lgb_merged.best_iteration)
helas3_lgb_merged.save_model('./model/LGB/helas3_merged_lgb.txt', num_iteration=helas3_lgb_merged.best_iteration)

In [316]:
joblib.dump(k562_svm_merged,'./model/RF/k562_svm_merged.model')
joblib.dump(imr90_svm_merged,'./model/RF/imr90_svm_merged.model')
joblib.dump(gm12878_svm_merged,'./model/RF/gm12878_svm_merged.model')

['./model/RF/gm12878_svm_merged.model']

In [317]:
joblib.dump(huvec_svm_merged,'./model/RF/huvec_svm_merged.model')
joblib.dump(nhek_svm_merged,'./model/RF/nhek_svm_merged.model')
joblib.dump(helas3_svm_merged,'./model/RF/helas3_svm_merged.model')

['./model/RF/helas3_svm_merged.model']

In [318]:
joblib.dump(k562_ada_merged,'./model/Adaboost/k562_ada_merged.model')
joblib.dump(imr90_ada_merged,'./model/Adaboost/imr90_ada_merged.model')
joblib.dump(gm12878_ada_merged,'./model/Adaboost/gm12878_ada_merged.model')

['./model/Adaboost/gm12878_ada_merged.model']

In [319]:
joblib.dump(huvec_ada_merged,'./model/Adaboost/huvec_ada_merged.model')
joblib.dump(nhek_ada_merged,'./model/Adaboost/nhek_ada_merged.model')
joblib.dump(helas3_ada_merged,'./model/Adaboost/helas3_ada_merged.model')

['./model/Adaboost/helas3_ada_merged.model']

## Save Data